In [1]:
#@title init
import io
import os, time
import pickle
import shutil
import numpy as np
# os.environ['PYTORCH_ENABLE_MPS_FALLBACK'] = '1'
import torch
import torch.nn.functional as F
import sys
import shutil
import torchvision.transforms.functional as TF
from torchvision.transforms import Compose, Resize, ToTensor, Normalize
from sklearn.model_selection import train_test_split
import csv
import numpy as np
import pandas as pd
import PIL.Image
from PIL import Image, ImageDraw
import IPython.display
import matplotlib.pyplot as plt
from pathlib import Path
from tqdm import tqdm
from ipywidgets import interact, Button, FloatSlider, Layout
import sys

import torch
import torch.nn.functional as F
import requests
import torchvision.transforms as transforms
import torchvision.transforms.functional as TF
import copy
import unicodedata
import re
from PIL import Image
from tqdm.notebook import tqdm
from torchvision.transforms import Compose, Resize, ToTensor, Normalize
from IPython.display import display
from einops import rearrange
from time import perf_counter
# !pip install einops plotly tqdm scikit-learn x_transformers 
# df = pd.read_hdf('coords_wlosses.h5')





df = pd.read_csv('/Users/adamsobieszek/PycharmProjects/psychGAN/content/coords_wlosses.csv')

In [2]:
import torch
import torch.nn as nn
import numpy as np
import pandas as pd
from pathlib import Path
from torchvision.transforms import Compose, Resize
import torchvision.transforms.functional as TF
from typing import List, Dict, Union, Tuple
%cd /Users/adamsobieszek/PycharmProjects/_manipy/
# Assuming the existence of these from a library like torchdyn
os.environ['PATH'] = os.environ['PATH']+':/opt/anaconda3/envs/manip311/'
print(os.environ['PATH'])


from manipy.models.flow_models import VectorFieldTransformer, RatingODE
from manipy.models.layers import EnsembleRegressor, MeanRegressor
from manipy.models.rating_models import AlphaBetaRegressor

final_models_path = "/Users/adamsobieszek/PycharmProjects/psychGAN/content/"


import locale

locale.getpreferredencoding = lambda: "UTF-8"
device= "cuda" if torch.cuda.is_available() else "mps" if torch.backends.mps.is_available() else "cpu"




class From100To1(nn.Module):
  def __init__(self, model):
     super().__init__()
     self.model = model

  def forward(self, x):
     return self.model(x)/100

# del control_models
if not "control_models" in dir():
  # if not os.path.exists("final_models.zip"):
  #   !gdown 1pPjOd-mx-d-vOw1QR_lpJoJmLAGdkI3W
  #   !unzip final_models.zip
  #   !unzip final_models.zip
  control_names = ['trustworthy','dominant', 'gender', 'age', 'white']
  control_models = [EnsembleRegressor([MeanRegressor(512,1) for _ in range(8)], model_kwargs={}).to(device) for label in control_names]
  for m,l in zip(control_models,control_names):
    m.load_state_dict(torch.load(f"{final_models_path}/final_models/ensemble_{l}.pt", map_location=torch.device("mps")))
    m.eval()
  ALL_MODELS = {**{l:From100To1(m) for l,m in zip(control_names,control_models)}}


# G, face_w, device = setup_stylegan()
# G, face_w, device = setup_stylegan()
sys.path.append('/Users/adamsobieszek/PycharmProjects/_manipy')
from mapping_network import *

DEVICE = torch.device('mps')
device = torch.device('mps')

mapping = MappingNetwork(512,0,512,18).to(DEVICE)
mapping.load_state_dict(torch.load("/Users/adamsobieszek/PycharmProjects/_manipy/mapping_network/map (1).pt", weights_only=True, map_location=DEVICE))
class MockGenerator(nn.Module):
    mapping = mapping


G = MockGenerator().eval().to(DEVICE)
G = torch.compile(G, )
start_time = time.time()
print(G.mapping.w_avg.shape)
all_z = torch.randn([1, G.mapping.z_dim], device=device)
face_w = G.mapping(all_z, None, truncation_psi=0.5)
dim = "trustworthy"


w_avg = G.mapping.w_avg

ALL_MODELS['trustworthy'](w_avg.reshape(1,512).to(device))



sys.path.append('/Users/adamsobieszek/PycharmProjects/psychGAN/content/psychGAN/stylegan3')
with open('/Users/adamsobieszek/PycharmProjects/psychGAN/stylegan2-ffhq-1024x1024.pkl', 'rb') as fp:
    G = pickle.load(fp)['G_ema'].to(device)

# Compute the average latent vector
all_z = torch.randn([1, G.mapping.z_dim], device=device)
face_w = G.mapping(all_z, None, truncation_psi=0.5)


/Users/adamsobieszek/PycharmProjects/_manipy
/opt/anaconda3/envs/manip311/bin:/Users/adamsobieszek/google-cloud-sdk/bin:/opt/homebrew/bin:/opt/homebrew/sbin:/opt/anaconda3/envs/manip311/bin:/opt/anaconda3/condabin:/usr/local/bin:/System/Cryptexes/App/usr/bin:/usr/bin:/bin:/usr/sbin:/sbin:/var/run/com.apple.security.cryptexd/codex.system/bootstrap/usr/local/bin:/var/run/com.apple.security.cryptexd/codex.system/bootstrap/usr/bin:/var/run/com.apple.security.cryptexd/codex.system/bootstrap/usr/appleinternal/bin:/usr/local/MacGPG2/bin:/Library/TeX/texbin:/opt/anaconda3/envs/manip311/
torch.Size([512])


# Attractive

.

.

.

.

.

.



















In [3]:
def pad_list(l, max_len):
    return l[:max_len] + [np.nan] * (max_len - len(l[:max_len]))
    
def prepare_data2(config: dict, verbose=False):
    xs, ys = photo_to_coords, dim_to_photo_to_ratings[config['data']['attribute_dim']]
    imgs = set(ys.keys()).intersection(set(xs.keys()))-set('638.jpg')
    X = torch.stack([xs[k] for k in imgs]).to(DEVICE, DTYPE)
    max_len = int(max(len(ys[k]) for k in imgs) * config['data'].get('rating_oversampling_factor', 1.0))
    y = torch.tensor([pad_list(ys[k], max_len) for k in imgs], device=DEVICE, dtype=DTYPE)
    n = y.shape[1] - y.isnan().sum(dim=1)
    sample_size_weights = (n.reshape(-1)) 
    sample_size_weights = sample_size_weights / sample_size_weights.sum()*len(n)
    from sklearn.neighbors import KernelDensity
    kde = KernelDensity(kernel='gaussian', bandwidth=.5).fit(torch.nanmean(y, dim=1).cpu().numpy().reshape(-1,1))
    log_dens = kde.score_samples(torch.nanmean(y, dim=1).cpu().numpy().reshape(-1,1))
    weights = (np.exp(-log_dens))
    weights = torch.tensor(weights/np.sum(weights)*len(n), device=DEVICE, dtype=DTYPE)

    # pressure = torch.sigmoid(torch.nanmean(y, dim=1, keepdim=True))*(1-torch.sigmoid(torch.nanmean(y, dim=1, keepdim=True)))
    # pressure = pressure / pressure.sum()*len(n)
    # weights = sample_size_weights*pressure
    # weights = weights**2
    # weights = weights / weights.sum()*len(n)
    return X, y, weights

psychGAN_path = "/Users/adamsobieszek/PycharmProjects/psychGAN/"
photo_to_coords = np.load(psychGAN_path+"photo_to_coords.npy", allow_pickle=True)
dim_to_photo_to_ratings = np.load(psychGAN_path+"dim_to_photo_to_ratings.npy", allow_pickle=True)





In [4]:
#@title TUTAJ SIĘ ZAPISUJA INPUTY
import torch
import numpy as np
import matplotlib.pyplot as plt
from torchvision.transforms import Compose, Resize
import torchvision.transforms.functional as TF
from ipywidgets import interact, Button
from IPython.display import display

# This is a placeholder for the actual models and data preparation functions
# that would be defined in a complete notebook environment.
# In a real scenario, ensure that G, model, control_models, device,
# directions, CIs, face_w, etc., are properly loaded and initialized.
# For example:
# from models import AlphaBetaRegressor, EnsembleRegressor, RatingODE
# from data_utils import prepare_data
# from torchdiffeq import odeint_adjoint as NeuralODE
# G, model, device, control_models = None, None, torch.device('cpu'), [None]*3
# directions, CIs = {}, {}
# face_w = torch.randn(1, 512)
# dim = "attractive"

@torch.no_grad()
def manipulation_showcase(coeff_vec):
        """
        Generates and displays facial manipulations based on two different vectors.

        This function takes a latent vector representing a face and manipulates it
        in positive and negative directions using a standard direction vector and a
        Covariance-Informed (CI) vector. It then generates and plots the resulting
        images in a 2x3 grid for comparison.

        Args:
            coeff_vec (float): The coefficient to scale the manipulation vectors.
        """
        # try:
        global G, model, device, directions, CIs, face_w

        # Prepare original latent vector by tiling it for all 18 layers
        original_face_w = torch.stack([face_w.clone().view(1, 512)] * 18, dim=1)
        w_orig_base = original_face_w[:, 0]

        # Get and normalize the primary direction vector
        direction = -directions[dim].to(device)
        direction /= direction.norm()

        # Get and normalize the Covariance-Informed (CI) vector
        ci = -CIs[dim].to(device).view(direction.shape)
        ci /= ci.norm()
        # # --- Orthogonal Projection Step ---
        # # Project the direction vector to be orthogonal to age and gender to
        # # disentangle the attribute manipulation from those characteristics.
        # with torch.enable_grad():
        #   w = w_orig_base.requires_grad_(True)
        #   ages = control_models[2](w)
        #   ages.sum().backward()
        #   age_grad = w.grad.detach()
        #   age_grad_unit = age_grad.view(-1) / age_grad.norm()
        #   direction -= torch.dot(direction.view(-1), age_grad_unit) * age_grad_unit
        #   ci -= torch.dot(ci.view(-1), age_grad_unit.view(-1)) * age_grad_unit

        #   w.grad = None
        #   w = w.requires_grad_(True)
        #   ages = control_models[1](w)
        #   ages.sum().backward()
        #   gender_grad = w.grad.detach()

        #   gender_grad_unit = gender_grad.view(-1) / gender_grad.norm()
        #   direction -= torch.dot(direction.view(-1), gender_grad_unit.view(-1)) * gender_grad_unit
        #   ci -= torch.dot(ci.view(-1), gender_grad_unit.view(-1)) * gender_grad_unit

        #   # 5. Re-normalize the final projected direction vector
        #   direction /= direction.norm()
        #   ci /= ci.norm()
        #   # --- End of Projection Step ---
        # with torch.enable_grad():
        #   w = (w_orig_base + direction/2).detach().requires_grad_(True)
        #   ages = control_models[2](w)
        #   ages.sum().backward()
        #   age_grad = w.grad.detach()
        #   age_grad_unit = age_grad.view(-1) / age_grad.norm()
        #   direction -= torch.dot(direction.view(-1), age_grad_unit) * age_grad_unit
        #   ci -= torch.dot(ci.view(-1), age_grad_unit.view(-1)) * age_grad_unit

        #   w.grad = None
        #   w = w.requires_grad_(True)
        #   ages = control_models[1](w)
        #   ages.sum().backward()
        #   gender_grad = w.grad.detach()

        #   gender_grad_unit = gender_grad.view(-1) / gender_grad.norm()
        #   direction -= torch.dot(direction.view(-1), gender_grad_unit.view(-1)) * gender_grad_unit
        #   ci -= torch.dot(ci.view(-1), gender_grad_unit.view(-1)) * gender_grad_unit

        #   # 5. Re-normalize the final projected direction vector
        #   direction /= direction.norm()
        #   ci /= ci.norm()
        #   # --- End of Projection Step ---
        # with torch.enable_grad():
        #   w = (w_orig_base + ci/2).detach().requires_grad_(True)
        #   ages = control_models[2](w)
        #   ages.sum().backward()
        #   age_grad = w.grad.detach()
        #   age_grad_unit = age_grad.view(-1) / age_grad.norm()
        #   direction -= torch.dot(direction.view(-1), age_grad_unit) * age_grad_unit
        #   ci -= torch.dot(ci.view(-1), age_grad_unit.view(-1)) * age_grad_unit

        #   w.grad = None
        #   w = w.requires_grad_(True)
        #   ages = control_models[1](w)
        #   ages.sum().backward()
        #   gender_grad = w.grad.detach()

        #   gender_grad_unit = gender_grad.view(-1) / gender_grad.norm()
        #   direction -= torch.dot(direction.view(-1), gender_grad_unit.view(-1)) * gender_grad_unit
        #   ci -= torch.dot(ci.view(-1), gender_grad_unit.view(-1)) * gender_grad_unit

        #   # 5. Re-normalize the final projected direction vector
        #   direction /= direction.norm()
        #   ci /= ci.norm()
        #   # --- End of Projection Step ---

        # Calculate positive and negative displacements for both vectors
        pos_vector_direction = direction * coeff_vec
        neg_vector_direction = direction * -coeff_vec
        pos_ci_direction = ci * coeff_vec
        neg_ci_direction = ci * -coeff_vec

        # Create latent codes for all 5 variations (original + 4 manipulations)
        w_orig_base = original_face_w[:, 0]
        neg_vector_w = torch.stack([w_orig_base + neg_vector_direction] * 18, dim=1)
        pos_vector_w = torch.stack([w_orig_base + pos_vector_direction] * 18, dim=1)
        neg_ci_w = torch.stack([w_orig_base + neg_ci_direction] * 18, dim=1)
        pos_ci_w = torch.stack([w_orig_base + pos_ci_direction] * 18, dim=1)

        # Stack all latent vectors for batch processing
        stacked_w = torch.stack([
            neg_vector_w, pos_vector_w, original_face_w, neg_ci_w, pos_ci_w
        ])

        # Generate all images at once
        images = G.synthesis(stacked_w.view(-1, 18, 512)).cpu()

        # Define image post-processing transform
        tf = Compose([
            Resize(512),
            lambda x: torch.clamp((x + 1) / 2, min=0, max=1),
        ])

        # Convert tensors to PIL images
        images_pil = [TF.to_pil_image(tf(img)) for img in images]
        img_neg_vec, img_pos_vec, img_orig, img_neg_ci, img_pos_ci = images_pil

        # Calculate beauty ratings and age for all images
        ratings = model(stacked_w[:, 0, 0], 'mean').cpu().numpy().flatten()
        ages = control_models[2](stacked_w[:, 0, 0]).cpu().numpy().flatten()
        (mean_neg_vec, mean_pos_vec, mean_original, mean_neg_ci, mean_pos_ci) = ratings
        (age_neg_vec, age_pos_vec, age_original, age_neg_ci, age_pos_ci) = ages



        # Create a 2x3 subplot for displaying the results
        fig, ax = plt.subplots(2, 3, figsize=(21, 14))

        # --- Top Row: Standard Vector Manipulation ---
        CAPTION = False
        vec_dist = f"Distance: {(w_orig_base - neg_vector_w[:, 0]).norm():.2f}"

        # Plot 1: Negative Vector Manipulation
        ax[0, 0].imshow(img_neg_vec)
        ax[0, 0].set_title("Direction (-)")
        def caption(ax, text):
            if CAPTION:
                ax.text(0.5, 0.05, text,
                        ha='center', va='center', transform=ax.transAxes, color='white', fontsize=14,
                        bbox=dict(facecolor='black', alpha=0.7))
        
        caption(ax[0, 0], f'ΔRating: {(mean_neg_vec - mean_original) * 100:.2f}\nΔAge: {(age_neg_vec - age_original):.2f}\n{vec_dist}')
        ax[0, 0].axis('off')

        # Plot 2: Original Image
        ax[0, 1].imshow(img_orig)
        ax[0, 1].set_title("Original Image")
        caption(ax[0, 1], f'Rating: {mean_original * 100:.2f}\nAge: {age_original:.2f}')
        ax[0, 1].axis('off')

        # Plot 3: Positive Vector Manipulation
        ax[0, 2].imshow(img_pos_vec)
        ax[0, 2].set_title("Direction (+)")
        caption(ax[0, 2], f'ΔRating: {(mean_pos_vec - mean_original) * 100:.2f}\nΔAge: {(age_pos_vec - age_original):.2f}\n{vec_dist}')
        ax[0, 2].axis('off')

        # --- Bottom Row: CI Vector Manipulation ---

        # Plot 4: Negative CI Manipulation
        ax[1, 0].imshow(img_neg_ci)
        ax[1, 0].set_title("CI (-)")
        ci_dist = f"Distance: {(w_orig_base - neg_ci_w[:, 0]).norm():.2f}"
        caption(ax[1, 0], f'ΔRating: {(mean_neg_ci - mean_original) * 100:.2f}\nΔAge: {(age_neg_ci - age_original):.2f}\n{ci_dist}')
        ax[1, 0].axis('off')

        # Plot 5: Original Image (repeated for context)
        ax[1, 1].imshow(img_orig)
        ax[1, 1].set_title("Original Image")
        caption(ax[1, 1], f'Rating: {mean_original * 100:.2f}\nAge: {age_original:.2f}')
        ax[1, 1].axis('off')

        # Plot 6: Positive CI Manipulation
        ax[1, 2].imshow(img_pos_ci)
        ax[1, 2].set_title("CI (+)")
        caption(ax[1, 2], f'ΔRating: {(mean_pos_ci - mean_original) * 100:.2f}\nΔAge: {(age_pos_ci - age_original):.2f}\n{ci_dist}')
        ax[1, 2].axis('off')

        plt.tight_layout()
        plt.show()
    # except Exception as ex:
    #     print(f"An error occurred: {ex}")
    #     return

def on_button_clicked(b):
    """Handles the face change button click event."""
    global traj_all, face_w, i_w
    # if i_w % 50 == 0:
    #     print("Generating new set of faces...")
    #     regen()
    i = i_w % 50
    # face_w = traj_all[:, i:i+1]
    face_w = init_w
    i_w += 1
    try:
        interactive_display.widget.update()
    except Exception as e:
        print(f"Could not update widget: {e}")

def grad(w, model, kwargs={}):
    """Computes the gradient of a model's output with respect to the input."""
    w = w.detach().clone().requires_grad_(True)
    output = model(w, **kwargs)
    torch.sum(output).backward()
    return w.grad.detach()


def regen():
    """Resets and regenerates the base face and trajectory."""
    global face_w, i_w, traj, node, traj_all, max_rating
    with torch.no_grad():
        # i_w = 0 # Uncomment to reset face counter
        # face_w = G.mapping.w_avg # Start from the average face
        traj = None
        # Example of trajectory generation (requires pre-configured 'node' and 'max_rating')
        # traj_all = node.trajectory(
        #     face_w,
        #     t_span=torch.linspace(0, max_rating, 100),
        # )

# --- Main execution block ---
# This block should contain the model loading and setup logic from your notebook.
# It is reproduced here based on the original script's structure.

# Initialize counters and data storage
i_w = 0
dataset = {}
dim = "trustworthy" # or "trustworthy"

# Assuming CONFIG, prepare_data, and necessary model classes are defined
# config = CONFIG.copy()
# config['data']['attribute_dim'] = dim
# X, y = prepare_data(config)
# y = -y

# # Perform PCA and calculate the Covariance-Informed gradient
# from sklearn.decomposition import PCA
# from sklearn.linear_model import LinearRegression
# X_full = sample_w(10000).detach().cpu().numpy()
  #G.mapping.w_avg # Fallback to average face

# Load models
# model_path = "/Users/adamsobieszek/PycharmProjects/psychGAN/"
# models = [AlphaBetaRegressor(dim=512).to(device) for _ in range(8)]
# model_files = [f"{model_path}best_models/model_{dim}_v{3+i}.pt" for i in range(8)]
# for i, m_file in enumerate(model_files):
#     models[i].load_state_dict(torch.load(m_file, map_location=device))
#     models[i].eval()
# model = EnsembleRegressor(models)


In [5]:

from sklearn.ensemble import RandomForestClassifier

class ZSpaceEvolutionarySampler:
    """
    Finds a broad distribution of Z-space vectors and trains a surrogate model of the valid subspace.
    Uses boundary-seeking elites and tangent space covariance projection.
    """
    def __init__(self, target_filters: Dict, config: Dict, models: Dict, G: torch.nn.Module, device: torch.device):
        self.config = config
        self.models = {name: model.to(device) for name, model in models.items()}
        self.G = G.to(device)
        self.device = device
        self.z_dim = self.G.mapping.z_dim
        self.target_bin = self._parse_filters(target_filters)
        self.mean = np.zeros(self.z_dim, dtype=np.float32)
        self.cov = np.eye(self.z_dim, dtype=np.float32) * self.config.get('initial_variance', 1.0)
        self.visualizer = LiveZSpaceVisualizer() if self.config.get('visualize_live', False) else None
        self.unconstrained_w_std = None
        # Initialize the surrogate model (Random Forest)
        self.rf_classifier = RandomForestClassifier(
            n_estimators=50, max_depth=10, random_state=42, n_jobs=-1
        )
        self.is_rf_trained = False

    def _parse_filters(self, filters: Dict) -> List[Dict]:
        # (Implementation unchanged)
        target = []
        print("Parsing target bin from range-based filters...")
        for var, condition_dict in filters.items():
            if 'range' not in condition_dict: raise ValueError(f"Filter for '{var}' must contain a 'range' key.")
            target.append({'var': var, 'range': condition_dict['range']})
        print(f"Target bin defined as: {target}")
        return target

    @torch.no_grad()
    def _calculate_fitness(self, z_batch_gpu: torch.Tensor) -> Tuple[np.ndarray, torch.Tensor, torch.Tensor]:
        # (Implementation unchanged)
        w_batch = self.G.mapping(z_batch_gpu, None)[:, 0]
        bin_loss = 0
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            target_val = low if high == np.inf else (high if low == -np.inf else (low + high) / 2.0)
            bin_loss += (preds - target_val)**2
        final_mask = torch.full((w_batch.shape[0],), True, device=self.device)
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            final_mask &= (preds >= low) & (preds <= high)
        return bin_loss.cpu().numpy(), final_mask, w_batch

    def _calculate_hds(self, z_samples: torch.Tensor) -> float:
        # (Implementation unchanged)
        if z_samples.shape[0] < 2: return 1.0
        z_norm = z_samples / torch.norm(z_samples, p=2, dim=1, keepdim=True)
        sim_matrix = torch.matmul(z_norm, z_norm.T)
        n = sim_matrix.shape[0]
        off_diagonal_elements = torch.triu(sim_matrix, diagonal=1)
        clumpiness = torch.sum(off_diagonal_elements**2) * 2 / (n * (n - 1))
        return (1.0 - torch.sqrt(clumpiness)).cpu().item()

    def run(self) -> Tuple[np.ndarray, RandomForestClassifier]:
        n_to_generate, pop_size = self.config['n_samples_to_generate'], self.config['population_size']
        n_elite = int(pop_size * self.config['elite_fraction'])
        if n_elite < 2: raise ValueError("Elite fraction too small.")

        print("Calculating baseline W-space standard deviation...")
        with torch.no_grad():
            initial_z_std = np.sqrt(self.config.get('initial_variance', 1.0))
            initial_z = torch.randn(pop_size, self.z_dim, device=self.device) * initial_z_std
            _, _, initial_w = self._calculate_fitness(initial_z)
            self.unconstrained_w_std = torch.mean(torch.std(initial_w, dim=0)).cpu().item()
            print(f"Baseline (unconstrained) W-space Std. Dev.: {self.unconstrained_w_std:.4f}")

        print(f"\nStarting evolutionary search...")
        pbar = tqdm(range(self.config['generations']), desc="Initializing...")

        for gen in pbar:
            stable_cov = self.cov + np.eye(self.z_dim, dtype=np.float32) * 1e-6
            z_candidates_cpu = np.random.multivariate_normal(self.mean, stable_cov, size=pop_size).astype(np.float32)
            z_candidates_gpu = torch.from_numpy(z_candidates_cpu).to(self.device, self.dtype)
            
            compliance_fitness, success_mask, w_candidates_gpu = self._calculate_fitness(z_candidates_gpu)
            
            # --- TRAIN RANDOM FOREST SURROGATE ---
            # We train the RF on the normalized vectors, as requested
            z_candidates_norm = z_candidates_cpu / np.linalg.norm(z_candidates_cpu, axis=1, keepdims=True)
            if np.any(success_mask.cpu().numpy()): # Start training once we have positive samples
                self.rf_classifier.fit(z_candidates_norm, success_mask.cpu().numpy())
                self.is_rf_trained = True

            # --- HYBRID ELITE SELECTION ---
            successful_z = z_candidates_cpu[success_mask.cpu().numpy()]
            unsuccessful_z = z_candidates_cpu[~success_mask.cpu().numpy()]
            unsuccessful_fitness = compliance_fitness[~success_mask.cpu().numpy()]
            n_boundary_elites = int(n_elite * self.config['boundary_elite_fraction'])
            n_success_elites = n_elite - n_boundary_elites

            if len(unsuccessful_z) > 0:
                boundary_indices = np.argsort(unsuccessful_fitness)[:int(n_boundary_elites*min(1,(gen+1)/5))]
                elite_boundary = unsuccessful_z[boundary_indices]
            else:
                elite_boundary = np.array([]).reshape(0, self.z_dim); n_success_elites = n_elite

            if len(successful_z) > 0:
                if len(successful_z) <= n_success_elites:
                    elite_success = successful_z
                else: 
                    # --- SPHERICAL MAHALANOBIS DISTANCE ---
                    successful_z_norm = successful_z / np.linalg.norm(successful_z, axis=1, keepdims=True)
                    succ_norm_mean = np.mean(successful_z_norm, axis=0)
                    succ_norm_cov = np.cov(successful_z_norm, rowvar=False)
                    inv_succ_norm_cov = np.linalg.inv(succ_norm_cov + np.eye(self.z_dim) * 1e-6)
                    deltas = successful_z_norm - succ_norm_mean
                    distances = np.sum((deltas @ inv_succ_norm_cov) * deltas, axis=1)
                    elite_indices = np.argsort(distances)[-n_success_elites:]
                    elite_success = successful_z[elite_indices]
            else:
                elite_success = np.array([]).reshape(0, self.z_dim)
            
            elite_z = np.vstack([elite_success, elite_boundary]) if len(elite_success) > 0 and len(elite_boundary) > 0 else (elite_success if len(elite_success) > 0 else elite_boundary)
            if elite_z.shape[0] < 2: pbar.set_description(f"Elite stall ({elite_z.shape[0]})"); continue
            
            # --- COVARIANCE PROJECTION (with corrected timing) ---
            new_mean = np.mean(elite_z, axis=0)
            new_cov = np.cov(elite_z, rowvar=False)#+np.eye(self.z_dim, dtype=np.float32)*1e-4
            lr = self.config['update_learning_rate']
            
            # 1. Update mean first
            self.mean = (1 - lr) * self.mean + lr * new_mean
            
            # 2. Use the NEWLY updated mean for projection
            mean_norm = np.linalg.norm(self.mean)
            if mean_norm > 1e-6:
                mu_hat = self.mean / mean_norm
                proj_matrix = np.eye(self.z_dim) - np.outer(mu_hat, mu_hat)
                projected_cov = proj_matrix @ new_cov @ proj_matrix
            else:
                projected_cov = new_cov # No projection at origin

            # 3. Update covariance using the projected matrix
            self.cov = (1 - lr) * self.cov + lr * projected_cov

            # --- METRICS AND VISUALIZATION ---
            current_success_rate = success_mask.float().mean().cpu().item()
            diversity_score = self._calculate_hds(torch.from_numpy(elite_z).to(self.device, self.dtype))
            successful_w = w_candidates_gpu[success_mask]
            mean_w_std = torch.mean(torch.std(successful_w, dim=0)).cpu().item() if successful_w.shape[0] > 1 else 0.0
            normalized_w_std = mean_w_std / self.unconstrained_w_std if self.unconstrained_w_std > 0 else 0.0
            rf_score = self.rf_classifier.score(z_candidates_norm, success_mask.cpu().numpy()) if self.is_rf_trained else 0.0

            pbar.set_description(f"Elite: {len(elite_success)}S/{len(elite_boundary)}B | RF Acc: {rf_score:.2f}")
            pbar.set_postfix(succ=f"{current_success_rate*100:.1f}%", hds=f"{diversity_score:.3f}", w_std_norm=f"{normalized_w_std:.3f}")

            if self.visualizer:
                self.visualizer.update_plot(self.mean, self.cov, current_success_rate, diversity_score, normalized_w_std, gen)

        print(f"\nEvolution complete. Harvesting final samples...")
        final_stable_cov = self.cov + np.eye(self.z_dim, dtype=np.float32) * 1e-6
        final_candidates_z = np.random.multivariate_normal(self.mean, final_stable_cov, size=int(n_to_generate * 3.0)).astype(np.float32)
        _, final_mask, _ = self._calculate_fitness(torch.from_numpy(final_candidates_z).to(self.device, self.dtype))
        successful_z = final_candidates_z[final_mask.cpu().numpy()][:n_to_generate]
        print(f"Successfully generated and filtered {len(successful_z)} Z vectors.")
        
        return successful_z, self.rf_classifier


# Trustworthy

.

.

.

.

.

.



















In [ ]:



from sklearn.ensemble import RandomForestClassifier

import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
import ipywidgets as widgets
from IPython.display import display
import torch
from tqdm.notebook import tqdm
from typing import List, Dict, Tuple
# The LiveZSpaceVisualizer class is unchanged.
class LiveZSpaceVisualizer:
    def __init__(self, z_dim=512):
        self.z_dim = z_dim
        self.generation_history, self.success_history, self.diversity_history, self.w_std_history = [], [], [], []
        self.fig = go.FigureWidget(make_subplots(
            rows=3, cols=2, specs=[[{"rowspan": 3}, {}], [None, {}], [None, {}]],
            subplot_titles=("Z-Space Distribution", "Success Rate (%)", "Hyperspherical Diversity (HDS)", "Normalized W-Space Std. Dev."),
            column_widths=[0.66, 0.34], vertical_spacing=0.1
        ))
        self._setup_plot()
        display(self.fig)
    def _setup_plot(self):
        for i in range(1, 4): self.fig.add_shape(type="circle", xref="x1", yref="y1", x0=-i, y0=-i, x1=i, y1=i, line_color="grey", line_dash="dot", fillcolor="rgba(0,0,0,0)")
        self.fig.add_trace(go.Scatter(x=[], y=[], fill="toself", fillcolor='rgba(0,191,255,0.3)', line=dict(color='rgba(0,0,0,0)'), name='2σ Covariance'), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='markers', marker=dict(color='red', size=10), name='Search Mean'), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines+markers', name='Success %', line=dict(color='green', width=2)), row=1, col=2)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines+markers', name='Diversity Score', line=dict(color='orange', width=2)), row=2, col=2)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines+markers', name='Normalized W-Std', line=dict(color='blue', width=2)), row=3, col=2)
        self.fig.update_layout(title_text="Live Evolutionary Search Analysis", title_x=0.5, width=2200, height=1050, showlegend=False)
        self.fig.update_xaxes(title_text="Z Dim 0", range=[-5, 5], row=1, col=1); self.fig.update_yaxes(title_text="Z Dim 1", range=[-5, 5], scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Generation", row=1, col=2); self.fig.update_yaxes(title_text="Success Rate (%)", row=1, col=2)
        self.fig.update_xaxes(title_text="Generation", row=2, col=2); self.fig.update_yaxes(title_text="Diversity Score (HDS)", row=2, col=2)
        self.fig.update_xaxes(title_text="Generation", row=3, col=2); self.fig.update_yaxes(title_text="Fraction of Initial Std.", row=3, col=2)
    def update_plot(self, mean_np: np.ndarray, cov_np: np.ndarray, success_rate: float, diversity_score: float, w_std_normalized: float, generation: int):
        self.generation_history.append(generation); self.success_history.append(success_rate * 100); self.diversity_history.append(diversity_score); self.w_std_history.append(w_std_normalized)
        mean_2d, cov_2d = mean_np[:2], cov_np[:2, :2]
        eigenvalues, eigenvectors = np.linalg.eigh(cov_2d); eigenvalues[eigenvalues < 0] = 1e-9
        angle = np.arctan2(eigenvectors[1, 0], eigenvectors[0, 0]); radii = 2 * np.sqrt(eigenvalues)
        t = np.linspace(0, 2 * np.pi, 100); ellipse_x_raw, ellipse_y_raw = radii[0] * np.cos(t), radii[1] * np.sin(t)
        ellipse_x = mean_2d[0] + (ellipse_x_raw * np.cos(angle) - ellipse_y_raw * np.sin(angle)); ellipse_y = mean_2d[1] + (ellipse_x_raw * np.sin(angle) + ellipse_y_raw * np.cos(angle))
        with self.fig.batch_update():
            self.fig.data[0].x, self.fig.data[0].y = ellipse_x, ellipse_y; self.fig.data[1].x, self.fig.data[1].y = [mean_2d[0]], [mean_2d[1]]
            self.fig.data[2].x, self.fig.data[2].y = self.generation_history, self.success_history; self.fig.data[3].x, self.fig.data[3].y = self.generation_history, self.diversity_history
            self.fig.data[4].x, self.fig.data[4].y = self.generation_history, self.w_std_history
# async_zspace_evolution_visualizer_robust.py
"""
Robust asynchronous visualizer using a thread-safe shared state.
Expensive calculations run in a background thread, but the plot update itself
is performed safely on the main Jupyter thread.
"""
from __future__ import annotations
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from IPython.display import display
from concurrent.futures import ThreadPoolExecutor, Future
import threading
from typing import Tuple, Any

import torch
from PIL import Image
from torchvision.transforms import Compose, Resize
import torchvision.transforms.functional as TF

class AsyncZSpaceVisualizer:
    """Non-blocking dashboard using a thread-safe handoff for plot updates."""

    def __init__(
        self,
        *,
        G: torch.nn.Module,
        device: torch.device,
        z_dim: int = 512,
        sample_size: int = 4,
    ) -> None:
        self.G = G.to(device).eval()
        self.device = device
        self.z_dim = z_dim
        self.sample_size = sample_size

        # --- Concurrency and State Management ---
        self._executor = ThreadPoolExecutor(max_workers=1)
        self._lock = threading.Lock()
        
        # Add exception handling for executor
        def _check_executor_exceptions():
            if self._future and self._future.done():
                try:
                    self._future.result()  # This will raise any exceptions from the executor
                except Exception as e:
                    print(f"Executor exception: {e}")
                    raise  # Re-raise the exception
        
        self._check_executor_exceptions = _check_executor_exceptions
        self._future: Future | None = None
        self._latest_payload: Any | None = None # The "mailbox" for results

        # --- Histories for plotting ---
        self.gen_hist, self.succ_hist, self.div_hist, self.wstd_hist = [], [], [], []

        # --- Figure Initialization ---
        self.fig = go.FigureWidget(make_subplots(
            rows=3, cols=2,
            specs=[
                [{"rowspan": 3}, {"type": "image"}],
                [None, {"rowspan": 2}],
                [None, None],
            ],
            column_widths=[0.66, 0.34],
            row_heights=[0.4, 0.3, 0.3],
            subplot_titles=("Z-Space Distribution", "Representative Samples", "Metrics"),
            vertical_spacing=0.05
        ))
        self._init_static_figure()
        display(self.fig)

    def request_update(
        self,
        *,
        generation: int,
        mean: np.ndarray,
        cov: np.ndarray,
        z_batch_gpu: torch.Tensor,
        success_rate: float,
        diversity: float,
        w_std_norm: float,
    ) -> None:
        """Submits a non-blocking request to calculate visualization data."""
        # Don't queue up new calculations if the previous one isn't finished.
        if self._future and not self._future.done():
            return

        # Submit the expensive calculation to the background thread.
        self._future = self._executor.submit(
            self._prepare_payload,
            generation, mean, cov, z_batch_gpu.detach().clone(),
            success_rate, diversity, w_std_norm
        )

    def update_plot_if_ready(self) -> None:
        """
        Checks for new data from the background thread and updates the plot.
        This method is fast and safe to call in every iteration of a loop.
        """
        payload_to_plot = None
        with self._lock:
            if self._latest_payload:
                payload_to_plot = self._latest_payload
                self._latest_payload = None # Consume the data
        if (self._check_executor_exceptions()) is not None:
            print("Executor exception")
        if payload_to_plot:
            (
                gen, succ, div, wstd,
                ellipse_x, ellipse_y, mx, my, grid_arr
            ) = payload_to_plot

            # Update histories
            self.gen_hist.append(gen)
            self.succ_hist.append(succ * 100)
            self.div_hist.append(div)
            self.wstd_hist.append(wstd)

            # Perform the plot update from the main thread
            with self.fig.batch_update():
                self.fig.data[0].x, self.fig.data[0].y = ellipse_x, ellipse_y
                self.fig.data[1].x, self.fig.data[1].y = [mx], [my]
                self.fig.data[2].z = grid_arr
                self.fig.data[3].x, self.fig.data[3].y = self.gen_hist, self.succ_hist
                self.fig.data[4].x, self.fig.data[4].y = self.gen_hist, self.div_hist
                self.fig.data[5].x, self.fig.data[5].y = self.gen_hist, self.wstd_hist

            return True
        
        if self._future and self._future.done():
            return True
        
        return False

    def _prepare_payload(self, gen, mean, cov, z_gpu, succ, div, wstd):
        """
        [Runs in Background] Performs long-running calculations.
        """
        # --- Start of your future long-running calculations ---
        ell_x, ell_y, mx, my = self._ellipse(mean, cov)
        grid = self._grid(z_gpu, mean)
        # --- End of long-running calculations ---

        payload = (gen, succ, div, wstd, ell_x, ell_y, mx, my, grid)

        # Safely place the result in the "mailbox"
        with self._lock:
            self._latest_payload = payload

    def shutdown(self):
        """Cleanly shuts down the background thread executor."""
        self._executor.shutdown()

    # (Helper methods like _init_static_figure, _ellipse, _grid, etc. remain the same)
    def _init_static_figure(self):
        """Initializes the static parts of the figure."""
        for r in range(1, 4): self.fig.add_shape(type="circle", xref="x1", yref="y1", x0=-r, y0=-r, x1=r, y1=r, line_color="grey", line_dash="dot", fillcolor="rgba(0,0,0,0)")
        self.fig.add_trace(go.Scatter(x=[], y=[], fill="toself", fillcolor="rgba(0,191,255,0.3)", name="Z Dist", line=dict(color="rgba(0,0,0,0)")), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode="markers", marker=dict(color="red", size=10), name="Mean"), row=1, col=1)
        self.fig.add_trace(go.Image(z=None), row=1, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="Success %", line=dict(width=2)), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="Diversity", line=dict(width=2, dash="dash")), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="W-Std", line=dict(width=2, dash="dot")), row=2, col=2)
        self.fig.update_layout(width=2200, height=1050, title_text="Live Evolutionary Search (Robust Async)", title_x=0.5, showlegend=True, legend=dict(x=0.67, y=0.6))
        self.fig.update_xaxes(title_text="Z Dim 0", range=[-5, 5], row=1, col=1)
        self.fig.update_yaxes(title_text="Z Dim 1", range=[-5, 5], scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Generation", row=2, col=2)
        self.fig.update_yaxes(title_text="Metric Value", row=2, col=2)

    def _ellipse(self, mean, cov):
        m2, c2 = mean[:2], cov[:2, :2]
        vals, vecs = np.linalg.eigh(c2)
        vals[vals < 0] = 1e-9
        ang = np.arctan2(vecs[1, 0], vecs[0, 0])
        r, t = 2 * np.sqrt(vals), np.linspace(0, 2 * np.pi, 200)
        ex, ey = r[0] * np.cos(t), r[1] * np.sin(t)
        ell_x, ell_y = m2[0] + ex * np.cos(ang) - ey * np.sin(ang), m2[1] + ex * np.sin(ang) + ey * np.cos(ang)
        return ell_x, ell_y, float(m2[0]), float(m2[1])

    def _grid(self, z_gpu, mean):
        z = z_gpu.cpu().numpy()
        dists = np.linalg.norm(z - mean, axis=1)
        idx = np.argsort(dists)[:self.sample_size]
        with torch.no_grad(): imgs_tensor = self.G.synthesis(self.G.mapping(z_gpu[idx], None)).cpu()
        tfm = Compose([Resize(512), lambda x: torch.clamp((x + 1) / 2, 0, 1)])
        pil_images = [TF.to_pil_image(tfm(im)) for im in imgs_tensor]
        return np.asarray(self._make_grid(pil_images))

    @staticmethod
    def _make_grid(imgs, rows=2):
        if not imgs: return None
        w, h = imgs[0].size
        cols = (len(imgs) + rows - 1) // rows
        canvas = Image.new("RGB", (cols * w, rows * h))
        for i, im in enumerate(imgs): canvas.paste(im, (i % cols * w, i // cols * h))
        return canvas

from tqdm import tqdm
from sklearn.ensemble import RandomForestClassifier
from typing import Dict, List, Tuple
import torch
import numpy as np

# Make sure the AsyncZSpaceVisualizer class is defined above this

class ZSpaceEvolutionarySampler2:
    """
    Finds a broad distribution of Z-space vectors and trains a surrogate model.
    """
    def __init__(self, target_filters: Dict, config: Dict, models: Dict, G: torch.nn.Module, device: torch.device):
        self.config = config
        self.models = {name: model.to(device) for name, model in models.items()}
        self.G = G.to(device)
        self.device = device
        self.z_dim = self.G.mapping.z_dim
        self.target_bin = self._parse_filters(target_filters)
        self.mean = np.zeros(self.z_dim, dtype=np.float32)
        self.cov = np.eye(self.z_dim, dtype=np.float32) * self.config.get('initial_variance', 1.0)
        self.original_mean = self.mean.copy()
        self.original_cov = self.cov.copy()
        self.unconstrained_w_std = None
        self.rf_classifier = RandomForestClassifier(n_estimators=50, max_depth=10, random_state=42, n_jobs=-1)
        self.is_rf_trained = False
        self.dtype = torch.float32

        # --- MODIFIED PART: Instantiate the correct visualizer ---
        if self.config.get('visualize_live', False):
            self.visualizer = AsyncZSpaceVisualizer(
                G=self.G,
                device=self.device,
                z_dim=self.z_dim,
                sample_size=self.config.get('image_sample_size', 4)
            )
        else:
            self.visualizer = None

    # Methods _parse_filters, _calculate_fitness, _calculate_hds remain unchanged
    def _parse_filters(self, filters: Dict) -> List[Dict]:
        target = []
        print("Parsing target bin from range-based filters...")
        for var, condition_dict in filters.items():
            if 'range' not in condition_dict: raise ValueError(f"Filter for '{var}' must contain a 'range' key.")
            target.append({'var': var, 'range': condition_dict['range'], 'weight': condition_dict.get('weight', 1.0)})
        print(f"Target bin defined as: {target}")
        return target

    @torch.no_grad()
    def _calculate_fitness(self, z_batch_gpu: torch.Tensor) -> Tuple[np.ndarray, torch.Tensor, torch.Tensor]:
        w_batch = self.G.mapping(z_batch_gpu, None)[:, 0]
        bin_loss = 0
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            target_val = low if high == np.inf else (high if low == -np.inf else (low + high) / 2.0)
            bin_loss += (preds - target_val)**2 * condition['weight']
        final_mask = torch.full((w_batch.shape[0],), True, device=self.device)
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            final_mask &= (preds >= low) & (preds <= high)
        return bin_loss.cpu().numpy(), final_mask, w_batch

    def _calculate_hds(self, z_samples: torch.Tensor) -> float:
        if z_samples.shape[0] < 2: return 1.0
        z_norm = z_samples / torch.norm(z_samples, p=2, dim=1, keepdim=True)
        sim_matrix = torch.matmul(z_norm, z_norm.T)
        n = sim_matrix.shape[0]
        off_diagonal_elements = torch.triu(sim_matrix, diagonal=1)
        clumpiness = torch.sum(off_diagonal_elements**2) * 2 / (n * (n - 1))
        return (1.0 - torch.sqrt(clumpiness)).cpu().item()


    def run(self) -> Tuple[np.ndarray, RandomForestClassifier]:
        n_to_generate, pop_size = self.config['n_samples_to_generate'], self.config['population_size']
        n_elite = int(pop_size * self.config['elite_fraction'])
        plot_every = self.config.get('plot_every_n_generations', 10) # Get plot frequency

        # --- Unchanged setup code ... ---
        print("Calculating baseline W-space standard deviation...")
        with torch.no_grad():
            initial_z_std = np.sqrt(self.config.get('initial_variance', 1.0))
            initial_z = torch.randn(pop_size, self.z_dim, device=self.device) * initial_z_std
            _, _, initial_w = self._calculate_fitness(initial_z)
            self.unconstrained_w_std = torch.mean(torch.std(initial_w, dim=0)).cpu().item()
        print(f"Baseline (unconstrained) W-space Std. Dev.: {self.unconstrained_w_std:.4f}")
        print(f"\nStarting evolutionary search...")
        
        pbar = tqdm(range(self.config['generations']), desc="Initializing...")

        # --- MODIFIED PART: Add try...finally for clean shutdown ---
        try:
            for gen in pbar:
                # --- Unchanged evolution logic ... ---
                stable_cov = self.cov + np.eye(self.z_dim, dtype=np.float32) * 1e-4
                z_candidates_cpu = np.random.multivariate_normal(self.mean, stable_cov, size=pop_size).astype(np.float32)
                z_candidates_gpu = torch.from_numpy(z_candidates_cpu).to(self.device, self.dtype)
                compliance_fitness, success_mask, w_candidates_gpu = self._calculate_fitness(z_candidates_gpu)
                z_candidates_norm = z_candidates_cpu / np.linalg.norm(z_candidates_cpu, axis=1, keepdims=True)
                if np.any(success_mask.cpu().numpy()):
                    self.rf_classifier.fit(z_candidates_norm, success_mask.cpu().numpy())
                    self.is_rf_trained = True
                successful_z = z_candidates_cpu[success_mask.cpu().numpy()]
                unsuccessful_z = z_candidates_cpu[~success_mask.cpu().numpy()]
                unsuccessful_fitness = compliance_fitness[~success_mask.cpu().numpy()]
                n_boundary_elites = int(n_elite * self.config['boundary_elite_fraction'])
                n_success_elites = n_elite - n_boundary_elites
                if len(unsuccessful_z) > 0:
                    boundary_indices = np.argsort(unsuccessful_fitness)[:int(n_boundary_elites*min(1,(gen+1)/5))]
                    elite_boundary = unsuccessful_z[boundary_indices]
                else:
                    elite_boundary = np.array([]).reshape(0, self.z_dim); n_success_elites = n_elite
                if len(successful_z) > 0:
                    if len(successful_z) <= n_success_elites: elite_success = successful_z
                    else: 
                        successful_z_norm = successful_z / np.linalg.norm(successful_z, axis=1, keepdims=True)
                        succ_norm_mean = np.mean(successful_z_norm, axis=0)
                        succ_norm_cov = np.cov(successful_z_norm, rowvar=False)
                        inv_succ_norm_cov = np.linalg.inv(succ_norm_cov + np.eye(self.z_dim) * 1e-6)
                        deltas = successful_z_norm - succ_norm_mean
                        distances = np.sum((deltas @ inv_succ_norm_cov) * deltas, axis=1)
                        elite_indices = np.argsort(distances)[-n_success_elites:]
                        elite_success = successful_z[elite_indices]
                else: elite_success = np.array([]).reshape(0, self.z_dim)
                elite_z = np.vstack([elite_success, elite_boundary]) if len(elite_success) > 0 and len(elite_boundary) > 0 else (elite_success if len(elite_success) > 0 else elite_boundary)
                if elite_z.shape[0] < 2: pbar.set_description(f"Elite stall ({elite_z.shape[0]})"); continue

                new_mean = np.mean(elite_z, axis=0)
                new_cov = np.cov(elite_z, rowvar=False)

                # calculate the James-Stein estimator
                n = elite_z.shape[0]
                p = self.z_dim
                alpha = 1 - (p-2)/n/(new_mean**2).sum()
                print(alpha)
                new_mean = (1-alpha) * new_mean
                

                lr = self.config['update_learning_rate']
                self.mean = (1 - lr) * self.mean + lr * new_mean
                mean_norm = np.linalg.norm(self.mean)
                # self.mean = self.mean / np.clip(mean_norm, 1, 10e18)
                print(mean_norm)
                if mean_norm > 1e-6:
                    mu_hat = self.mean / mean_norm
                    proj_matrix = np.eye(self.z_dim) - np.outer(mu_hat, mu_hat)
                    projected_cov = proj_matrix @ new_cov @ proj_matrix
                else: projected_cov = new_cov
                self.cov = (1 - lr) * self.cov + lr * projected_cov 

                # weight decay step:
                weight_decay = self.config['weight_decay']
                # self.mean = (1 - weight_decay) * self.mean + weight_decay * self.original_mean
                # self.cov = (1 - weight_decay) * self.cov + weight_decay * self.original_cov
                
                
                # --- METRICS AND VISUALIZATION ---
                current_success_rate = success_mask.float().mean().cpu().item()
                diversity_score = self._calculate_hds(torch.from_numpy(elite_z).to(self.device, self.dtype))
                successful_w = w_candidates_gpu[success_mask]
                mean_w_std = torch.mean(torch.std(successful_w, dim=0)).cpu().item() if successful_w.shape[0] > 1 else 0.0
                normalized_w_std = mean_w_std / self.unconstrained_w_std if self.unconstrained_w_std > 0 else 0.0
                rf_score = self.rf_classifier.score(z_candidates_norm, success_mask.cpu().numpy()) if self.is_rf_trained else 0.0
                pbar.set_description(f"Elite: {len(elite_success)}S/{len(elite_boundary)}B | RF Acc: {rf_score:.2f}")
                pbar.set_postfix(succ=f"{current_success_rate*100:.1f}%", hds=f"{diversity_score:.3f}", w_std_norm=f"{normalized_w_std:.3f}")

                # --- MODIFIED PART: Add visualizer calls ---
                if self.visualizer:
                    # 1. Request an update periodically (non-blocking)
                    if gen % plot_every == 0:
                        self.visualizer.request_update(
                            generation=gen,
                            mean=self.mean,
                            cov=self.cov,
                            z_batch_gpu=z_candidates_gpu, # Use the z-vectors from this generation
                            success_rate=current_success_rate,
                            diversity=diversity_score,
                            w_std_norm=normalized_w_std
                        )
                    # 2. Check for and apply updates on every iteration (non-blocking)
                    # while not self.visualizer.update_plot_if_ready():
                    #     pass
                    self.visualizer.update_plot_if_ready()
        finally:
            # 3. Ensure the background thread is shut down cleanly
            if self.visualizer:
                self.visualizer.shutdown()

        # --- Unchanged final sample generation ... ---
        print(f"\nEvolution complete. Harvesting final samples...")
        final_stable_cov = self.cov + np.eye(self.z_dim, dtype=np.float32) * 1e-6
        final_candidates_z = np.random.multivariate_normal(self.mean, final_stable_cov, size=int(n_to_generate * 3.0)).astype(np.float32)
        _, final_mask, _ = self._calculate_fitness(torch.from_numpy(final_candidates_z).to(self.device, self.dtype))
        successful_z = final_candidates_z[final_mask.cpu().numpy()][:n_to_generate]
        print(f"Successfully generated and filtered {len(successful_z)} Z vectors.")
        
        return successful_z, self.rf_classifier
        self.z_dim = z_dim
        self.sample_size = sample_size

        # --- Concurrency and State Management ---
        self._executor = ThreadPoolExecutor(max_workers=1)
        self._lock = threading.Lock()
        
        # Add exception handling for executor
        def _check_executor_exceptions():
            if self._future and self._future.done():
                try:
                    self._future.result()  # This will raise any exceptions from the executor
                except Exception as e:
                    print(f"Executor exception: {e}")
                    raise  # Re-raise the exception
        
        self._check_executor_exceptions = _check_executor_exceptions
        self._future: Future | None = None
        self._latest_payload: Any | None = None # The "mailbox" for results

        # --- Histories for plotting ---
        self.gen_hist, self.succ_hist, self.div_hist, self.wstd_hist = [], [], [], []

        # --- Figure Initialization ---
        self.fig = go.FigureWidget(make_subplots(
            rows=3, cols=2,
            specs=[
                [{"rowspan": 3}, {"type": "image"}],
                [None, {"rowspan": 2}],
                [None, None],
            ],
            column_widths=[0.66, 0.34],
            row_heights=[0.4, 0.3, 0.3],
            subplot_titles=("Z-Space Distribution", "Representative Samples", "Metrics"),
            vertical_spacing=0.05
        ))
        self._init_static_figure()
        display(self.fig)

    def request_update(
        self,
        *,
        generation: int,
        mean: np.ndarray,
        cov: np.ndarray,
        z_batch_gpu: torch.Tensor,
        success_rate: float,
        diversity: float,
        w_std_norm: float,
    ) -> None:
        """Submits a non-blocking request to calculate visualization data."""
        # Don't queue up new calculations if the previous one isn't finished.
        if self._future and not self._future.done():
            return

        # Submit the expensive calculation to the background thread.
        self._future = self._executor.submit(
            self._prepare_payload,
            generation, mean, cov, z_batch_gpu.detach().clone(),
            success_rate, diversity, w_std_norm
        )

    def update_plot_if_ready(self) -> None:
        """
        Checks for new data from the background thread and updates the plot.
        This method is fast and safe to call in every iteration of a loop.
        """
        payload_to_plot = None
        with self._lock:
            if self._latest_payload:
                payload_to_plot = self._latest_payload
                self._latest_payload = None # Consume the data
        if (self._check_executor_exceptions()) is not None:
            print("Executor exception")
        if payload_to_plot:
            (
                gen, succ, div, wstd,
                ellipse_x, ellipse_y, mx, my, grid_arr
            ) = payload_to_plot

            # Update histories
            self.gen_hist.append(gen)
            self.succ_hist.append(succ * 100)
            self.div_hist.append(div)
            self.wstd_hist.append(wstd)

            # Perform the plot update from the main thread
            with self.fig.batch_update():
                self.fig.data[0].x, self.fig.data[0].y = ellipse_x, ellipse_y
                self.fig.data[1].x, self.fig.data[1].y = [mx], [my]
                self.fig.data[2].z = grid_arr
                self.fig.data[3].x, self.fig.data[3].y = self.gen_hist, self.succ_hist
                self.fig.data[4].x, self.fig.data[4].y = self.gen_hist, self.div_hist
                self.fig.data[5].x, self.fig.data[5].y = self.gen_hist, self.wstd_hist

            return True
        
        if self._future and self._future.done():
            return True
        
        return False

    def _prepare_payload(self, gen, mean, cov, z_gpu, succ, div, wstd):
        """
        [Runs in Background] Performs long-running calculations.
        """
        # --- Start of your future long-running calculations ---
        ell_x, ell_y, mx, my = self._ellipse(mean, cov)
        grid = self._grid(z_gpu, mean)
        # --- End of long-running calculations ---

        payload = (gen, succ, div, wstd, ell_x, ell_y, mx, my, grid)

        # Safely place the result in the "mailbox"
        with self._lock:
            self._latest_payload = payload

    def shutdown(self):
        """Cleanly shuts down the background thread executor."""
        self._executor.shutdown()

    # (Helper methods like _init_static_figure, _ellipse, _grid, etc. remain the same)
    def _init_static_figure(self):
        """Initializes the static parts of the figure."""
        for r in range(1, 4): self.fig.add_shape(type="circle", xref="x1", yref="y1", x0=-r, y0=-r, x1=r, y1=r, line_color="grey", line_dash="dot", fillcolor="rgba(0,0,0,0)")
        self.fig.add_trace(go.Scatter(x=[], y=[], fill="toself", fillcolor="rgba(0,191,255,0.3)", name="Z Dist", line=dict(color="rgba(0,0,0,0)")), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode="markers", marker=dict(color="red", size=10), name="Mean"), row=1, col=1)
        self.fig.add_trace(go.Image(z=None), row=1, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="Success %", line=dict(width=2)), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="Diversity", line=dict(width=2, dash="dash")), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="W-Std", line=dict(width=2, dash="dot")), row=2, col=2)
        self.fig.update_layout(width=2200, height=1050, title_text="Live Evolutionary Search (Robust Async)", title_x=0.5, showlegend=True, legend=dict(x=0.67, y=0.6))
        self.fig.update_xaxes(title_text="Z Dim 0", range=[-5, 5], row=1, col=1)
        self.fig.update_yaxes(title_text="Z Dim 1", range=[-5, 5], scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Generation", row=2, col=2)
        self.fig.update_yaxes(title_text="Metric Value", row=2, col=2)

    def _ellipse(self, mean, cov):
        m2, c2 = mean[:2], cov[:2, :2]
        vals, vecs = np.linalg.eigh(c2)
        vals[vals < 0] = 1e-9
        ang = np.arctan2(vecs[1, 0], vecs[0, 0])
        r, t = 2 * np.sqrt(vals), np.linspace(0, 2 * np.pi, 200)
        ex, ey = r[0] * np.cos(t), r[1] * np.sin(t)
        ell_x, ell_y = m2[0] + ex * np.cos(ang) - ey * np.sin(ang), m2[1] + ex * np.sin(ang) + ey * np.cos(ang)
        return ell_x, ell_y, float(m2[0]), float(m2[1])

    def _grid(self, z_gpu, mean):
        z = z_gpu.cpu().numpy()
        dists = np.linalg.norm(z - mean, axis=1)
        idx = np.argsort(dists)[:self.sample_size]
        with torch.no_grad(): imgs_tensor = self.G.synthesis(self.G.mapping(z_gpu[idx], None)).cpu()
        tfm = Compose([Resize(512), lambda x: torch.clamp((x + 1) / 2, 0, 1)])
        pil_images = [TF.to_pil_image(tfm(im)) for im in imgs_tensor]
        return np.asarray(self._make_grid(pil_images))

    @staticmethod
    def _make_grid(imgs, rows=2):
        if not imgs: return None
        w, h = imgs[0].size
        cols = (len(imgs) + rows - 1) // rows
        canvas = Image.new("RGB", (cols * w, rows * h))
        for i, im in enumerate(imgs): canvas.paste(im, (i % cols * w, i // cols * h))
        return canvas

from tqdm import tqdm
from sklearn.ensemble import RandomForestClassifier
from typing import Dict, List, Tuple
import torch
import numpy as np

# Make sure the AsyncZSpaceVisualizer class is defined above this

class ZSpaceEvolutionarySampler2:
    """
    Finds a broad distribution of Z-space vectors and trains a surrogate model.
    """
    def __init__(self, target_filters: Dict, config: Dict, models: Dict, G: torch.nn.Module, device: torch.device):
        self.config = config
        self.models = {name: model.to(device) for name, model in models.items()}
        self.G = G.to(device)
        self.device = device
        self.z_dim = self.G.mapping.z_dim
        self.target_bin = self._parse_filters(target_filters)
        self.mean = np.zeros(self.z_dim, dtype=np.float32)
        self.cov = np.eye(self.z_dim, dtype=np.float32) * self.config.get('initial_variance', 1.0)
        self.original_mean = self.mean.copy()
        self.original_cov = self.cov.copy()
        self.unconstrained_w_std = None
        self.rf_classifier = RandomForestClassifier(n_estimators=50, max_depth=10, random_state=42, n_jobs=-1)
        self.is_rf_trained = False
        self.dtype = torch.float32

        # --- MODIFIED PART: Instantiate the correct visualizer ---
        if self.config.get('visualize_live', False):
            self.visualizer = AsyncZSpaceVisualizer(
                G=self.G,
                device=self.device,
                z_dim=self.z_dim,
                sample_size=self.config.get('image_sample_size', 4)
            )
        else:
            self.visualizer = None

    # Methods _parse_filters, _calculate_fitness, _calculate_hds remain unchanged
    def _parse_filters(self, filters: Dict) -> List[Dict]:
        target = []
        print("Parsing target bin from range-based filters...")
        for var, condition_dict in filters.items():
            if 'range' not in condition_dict: raise ValueError(f"Filter for '{var}' must contain a 'range' key.")
            target.append({'var': var, 'range': condition_dict['range'], 'weight': condition_dict.get('weight', 1.0)})
        print(f"Target bin defined as: {target}")
        return target

    @torch.no_grad()
    def _calculate_fitness(self, z_batch_gpu: torch.Tensor) -> Tuple[np.ndarray, torch.Tensor, torch.Tensor]:
        w_batch = self.G.mapping(z_batch_gpu, None)[:, 0]
        bin_loss = 0
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            target_val = low if high == np.inf else (high if low == -np.inf else (low + high) / 2.0)
            bin_loss += (preds - target_val)**2 * condition['weight']
        final_mask = torch.full((w_batch.shape[0],), True, device=self.device)
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            final_mask &= (preds >= low) & (preds <= high)
        return bin_loss.cpu().numpy(), final_mask, w_batch

    def _calculate_hds(self, z_samples: torch.Tensor) -> float:
        if z_samples.shape[0] < 2: return 1.0
        z_norm = z_samples / torch.norm(z_samples, p=2, dim=1, keepdim=True)
        sim_matrix = torch.matmul(z_norm, z_norm.T)
        n = sim_matrix.shape[0]
        off_diagonal_elements = torch.triu(sim_matrix, diagonal=1)
        clumpiness = torch.sum(off_diagonal_elements**2) * 2 / (n * (n - 1))
        return (1.0 - torch.sqrt(clumpiness)).cpu().item()


    def run(self) -> Tuple[np.ndarray, RandomForestClassifier]:
        n_to_generate, pop_size = self.config['n_samples_to_generate'], self.config['population_size']
        n_elite = int(pop_size * self.config['elite_fraction'])
        plot_every = self.config.get('plot_every_n_generations', 10) # Get plot frequency

        # --- Unchanged setup code ... ---
        print("Calculating baseline W-space standard deviation...")
        with torch.no_grad():
            initial_z_std = np.sqrt(self.config.get('initial_variance', 1.0))
            initial_z = torch.randn(pop_size, self.z_dim, device=self.device) * initial_z_std
            _, _, initial_w = self._calculate_fitness(initial_z)
            self.unconstrained_w_std = torch.mean(torch.std(initial_w, dim=0)).cpu().item()
        print(f"Baseline (unconstrained) W-space Std. Dev.: {self.unconstrained_w_std:.4f}")
        print(f"\nStarting evolutionary search...")
        
        pbar = tqdm(range(self.config['generations']), desc="Initializing...")

        # --- MODIFIED PART: Add try...finally for clean shutdown ---
        try:
            for gen in pbar:
                # --- Unchanged evolution logic ... ---
                stable_cov = self.cov + np.eye(self.z_dim, dtype=np.float32) * 1e-4
                z_candidates_cpu = np.random.multivariate_normal(self.mean, stable_cov, size=pop_size).astype(np.float32)
                z_candidates_gpu = torch.from_numpy(z_candidates_cpu).to(self.device, self.dtype)
                compliance_fitness, success_mask, w_candidates_gpu = self._calculate_fitness(z_candidates_gpu)
                z_candidates_norm = z_candidates_cpu / np.linalg.norm(z_candidates_cpu, axis=1, keepdims=True)
                if np.any(success_mask.cpu().numpy()):
                    self.rf_classifier.fit(z_candidates_norm, success_mask.cpu().numpy())
                    self.is_rf_trained = True
                successful_z = z_candidates_cpu[success_mask.cpu().numpy()]
                unsuccessful_z = z_candidates_cpu[~success_mask.cpu().numpy()]
                unsuccessful_fitness = compliance_fitness[~success_mask.cpu().numpy()]
                n_boundary_elites = int(n_elite * self.config['boundary_elite_fraction'])
                n_success_elites = n_elite - n_boundary_elites
                if len(unsuccessful_z) > 0:
                    boundary_indices = np.argsort(unsuccessful_fitness)[:int(n_boundary_elites*min(1,(gen+1)/5))]
                    elite_boundary = unsuccessful_z[boundary_indices]
                else:
                    elite_boundary = np.array([]).reshape(0, self.z_dim); n_success_elites = n_elite
                if len(successful_z) > 0:
                    if len(successful_z) <= n_success_elites: elite_success = successful_z
                    else: 
                        successful_z_norm = successful_z / np.linalg.norm(successful_z, axis=1, keepdims=True)
                        succ_norm_mean = np.mean(successful_z_norm, axis=0)
                        succ_norm_cov = np.cov(successful_z_norm, rowvar=False)
                        inv_succ_norm_cov = np.linalg.inv(succ_norm_cov + np.eye(self.z_dim) * 1e-6)
                        deltas = successful_z_norm - succ_norm_mean
                        distances = np.sum((deltas @ inv_succ_norm_cov) * deltas, axis=1)
                        elite_indices = np.argsort(distances)[-n_success_elites:]
                        elite_success = successful_z[elite_indices]
                else: elite_success = np.array([]).reshape(0, self.z_dim)
                elite_z = np.vstack([elite_success, elite_boundary]) if len(elite_success) > 0 and len(elite_boundary) > 0 else (elite_success if len(elite_success) > 0 else elite_boundary)
                if elite_z.shape[0] < 2: pbar.set_description(f"Elite stall ({elite_z.shape[0]})"); continue

                new_mean = np.mean(elite_z, axis=0)
                new_cov = np.cov(elite_z, rowvar=False)

                # calculate the James-Stein estimator
                n = elite_z.shape[0]
                p = self.z_dim
                alpha = 1 - (p-2)/n/(new_mean**2).sum()
                print(alpha)
                new_mean = (1-alpha) * new_mean
                

                lr = self.config['update_learning_rate']
                self.mean = (1 - lr) * self.mean + lr * new_mean
                mean_norm = np.linalg.norm(self.mean)
                # self.mean = self.mean / np.clip(mean_norm, 1, 10e18)
                print(mean_norm)
                if mean_norm > 1e-6:
                    mu_hat = self.mean / mean_norm
                    proj_matrix = np.eye(self.z_dim) - np.outer(mu_hat, mu_hat)
                    projected_cov = proj_matrix @ new_cov @ proj_matrix
                else: projected_cov = new_cov
                self.cov = (1 - lr) * self.cov + lr * projected_cov 

                # weight decay step:
                weight_decay = self.config['weight_decay']
                # self.mean = (1 - weight_decay) * self.mean + weight_decay * self.original_mean
                # self.cov = (1 - weight_decay) * self.cov + weight_decay * self.original_cov
                
                
                # --- METRICS AND VISUALIZATION ---
                current_success_rate = success_mask.float().mean().cpu().item()
                diversity_score = self._calculate_hds(torch.from_numpy(elite_z).to(self.device, self.dtype))
                successful_w = w_candidates_gpu[success_mask]
                mean_w_std = torch.mean(torch.std(successful_w, dim=0)).cpu().item() if successful_w.shape[0] > 1 else 0.0
                normalized_w_std = mean_w_std / self.unconstrained_w_std if self.unconstrained_w_std > 0 else 0.0
                rf_score = self.rf_classifier.score(z_candidates_norm, success_mask.cpu().numpy()) if self.is_rf_trained else 0.0
                pbar.set_description(f"Elite: {len(elite_success)}S/{len(elite_boundary)}B | RF Acc: {rf_score:.2f}")
                pbar.set_postfix(succ=f"{current_success_rate*100:.1f}%", hds=f"{diversity_score:.3f}", w_std_norm=f"{normalized_w_std:.3f}")

                # --- MODIFIED PART: Add visualizer calls ---
                if self.visualizer:
                    # 1. Request an update periodically (non-blocking)
                    if gen % plot_every == 0:
                        self.visualizer.request_update(
                            generation=gen,
                            mean=self.mean,
                            cov=self.cov,
                            z_batch_gpu=z_candidates_gpu, # Use the z-vectors from this generation
                            success_rate=current_success_rate,
                            diversity=diversity_score,
                            w_std_norm=normalized_w_std
                        )
                    # 2. Check for and apply updates on every iteration (non-blocking)
                    # while not self.visualizer.update_plot_if_ready():
                    #     pass
                    self.visualizer.update_plot_if_ready()
        finally:
            # 3. Ensure the background thread is shut down cleanly
            if self.visualizer:
                self.visualizer.shutdown()

        # --- Unchanged final sample generation ... ---
        print(f"\nEvolution complete. Harvesting final samples...")
        final_stable_cov = self.cov + np.eye(self.z_dim, dtype=np.float32) * 1e-6
        final_candidates_z = np.random.multivariate_normal(self.mean, final_stable_cov, size=int(n_to_generate * 3.0)).astype(np.float32)
        _, final_mask, _ = self._calculate_fitness(torch.from_numpy(final_candidates_z).to(self.device, self.dtype))
        successful_z = final_candidates_z[final_mask.cpu().numpy()][:n_to_generate]
        print(f"Successfully generated and filtered {len(successful_z)} Z vectors.")
        
        return successful_z, self.rf_classifier
        self.z_dim = z_dim
        self.sample_size = sample_size

        # --- Concurrency and State Management ---
        self._executor = ThreadPoolExecutor(max_workers=1)
        self._lock = threading.Lock()
        
        # Add exception handling for executor
        def _check_executor_exceptions():
            if self._future and self._future.done():
                try:
                    self._future.result()  # This will raise any exceptions from the executor
                except Exception as e:
                    print(f"Executor exception: {e}")
                    raise  # Re-raise the exception
        
        self._check_executor_exceptions = _check_executor_exceptions
        self._future: Future | None = None
        self._latest_payload: Any | None = None # The "mailbox" for results

        # --- Histories for plotting ---
        self.gen_hist, self.succ_hist, self.div_hist, self.wstd_hist = [], [], [], []

        # --- Figure Initialization ---
        self.fig = go.FigureWidget(make_subplots(
            rows=3, cols=2,
            specs=[
                [{"rowspan": 3}, {"type": "image"}],
                [None, {"rowspan": 2}],
                [None, None],
            ],
            column_widths=[0.66, 0.34],
            row_heights=[0.4, 0.3, 0.3],
            subplot_titles=("Z-Space Distribution", "Representative Samples", "Metrics"),
            vertical_spacing=0.05
        ))
        self._init_static_figure()
        display(self.fig)

    def request_update(
        self,
        *,
        generation: int,
        mean: np.ndarray,
        cov: np.ndarray,
        z_batch_gpu: torch.Tensor,
        success_rate: float,
        diversity: float,
        w_std_norm: float,
    ) -> None:
        """Submits a non-blocking request to calculate visualization data."""
        # Don't queue up new calculations if the previous one isn't finished.
        if self._future and not self._future.done():
            return

        # Submit the expensive calculation to the background thread.
        self._future = self._executor.submit(
            self._prepare_payload,
            generation, mean, cov, z_batch_gpu.detach().clone(),
            success_rate, diversity, w_std_norm
        )

    def update_plot_if_ready(self) -> None:
        """
        Checks for new data from the background thread and updates the plot.
        This method is fast and safe to call in every iteration of a loop.
        """
        payload_to_plot = None
        with self._lock:
            if self._latest_payload:
                payload_to_plot = self._latest_payload
                self._latest_payload = None # Consume the data
        if (self._check_executor_exceptions()) is not None:
            print("Executor exception")
        if payload_to_plot:
            (
                gen, succ, div, wstd,
                ellipse_x, ellipse_y, mx, my, grid_arr
            ) = payload_to_plot

            # Update histories
            self.gen_hist.append(gen)
            self.succ_hist.append(succ * 100)
            self.div_hist.append(div)
            self.wstd_hist.append(wstd)

            # Perform the plot update from the main thread
            with self.fig.batch_update():
                self.fig.data[0].x, self.fig.data[0].y = ellipse_x, ellipse_y
                self.fig.data[1].x, self.fig.data[1].y = [mx], [my]
                self.fig.data[2].z = grid_arr
                self.fig.data[3].x, self.fig.data[3].y = self.gen_hist, self.succ_hist
                self.fig.data[4].x, self.fig.data[4].y = self.gen_hist, self.div_hist
                self.fig.data[5].x, self.fig.data[5].y = self.gen_hist, self.wstd_hist

            return True
        
        if self._future and self._future.done():
            return True
        
        return False

    def _prepare_payload(self, gen, mean, cov, z_gpu, succ, div, wstd):
        """
        [Runs in Background] Performs long-running calculations.
        """
        # --- Start of your future long-running calculations ---
        ell_x, ell_y, mx, my = self._ellipse(mean, cov)
        grid = self._grid(z_gpu, mean)
        # --- End of long-running calculations ---

        payload = (gen, succ, div, wstd, ell_x, ell_y, mx, my, grid)

        # Safely place the result in the "mailbox"
        with self._lock:
            self._latest_payload = payload

    def shutdown(self):
        """Cleanly shuts down the background thread executor."""
        self._executor.shutdown()

    # (Helper methods like _init_static_figure, _ellipse, _grid, etc. remain the same)
    def _init_static_figure(self):
        """Initializes the static parts of the figure."""
        for r in range(1, 4): self.fig.add_shape(type="circle", xref="x1", yref="y1", x0=-r, y0=-r, x1=r, y1=r, line_color="grey", line_dash="dot", fillcolor="rgba(0,0,0,0)")
        self.fig.add_trace(go.Scatter(x=[], y=[], fill="toself", fillcolor="rgba(0,191,255,0.3)", name="Z Dist", line=dict(color="rgba(0,0,0,0)")), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode="markers", marker=dict(color="red", size=10), name="Mean"), row=1, col=1)
        self.fig.add_trace(go.Image(z=None), row=1, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="Success %", line=dict(width=2)), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="Diversity", line=dict(width=2, dash="dash")), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="W-Std", line=dict(width=2, dash="dot")), row=2, col=2)
        self.fig.update_layout(width=2200, height=1050, title_text="Live Evolutionary Search (Robust Async)", title_x=0.5, showlegend=True, legend=dict(x=0.67, y=0.6))
        self.fig.update_xaxes(title_text="Z Dim 0", range=[-5, 5], row=1, col=1)
        self.fig.update_yaxes(title_text="Z Dim 1", range=[-5, 5], scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Generation", row=2, col=2)
        self.fig.update_yaxes(title_text="Metric Value", row=2, col=2)

    def _ellipse(self, mean, cov):
        m2, c2 = mean[:2], cov[:2, :2]
        vals, vecs = np.linalg.eigh(c2)
        vals[vals < 0] = 1e-9
        ang = np.arctan2(vecs[1, 0], vecs[0, 0])
        r, t = 2 * np.sqrt(vals), np.linspace(0, 2 * np.pi, 200)
        ex, ey = r[0] * np.cos(t), r[1] * np.sin(t)
        ell_x, ell_y = m2[0] + ex * np.cos(ang) - ey * np.sin(ang), m2[1] + ex * np.sin(ang) + ey * np.cos(ang)
        return ell_x, ell_y, float(m2[0]), float(m2[1])

    def _grid(self, z_gpu, mean):
        z = z_gpu.cpu().numpy()
        dists = np.linalg.norm(z - mean, axis=1)
        idx = np.argsort(dists)[:self.sample_size]
        with torch.no_grad(): imgs_tensor = self.G.synthesis(self.G.mapping(z_gpu[idx], None)).cpu()
        tfm = Compose([Resize(512), lambda x: torch.clamp((x + 1) / 2, 0, 1)])
        pil_images = [TF.to_pil_image(tfm(im)) for im in imgs_tensor]
        return np.asarray(self._make_grid(pil_images))

    @staticmethod
    def _make_grid(imgs, rows=2):
        if not imgs: return None
        w, h = imgs[0].size
        cols = (len(imgs) + rows - 1) // rows
        canvas = Image.new("RGB", (cols * w, rows * h))
        for i, im in enumerate(imgs): canvas.paste(im, (i % cols * w, i // cols * h))
        return canvas

from tqdm import tqdm
from sklearn.ensemble import RandomForestClassifier
from typing import Dict, List, Tuple
import torch
import numpy as np

# Make sure the AsyncZSpaceVisualizer class is defined above this

class ZSpaceEvolutionarySampler2:
    """
    Finds a broad distribution of Z-space vectors and trains a surrogate model.
    """
    def __init__(self, target_filters: Dict, config: Dict, models: Dict, G: torch.nn.Module, device: torch.device):
        self.config = config
        self.models = {name: model.to(device) for name, model in models.items()}
        self.G = G.to(device)
        self.device = device
        self.z_dim = self.G.mapping.z_dim
        self.target_bin = self._parse_filters(target_filters)
        self.mean = np.zeros(self.z_dim, dtype=np.float32)
        self.cov = np.eye(self.z_dim, dtype=np.float32) * self.config.get('initial_variance', 1.0)
        self.original_mean = self.mean.copy()
        self.original_cov = self.cov.copy()
        self.unconstrained_w_std = None
        self.rf_classifier = RandomForestClassifier(n_estimators=50, max_depth=10, random_state=42, n_jobs=-1)
        self.is_rf_trained = False
        self.dtype = torch.float32

        # --- MODIFIED PART: Instantiate the correct visualizer ---
        if self.config.get('visualize_live', False):
            self.visualizer = AsyncZSpaceVisualizer(
                G=self.G,
                device=self.device,
                z_dim=self.z_dim,
                sample_size=self.config.get('image_sample_size', 4)
            )
        else:
            self.visualizer = None

    # Methods _parse_filters, _calculate_fitness, _calculate_hds remain unchanged
    def _parse_filters(self, filters: Dict) -> List[Dict]:
        target = []
        print("Parsing target bin from range-based filters...")
        for var, condition_dict in filters.items():
            if 'range' not in condition_dict: raise ValueError(f"Filter for '{var}' must contain a 'range' key.")
            target.append({'var': var, 'range': condition_dict['range'], 'weight': condition_dict.get('weight', 1.0)})
        print(f"Target bin defined as: {target}")
        return target

    @torch.no_grad()
    def _calculate_fitness(self, z_batch_gpu: torch.Tensor) -> Tuple[np.ndarray, torch.Tensor, torch.Tensor]:
        w_batch = self.G.mapping(z_batch_gpu, None)[:, 0]
        bin_loss = 0
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            target_val = low if high == np.inf else (high if low == -np.inf else (low + high) / 2.0)
            bin_loss += (preds - target_val)**2 * condition['weight']
        final_mask = torch.full((w_batch.shape[0],), True, device=self.device)
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            final_mask &= (preds >= low) & (preds <= high)
        return bin_loss.cpu().numpy(), final_mask, w_batch

    def _calculate_hds(self, z_samples: torch.Tensor) -> float:
        if z_samples.shape[0] < 2: return 1.0
        z_norm = z_samples / torch.norm(z_samples, p=2, dim=1, keepdim=True)
        sim_matrix = torch.matmul(z_norm, z_norm.T)
        n = sim_matrix.shape[0]
        off_diagonal_elements = torch.triu(sim_matrix, diagonal=1)
        clumpiness = torch.sum(off_diagonal_elements**2) * 2 / (n * (n - 1))
        return (1.0 - torch.sqrt(clumpiness)).cpu().item()


    def run(self) -> Tuple[np.ndarray, RandomForestClassifier]:
        n_to_generate, pop_size = self.config['n_samples_to_generate'], self.config['population_size']
        n_elite = int(pop_size * self.config['elite_fraction'])
        plot_every = self.config.get('plot_every_n_generations', 10) # Get plot frequency

        # --- Unchanged setup code ... ---
        print("Calculating baseline W-space standard deviation...")
        with torch.no_grad():
            initial_z_std = np.sqrt(self.config.get('initial_variance', 1.0))
            initial_z = torch.randn(pop_size, self.z_dim, device=self.device) * initial_z_std
            _, _, initial_w = self._calculate_fitness(initial_z)
            self.unconstrained_w_std = torch.mean(torch.std(initial_w, dim=0)).cpu().item()
        print(f"Baseline (unconstrained) W-space Std. Dev.: {self.unconstrained_w_std:.4f}")
        print(f"\nStarting evolutionary search...")
        
        pbar = tqdm(range(self.config['generations']), desc="Initializing...")

        # --- MODIFIED PART: Add try...finally for clean shutdown ---
        try:
            for gen in pbar:
                # --- Unchanged evolution logic ... ---
                stable_cov = self.cov + np.eye(self.z_dim, dtype=np.float32) * 1e-4
                z_candidates_cpu = np.random.multivariate_normal(self.mean, stable_cov, size=pop_size).astype(np.float32)
                z_candidates_gpu = torch.from_numpy(z_candidates_cpu).to(self.device, self.dtype)
                compliance_fitness, success_mask, w_candidates_gpu = self._calculate_fitness(z_candidates_gpu)
                z_candidates_norm = z_candidates_cpu / np.linalg.norm(z_candidates_cpu, axis=1, keepdims=True)
                if np.any(success_mask.cpu().numpy()):
                    self.rf_classifier.fit(z_candidates_norm, success_mask.cpu().numpy())
                    self.is_rf_trained = True
                successful_z = z_candidates_cpu[success_mask.cpu().numpy()]
                unsuccessful_z = z_candidates_cpu[~success_mask.cpu().numpy()]
                unsuccessful_fitness = compliance_fitness[~success_mask.cpu().numpy()]
                n_boundary_elites = int(n_elite * self.config['boundary_elite_fraction'])
                n_success_elites = n_elite - n_boundary_elites
                if len(unsuccessful_z) > 0:
                    boundary_indices = np.argsort(unsuccessful_fitness)[:int(n_boundary_elites*min(1,(gen+1)/5))]
                    elite_boundary = unsuccessful_z[boundary_indices]
                else:
                    elite_boundary = np.array([]).reshape(0, self.z_dim); n_success_elites = n_elite
                if len(successful_z) > 0:
                    if len(successful_z) <= n_success_elites: elite_success = successful_z
                    else: 
                        successful_z_norm = successful_z / np.linalg.norm(successful_z, axis=1, keepdims=True)
                        succ_norm_mean = np.mean(successful_z_norm, axis=0)
                        succ_norm_cov = np.cov(successful_z_norm, rowvar=False)
                        inv_succ_norm_cov = np.linalg.inv(succ_norm_cov + np.eye(self.z_dim) * 1e-6)
                        deltas = successful_z_norm - succ_norm_mean
                        distances = np.sum((deltas @ inv_succ_norm_cov) * deltas, axis=1)
                        elite_indices = np.argsort(distances)[-n_success_elites:]
                        elite_success = successful_z[elite_indices]
                else: elite_success = np.array([]).reshape(0, self.z_dim)
                elite_z = np.vstack([elite_success, elite_boundary]) if len(elite_success) > 0 and len(elite_boundary) > 0 else (elite_success if len(elite_success) > 0 else elite_boundary)
                if elite_z.shape[0] < 2: pbar.set_description(f"Elite stall ({elite_z.shape[0]})"); continue

                new_mean = np.mean(elite_z, axis=0)
                new_cov = np.cov(elite_z, rowvar=False)

                # calculate the James-Stein estimator
                n = elite_z.shape[0]
                p = self.z_dim
                alpha = 1 - (p-2)/n/(new_mean**2).sum()
                print(alpha)
                new_mean = (1-alpha) * new_mean
                

                lr = self.config['update_learning_rate']
                self.mean = (1 - lr) * self.mean + lr * new_mean
                mean_norm = np.linalg.norm(self.mean)
                # self.mean = self.mean / np.clip(mean_norm, 1, 10e18)
                print(mean_norm)
                if mean_norm > 1e-6:
                    mu_hat = self.mean / mean_norm
                    proj_matrix = np.eye(self.z_dim) - np.outer(mu_hat, mu_hat)
                    projected_cov = proj_matrix @ new_cov @ proj_matrix
                else: projected_cov = new_cov
                self.cov = (1 - lr) * self.cov + lr * projected_cov 

                # weight decay step:
                weight_decay = self.config['weight_decay']
                # self.mean = (1 - weight_decay) * self.mean + weight_decay * self.original_mean
                # self.cov = (1 - weight_decay) * self.cov + weight_decay * self.original_cov
                
                
                # --- METRICS AND VISUALIZATION ---
                current_success_rate = success_mask.float().mean().cpu().item()
                diversity_score = self._calculate_hds(torch.from_numpy(elite_z).to(self.device, self.dtype))
                successful_w = w_candidates_gpu[success_mask]
                mean_w_std = torch.mean(torch.std(successful_w, dim=0)).cpu().item() if successful_w.shape[0] > 1 else 0.0
                normalized_w_std = mean_w_std / self.unconstrained_w_std if self.unconstrained_w_std > 0 else 0.0
                rf_score = self.rf_classifier.score(z_candidates_norm, success_mask.cpu().numpy()) if self.is_rf_trained else 0.0
                pbar.set_description(f"Elite: {len(elite_success)}S/{len(elite_boundary)}B | RF Acc: {rf_score:.2f}")
                pbar.set_postfix(succ=f"{current_success_rate*100:.1f}%", hds=f"{diversity_score:.3f}", w_std_norm=f"{normalized_w_std:.3f}")

                # --- MODIFIED PART: Add visualizer calls ---
                if self.visualizer:
                    # 1. Request an update periodically (non-blocking)
                    if gen % plot_every == 0:
                        self.visualizer.request_update(
                            generation=gen,
                            mean=self.mean,
                            cov=self.cov,
                            z_batch_gpu=z_candidates_gpu, # Use the z-vectors from this generation
                            success_rate=current_success_rate,
                            diversity=diversity_score,
                            w_std_norm=normalized_w_std
                        )
                    # 2. Check for and apply updates on every iteration (non-blocking)
                    # while not self.visualizer.update_plot_if_ready():
                    #     pass
                    self.visualizer.update_plot_if_ready()
        finally:
            # 3. Ensure the background thread is shut down cleanly
            if self.visualizer:
                self.visualizer.shutdown()

        # --- Unchanged final sample generation ... ---
        print(f"\nEvolution complete. Harvesting final samples...")
        final_stable_cov = self.cov + np.eye(self.z_dim, dtype=np.float32) * 1e-6
        final_candidates_z = np.random.multivariate_normal(self.mean, final_stable_cov, size=int(n_to_generate * 3.0)).astype(np.float32)
        _, final_mask, _ = self._calculate_fitness(torch.from_numpy(final_candidates_z).to(self.device, self.dtype))
        successful_z = final_candidates_z[final_mask.cpu().numpy()][:n_to_generate]
        print(f"Successfully generated and filtered {len(successful_z)} Z vectors.")
        
        return successful_z, self.rf_classifier
# ==============================================================================
#                      CONFIGURATION AND EXECUTION
# ==============================================================================

if __name__ == '__main__':
    EVOLUTIONARY_CONFIG = {
        'n_samples_to_generate': 4096,
        'population_size': 4096*2,
        'elite_fraction': 0.5,
        'generations': 350,

        'update_learning_rate': 0.15,
        'initial_variance': 5.0, # High variance to encourage broad initial exploration
        'visualize_live': True,
        'boundary_elite_fraction': 0.5, # 60% of elites will be boundary-seekers
        'plot_every_n_generations': 10, # How often to start a new background calculation
        'image_sample_size': 8,      # Number of sample images to show (e.g., 4 for a 2x2 grid)
        'weight_decay': 0.001,
    }

    TARGET_FILTERS = {
        'trustworthy': {'range': (0, 35)},
        'dominant': {'range': (0, 35)},
    }
    
    # This block would be uncommented and run in an environment where G,
    # ALL_MODELS, and device are properly defined.
    
    sampler = ZSpaceEvolutionarySampler2(
        target_filters=TARGET_FILTERS,
        config=EVOLUTIONARY_CONFIG,
        models=ALL_MODELS,
        G=G,
        device='mps'
    )

    final_z_vectors_np, trained_rf_classifier = sampler.run()
    
    # final_z_vectors_np, trained_rf_classifier = sampler.run()
    print(f"\nShape of final Z vectors: {final_z_vectors_np.shape}")
    print(f"Trained Random Forest Classifier ready: {trained_rf_classifier}")

Parsing target bin from range-based filters...
Target bin defined as: [{'var': 'trustworthy', 'range': (0, 35), 'weight': 1.0}, {'var': 'dominant', 'range': (0, 35), 'weight': 1.0}]


FigureWidget({
    'data': [{'fill': 'toself',
              'fillcolor': 'rgba(0,191,255,0.3)',
              'line': {'color': 'rgba(0,0,0,0)'},
              'name': 'Z Dist',
              'type': 'scatter',
              'uid': 'ee4010dc-5399-475a-9ed6-d0726e8d3f7a',
              'x': [],
              'xaxis': 'x',
              'y': [],
              'yaxis': 'y'},
             {'marker': {'color': 'red', 'size': 10},
              'mode': 'markers',
              'name': 'Mean',
              'type': 'scatter',
              'uid': 'c9304615-d27c-49fe-a3e2-4f8e42cee88a',
              'x': [],
              'xaxis': 'x',
              'y': [],
              'yaxis': 'y'},
             {'type': 'image', 'uid': 'fefcd84a-c834-4c67-a8a8-669768883a83', 'xaxis': 'x2', 'yaxis': 'y2'},
             {'line': {'width': 2},
              'mode': 'lines+markers',
              'name': 'Success %',
              'type': 'scatter',
              'uid': 'b3ced5f2-1297-43af-947f-a09bfdd44a83

Calculating baseline W-space standard deviation...
Baseline (unconstrained) W-space Std. Dev.: 0.4228

Starting evolutionary search...


Elite: 0S/409B | RF Acc: 0.00:   0%|          | 0/350 [00:10<?, ?it/s, hds=0.956, succ=0.0%, w_std_norm=0.000]

0.9129296402066123
0.049425367


...

Elite: 835S/2048B | RF Acc: 0.99:  29%|██▉       | 102/350 [09:28<36:46,  8.90s/it, hds=0.273, succ=10.2%, w_std_norm=1.188]

0.9972461065881637
0.012421982


Elite: 738S/2048B | RF Acc: 0.99:  29%|██▉       | 103/350 [09:33<32:35,  7.92s/it, hds=0.276, succ=9.0%, w_std_norm=1.351] 

0.9971662654054204
0.013900701


Elite: 738S/2048B | RF Acc: 0.99:  30%|██▉       | 104/350 [09:40<30:46,  7.51s/it, hds=0.269, succ=9.0%, w_std_norm=1.297]

In [ ]:
# Re-register the module without torchvision dependency (use pure PIL + PyTorch for resize/normalize)

from __future__ import annotations

import numpy as np
import threading
from concurrent.futures import ThreadPoolExecutor, Future
from typing import Any, Dict, Optional, Tuple

import plotly.graph_objects as go
from plotly.subplots import make_subplots
from IPython.display import display

import torch
import torch.nn as nn
import torch.nn.functional as F

from PIL import Image


# -----------------------------
# Helper: Orthogonal-Scale map B via Householder + diag(scales)
# -----------------------------
class OrthoScale(nn.Module):
    """
    B = Q * diag(exp(log_sigma)), with Q orthogonal from product of Householder reflections.
    We enforce mean(log_sigma) = 0 each forward to fix global scale (ACG invariance).
    """
    def __init__(self, d: int, k_householder: int = 4, dtype=torch.float32, device: Optional[torch.device] = None):
        super().__init__()
        self.d = d
        self.k = k_householder
        self.v = nn.Parameter(torch.randn(k_householder, d, dtype=dtype, device=device) * 0.01)
        self.log_sigma = nn.Parameter(torch.zeros(d, dtype=dtype, device=device))

    def _householder_Q(self) -> torch.Tensor:
        d, k = self.d, self.k
        I = torch.eye(d, device=self.v.device, dtype=self.v.dtype)
        Q = I
        for i in range(k):
            v = self.v[i].unsqueeze(1)                              # [d,1]
            v = v / (v.norm(dim=0, keepdim=True) + 1e-8)           # normalize
            H = I - 2.0 * (v @ v.transpose(0,1))                   # [d,d]
            Q = H @ Q
        return Q

    def forward(self) -> torch.Tensor:
        # return B
        Q = self._householder_Q()
        log_sigma = self.log_sigma - self.log_sigma.mean()         # fix global scale
        S = torch.diag(log_sigma.exp())
        B = Q @ S
        return B


# -----------------------------
# Metrics
# -----------------------------
def wasserstein2_uniform_loss(t: torch.Tensor, a: float, b: float) -> torch.Tensor:
    """
    1D W2^2 between empirical {t} and target Uniform[a,b] via sorted matching.
    """
    t_sorted, _ = torch.sort(t)
    n = t_sorted.numel()
    device = t_sorted.device
    r = torch.linspace(a + (b - a) / (2 * n), b - (b - a) / (2 * n), n, device=device, dtype=t_sorted.dtype)
    return F.mse_loss(t_sorted, r)


def cvm_uniform_loss(t: torch.Tensor, a: float, b: float, num_bins: int = 64) -> torch.Tensor:
    """
    Cramér–von Mises distance to Uniform[a,b] using a histogram approximation (smooth, differentiable through soft histogram).
    """
    device, dtype = t.device, t.dtype
    # normalize to [0,1]
    u = (t - a) / (b - a + 1e-8)
    u = torch.clamp(u, 0.0, 1.0)
    # soft histogram with triangular kernel
    edges = torch.linspace(0, 1, num_bins + 1, device=device, dtype=dtype)
    centers = 0.5 * (edges[:-1] + edges[1:])
    # kernel width = bin spacing
    h = (edges[1] - edges[0]).item()
    # compute weights: triangular kernel
    diffs = (u[:, None] - centers[None, :]).abs()
    weights = torch.clamp(1.0 - diffs / (h + 1e-8), min=0.0)     # [N, B]
    hist = weights.mean(dim=0)                                   # average over samples
    # target uniform density over bins
    target = torch.full_like(hist, 1.0 / num_bins)
    # CVM ~ L2 between CDFs; approx via L2 between histograms' cumulative sums
    cdf_emp = torch.cumsum(hist, dim=0)
    cdf_target = torch.cumsum(target, dim=0)
    return F.mse_loss(cdf_emp, cdf_target)


def fraction_in_range(t: torch.Tensor, a: float, b: float) -> torch.Tensor:
    return (t.ge(a) & t.le(b)).float().mean()


def hds_diversity(z: torch.Tensor) -> torch.Tensor:
    """
    Hyperspherical diversity score on z (post-normalization). z: [N,d]
    """
    if z.shape[0] < 2:
        return torch.tensor(1.0, device=z.device, dtype=z.dtype)
    z_norm = z / (z.norm(p=2, dim=1, keepdim=True) + 1e-8)
    sim = z_norm @ z_norm.t()
    n = sim.shape[0]
    tril = torch.tril(sim, diagonal=-1)
    clump = (tril.pow(2).sum() * 2.0) / (n * (n - 1) + 1e-8)
    return (1.0 - clump.sqrt())


def tensor_to_pil_batch(imgs: torch.Tensor, out_size: int = 384) -> list:
    """
    imgs: [N,C,H,W], range approx [-1,1] or [0,1].
    Resize with F.interpolate, clamp to [0,1], convert to PIL.
    """
    if imgs.ndim != 4:
        raise ValueError("Expected 4D tensor [N,C,H,W]")
    with torch.no_grad():
        N, C, H, W = imgs.shape
        if H != out_size or W != out_size:
            imgs = F.interpolate(imgs, size=(out_size, out_size), mode="bilinear", align_corners=False)
        imgs = torch.clamp((imgs + 1.0) / 2.0, 0.0, 1.0)
        pil_list = []
        for i in range(N):
            arr = (imgs[i].permute(1, 2, 0).cpu().numpy() * 255.0).astype(np.uint8)
            pil_list.append(Image.fromarray(arr))
        return pil_list


# -----------------------------
# Visualizer (async, robust)
# -----------------------------
class AsyncConstantDistVisualizer:
    """
    Non-blocking dashboard for constant-marginal training.
    Left: 2σ ellipse of pre-normalization u = B s (2D slice).
    Top-right: sample image grid.
    Bottom-right: metric curves (W2 loss, CVM loss, coverage %, normalized W-std).
    """
    def __init__(
        self,
        *,
        G: nn.Module,
        device: torch.device,
        z_dim: int,
        sample_size: int = 6,
        title: str = "Constant-Marginal Training (ACG in Z)"
    ) -> None:
        self.G = G.to(device).eval()
        self.device = device
        self.z_dim = z_dim
        self.sample_size = sample_size

        # Concurrency
        self._executor = ThreadPoolExecutor(max_workers=1)
        self._lock = threading.Lock()
        self._future: Optional[Future] = None
        self._latest_payload: Optional[Any] = None

        # History
        self.step_hist, self.w2_hist, self.cvm_hist, self.cov_hist, self.wstd_hist = [], [], [], [], []

        # Figure
        self.fig = go.FigureWidget(make_subplots(
            rows=3, cols=2,
            specs=[
                [{"rowspan": 3}, {"type": "image"}],
                [None, {"rowspan": 2}],
                [None, None],
            ],
            column_widths=[0.66, 0.34],
            row_heights=[0.4, 0.3, 0.3],
            subplot_titles=("Z Pre-Norm Ellipse (u=Bs)", "Representative Samples", "Metrics"),
            vertical_spacing=0.05
        ))
        self._init_static_figure(title)
        display(self.fig)

    def _init_static_figure(self, title: str) -> None:
        for r in range(1, 4):
            self.fig.add_shape(type="circle", xref="x1", yref="y1",
                               x0=-r, y0=-r, x1=r, y1=r,
                               line_color="grey", line_dash="dot",
                               fillcolor="rgba(0,0,0,0)")
        self.fig.add_trace(go.Scatter(x=[], y=[], fill="toself", fillcolor="rgba(0,191,255,0.3)",
                                      name="2σ Covariance", line=dict(color="rgba(0,0,0,0)")), row=1, col=1)
        self.fig.add_trace(go.Image(z=None), row=1, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="W2 Loss", line=dict(width=2)), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="CVM Loss", line=dict(width=2, dash="dash")), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="Coverage %", line=dict(width=2, dash="dot")), row=2, col=2)
        self.fig.add_trace(go.Scatter(mode="lines+markers", name="W-Std (Norm.)", line=dict(width=2)), row=2, col=2)

        self.fig.update_layout(width=2200, height=1050, title_text=title, title_x=0.5, showlegend=True, legend=dict(x=0.67, y=0.6))
        self.fig.update_xaxes(title_text="Z Dim 0", range=[-5, 5], row=1, col=1)
        self.fig.update_yaxes(title_text="Z Dim 1", range=[-5, 5], scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Training Step", row=2, col=2)
        self.fig.update_yaxes(title_text="Metric Value", row=2, col=2)

    def request_update(
        self,
        *,
        step: int,
        B_2x2: np.ndarray,
        z_batch_gpu: torch.Tensor,
        w2_loss: float,
        cvm_loss: float,
        coverage: float,
        w_std_norm: float,
    ) -> None:
        if self._future and not self._future.done():
            return
        self._future = self._executor.submit(
            self._prepare_payload,
            step, B_2x2, z_batch_gpu.detach().clone(),
            w2_loss, cvm_loss, coverage, w_std_norm
        )

    def update_plot_if_ready(self) -> bool:
        payload_to_plot = None
        with self._lock:
            if self._latest_payload is not None:
                payload_to_plot = self._latest_payload
                self._latest_payload = None

        # Propagate exceptions
        if self._future and self._future.done():
            try:
                self._future.result()
            except Exception as e:
                print(f"[Visualizer] Executor exception: {e}")
                raise

        if payload_to_plot is None:
            return self._future is not None and self._future.done()

        (step, w2, cvm, covg, wstd, ellipse_x, ellipse_y, grid_arr) = payload_to_plot

        self.step_hist.append(step)
        self.w2_hist.append(w2)
        self.cvm_hist.append(cvm)
        self.cov_hist.append(covg * 100.0)
        self.wstd_hist.append(wstd)

        with self.fig.batch_update():
            self.fig.data[0].x, self.fig.data[0].y = ellipse_x, ellipse_y
            self.fig.data[1].z = grid_arr
            self.fig.data[2].x, self.fig.data[2].y = self.step_hist, self.w2_hist
            self.fig.data[3].x, self.fig.data[3].y = self.step_hist, self.cvm_hist
            self.fig.data[4].x, self.fig.data[4].y = self.step_hist, self.cov_hist
            self.fig.data[5].x, self.fig.data[5].y = self.step_hist, self.wstd_hist

        return True

    def shutdown(self) -> None:
        self._executor.shutdown()

    # === helpers (background thread) ===
    def _ellipse(self, B_2x2: np.ndarray) -> Tuple[np.ndarray, np.ndarray]:
        # Covariance of u=Bs is Sigma = B B^T
        Sigma = B_2x2 @ B_2x2.T
        vals, vecs = np.linalg.eigh(Sigma)
        vals[vals < 1e-12] = 1e-12
        ang = np.arctan2(vecs[1, 0], vecs[0, 0])
        r = 2.0 * np.sqrt(vals)
        t = np.linspace(0, 2*np.pi, 256)
        ex, ey = r[0]*np.cos(t), r[1]*np.sin(t)
        ell_x = ex*np.cos(ang) - ey*np.sin(ang)
        ell_y = ex*np.sin(ang) + ey*np.cos(ang)
        return ell_x, ell_y

    def _grid(self, z_gpu: torch.Tensor) -> Optional[np.ndarray]:
        try:
            idx = torch.randint(0, z_gpu.shape[0], (min(self.sample_size, z_gpu.shape[0]),), device=z_gpu.device)
            with torch.no_grad():
                ws = self.G.mapping(z_gpu[idx], None)
                imgs_tensor = self.G.synthesis(ws).detach().cpu()
            pil_images = tensor_to_pil_batch(imgs_tensor, out_size=384)
            return np.asarray(self._make_grid(pil_images))
        except Exception as e:
            print(f"[Visualizer] Grid generation failed: {e}")
            return None

    @staticmethod
    def _make_grid(imgs, rows=2):
        if not imgs:
            return None
        w, h = imgs[0].size
        cols = (len(imgs) + rows - 1) // rows
        canvas = Image.new("RGB", (cols * w, rows * h))
        for i, im in enumerate(imgs):
            canvas.paste(im, (i % cols * w, i // cols * h))
        return canvas

    def _prepare_payload(self, step, B_2x2, z_gpu, w2, cvm, covg, wstd):
        ellipse_x, ellipse_y = self._ellipse(B_2x2)
        grid = self._grid(z_gpu)
        with self._lock:
            self._latest_payload = (step, w2, cvm, covg, wstd, ellipse_x, ellipse_y, grid)


# -----------------------------
# Constant-Marginal Trainer (ACG in Z)
# -----------------------------
class ConstantDistributionTrainerACG:
    """
    Learn B so that z' = r_z * (B s / ||B s||), s ~ N(0, I), when passed through G.mapping
    and evaluated by `regressor(w)`, produces f(w) with desired marginal (default: uniform in [a,b]).
    """
    def __init__(
        self,
        *,
        G: nn.Module,
        regressor: nn.Module,
        target_range: Tuple[float, float],
        device: torch.device,
        z_dim: Optional[int] = None,
        k_householder: int = 4,
        r_z: float = 1.0,
        regressor_scale: float = 100.0,     # multiply regressor output by this (e.g., if regressor in [0,1] → [0,100])
        loss_mix: float = 0.5,              # mix W2 and CVM: L = mix*W2 + (1-mix)*CVM
        anisotropy_reg: float = 1e-3,       # L2 on log_sigma
        lr: float = 5e-3,
        visualizer: Optional[AsyncConstantDistVisualizer] = None
    ) -> None:
        self.G = G.to(device).eval()
        self.regressor = regressor.to(device).eval()
        self.device = device
        self.z_dim = z_dim if z_dim is not None else G.mapping.z_dim
        self.r_z = r_z
        self.a, self.b = target_range
        self.regressor_scale = regressor_scale
        self.loss_mix = loss_mix
        self.anisotropy_reg = anisotropy_reg
        self.visualizer = visualizer

        # Learnable ACG map
        self.Bnet = OrthoScale(self.z_dim, k_householder=k_householder, device=device)
        self.opt = torch.optim.Adam(self.Bnet.parameters(), lr=lr, betas=(0.9, 0.99))

        # Baseline W-std (for normalization metric)
        with torch.no_grad():
            z0 = torch.randn(1024, self.z_dim, device=device)
            w0 = self.G.mapping(z0, None)[:, 0]
            self.wstd_baseline = torch.mean(torch.std(w0, dim=0)).item()

    def _sample_z(self, n: int) -> Tuple[torch.Tensor, torch.Tensor]:
        """
        Returns: z'[N,d] (normalized after B), and pre-norm u=Bs for metrics [N,d].
        """
        s = torch.randn(n, self.z_dim, device=self.device)
        B = self.Bnet()                       # [d,d]
        u = s @ B.T                           # [N,d]
        x = u / (u.norm(dim=1, keepdim=True) + 1e-8)
        z = self.r_z * x
        return z, u

    def _forward_batch(self, n: int) -> Dict[str, torch.Tensor]:
        z, u = self._sample_z(n)
        ws = self.G.mapping(z, None)          # [N, num_ws, d]
        w = ws[:, 0]
        t = (self.regressor(w).view(-1) * self.regressor_scale)
        return {"z": z, "u": u, "t": t, "w": w}

    def _loss(self, t: torch.Tensor) -> Tuple[torch.Tensor, Dict[str, float]]:
        w2 = wasserstein2_uniform_loss(t, self.a, self.b)
        cvm = cvm_uniform_loss(t, self.a, self.b)
        # Anisotropy regularization (encourage gentle scales)
        log_sigma = self.Bnet.log_sigma - self.Bnet.log_sigma.mean()
        l_reg = (log_sigma ** 2).mean()
        loss = self.loss_mix * w2 + (1.0 - self.loss_mix) * cvm + self.anisotropy_reg * l_reg
        return loss, {"w2": float(w2.detach().cpu()), "cvm": float(cvm.detach().cpu()), "reg": float(l_reg.detach().cpu())}

    @torch.no_grad()
    def _metrics(self, z: torch.Tensor, t: torch.Tensor, w: torch.Tensor) -> Dict[str, float]:
        covg = float(fraction_in_range(t, self.a, self.b).detach().cpu())
        wstd = float(torch.mean(torch.std(w, dim=0)).detach().cpu())
        wstd_norm = wstd / (self.wstd_baseline + 1e-8)
        div = float(hds_diversity(z).detach().cpu())
        return {"coverage": covg, "wstd_norm": wstd_norm, "diversity": div}

    def train(
        self,
        *,
        steps: int = 2000,
        batch_size: int = 512,
        viz_every: int = 10
    ) -> None:
        for step in range(1, steps + 1):
            out = self._forward_batch(batch_size)
            loss, loss_parts = self._loss(out["t"])
            self.opt.zero_grad(set_to_none=True)
            loss.backward()
            nn.utils.clip_grad_norm_(self.Bnet.parameters(), max_norm=10.0)
            self.opt.step()

            if self.visualizer and (step % viz_every == 0):
                with torch.no_grad():
                    out_v = self._forward_batch(batch_size)
                    mets = self._metrics(out_v["z"], out_v["t"], out_v["w"])
                    B = self.Bnet().detach().cpu().numpy()
                    B_2x2 = B[:2, :2]
                    self.visualizer.request_update(
                        step=step,
                        B_2x2=B_2x2,
                        z_batch_gpu=out_v["z"],
                        w2_loss=loss_parts["w2"],
                        cvm_loss=loss_parts["cvm"],
                        coverage=mets["coverage"],
                        w_std_norm=mets["wstd_norm"],
                    )
                    self.visualizer.update_plot_if_ready()

    @torch.no_grad()
    def sample_z(self, n: int) -> torch.Tensor:
        z, _ = self._sample_z(n)
        return z

    @torch.no_grad()
    def current_B(self) -> torch.Tensor:
        return self.Bnet()

In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from IPython.display import display, clear_output
import torch
from concurrent.futures import ThreadPoolExecutor
import threading
from typing import Any, List, Dict, Tuple
from PIL import Image
from torchvision.transforms import Compose, Resize
import torchvision.transforms.functional as TF


class MeanDiscoveryVisualizer:
    """Visualizer for Phase 1: Finding the category's central direction."""

    def __init__(self, z_dim: int = 512):
        self.z_dim = z_dim
        self.fig = go.FigureWidget(make_subplots(
            rows=1, cols=2,
            subplot_titles=("Z-Space Mean Trajectory", "Best Fitness per Generation"),
            column_widths=[0.5, 0.5]
        ))
        self._init_figure()
        self.mean_history = []
        self.fitness_history = []
        self.generation_history = []
        display(self.fig)

    def _init_figure(self):
        # Left plot: Z-space
        for i in range(1, 4):
            self.fig.add_shape(type="circle", xref="x1", yref="y1", x0=-i, y0=-i, x1=i, y1=i, line_color="grey", line_dash="dot", fillcolor="rgba(0,0,0,0)")
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines+markers', name='Mean Path', line=dict(color='orange')), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='markers', name='Current Mean', marker=dict(color='red', size=12)), row=1, col=1)

        # Right plot: Fitness
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines+markers', name='Best Fitness', line=dict(color='green')), row=1, col=2)

        self.fig.update_layout(title_text="Phase 1: Mean Discovery", title_x=0.5, height=500, showlegend=False)
        self.fig.update_xaxes(title_text="Z Dim 0", range=[-5, 5], row=1, col=1)
        self.fig.update_yaxes(title_text="Z Dim 1", range=[-5, 5], scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Generation", row=1, col=2)
        self.fig.update_yaxes(title_text="Fitness (Lower is Better)", type="log", row=1, col=2)

    def update(self, generation: int, mean_vec: np.ndarray, best_fitness: float):
        self.generation_history.append(generation)
        self.mean_history.append(mean_vec[:2].copy())
        self.fitness_history.append(best_fitness)

        mean_path_x, mean_path_y = zip(*self.mean_history)

        with self.fig.batch_update():
            self.fig.data[0].x = mean_path_x
            self.fig.data[0].y = mean_path_y
            self.fig.data[1].x = [mean_vec[0]]
            self.fig.data[1].y = [mean_vec[1]]
            self.fig.data[2].x = self.generation_history
            self.fig.data[2].y = self.fitness_history




class BoundarySeekerVisualizer:
    """Visualizer for Phase 2: Modeling the boundary in Parameter Space."""

    def __init__(self, p_dim: int = 511):
        self.p_dim = p_dim
        self.fig = go.FigureWidget(make_subplots(
            rows=2, cols=2,
            specs=[[{"rowspan": 2}, {}], [None, {}]],
            subplot_titles=(
                f"Parameter Space (Dims 0 & 1 of {p_dim})",
                "Optimization Metrics",
                "Sample Images from Distribution"
            ),
            column_widths=[0.6, 0.4],
            vertical_spacing=0.1
        ))
        self._init_figure()
        self.history = {'gen': [], 'log_det': [], 'fail_rate': [], 'coverage_loss': []}
        display(self.fig)

    def _init_figure(self):
        # Left plot: Parameter space
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='markers', name='Reference Samples', marker=dict(color='rgba(0, 0, 255, 0.4)', symbol='x')), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], fill="toself", fillcolor='rgba(255,165,0,0.3)', line=dict(color='rgba(0,0,0,0)'), name='2σ Covariance'), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='markers', name='Mean', marker=dict(color='red', size=10)), row=1, col=1)

        # Right top plot: Metrics
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines', name='Log(det(Σ))', line=dict(color='blue')), row=1, col=2)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines', name='Failure Rate (%)', line=dict(color='red')), row=1, col=2)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines', name='Coverage Loss', line=dict(color='green')), row=1, col=2)

        # Right bottom plot: Images
        self.fig.add_trace(go.Image(z=None), row=2, col=2)

        self.fig.update_layout(title_text="Phase 2: Boundary Modeling (in Parameter Space)", title_x=0.5, height=800, legend=dict(x=0.61, y=0.98))
        self.fig.update_xaxes(title_text="P Dim 0", range=[-1.5, 1.5], row=1, col=1)
        self.fig.update_yaxes(title_text="P Dim 1", range=[-1.5, 1.5], scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Generation", row=1, col=2)

    def update(self, generation: int, metrics: Dict, p_mean: np.ndarray, p_cov: np.ndarray, p_ref_samples: np.ndarray, image_grid: np.ndarray):
        self.history['gen'].append(generation)
        for key in ['log_det', 'fail_rate', 'coverage_loss']:
            self.history[key].append(metrics.get(key, np.nan))

        # Calculate ellipse for the parameter space covariance
        mean_2d, cov_2d = p_mean[:2], p_cov[:2, :2]
        eigenvalues, eigenvectors = np.linalg.eigh(cov_2d)
        eigenvalues[eigenvalues < 0] = 1e-9
        angle = np.arctan2(eigenvectors[1, 0], eigenvectors[0, 0])
        radii = 2 * np.sqrt(eigenvalues)
        t = np.linspace(0, 2 * np.pi, 100)
        ellipse_x_raw, ellipse_y_raw = radii[0] * np.cos(t), radii[1] * np.sin(t)
        ellipse_x = mean_2d[0] + (ellipse_x_raw * np.cos(angle) - ellipse_y_raw * np.sin(angle))
        ellipse_y = mean_2d[1] + (ellipse_x_raw * np.sin(angle) + ellipse_y_raw * np.cos(angle))

        with self.fig.batch_update():
            # Parameter space plot
            self.fig.data[0].x = p_ref_samples[:, 0]
            self.fig.data[0].y = p_ref_samples[:, 1]
            self.fig.data[1].x, self.fig.data[1].y = ellipse_x, ellipse_y
            self.fig.data[2].x, self.fig.data[2].y = [mean_2d[0]], [mean_2d[1]]

            # Metrics plot
            self.fig.data[3].x = self.history['gen']
            self.fig.data[3].y = self.history['log_det']
            self.fig.data[4].x = self.history['gen']
            self.fig.data[4].y = [h * 100 for h in self.history['fail_rate']] # as percentage
            self.fig.data[5].x = self.history['gen']
            self.fig.data[5].y = self.history['coverage_loss']
            
            # Image Grid
            self.fig.data[6].z = image_grid

In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from IPython.display import display, clear_output
import torch
from concurrent.futures import ThreadPoolExecutor
import threading
from typing import Any, List, Dict, Tuple
from PIL import Image
from torchvision.transforms import Compose, Resize
import torchvision.transforms.functional as TF
from scipy.special import softmax
from tqdm.notebook import tqdm
from sklearn.decomposition import PCA

# --- Visualizer and Parameterization classes remain the same ---

class MeanDiscoveryVisualizer:
    """Visualizer for Phase 1: Finding the category's central direction."""
    def __init__(self, z_dim: int = 512):
        self.z_dim = z_dim
        self.fig = go.FigureWidget(make_subplots(
            rows=1, cols=2,
            subplot_titles=("Z-Space Mean Trajectory", "Best Fitness per Generation"),
            column_widths=[0.5, 0.5]
        ))
        self._init_figure()
        self.mean_history = []
        self.fitness_history = []
        self.generation_history = []
        display(self.fig)

    def _init_figure(self):
        for i in range(1, 4):
            self.fig.add_shape(type="circle", xref="x1", yref="y1", x0=-i, y0=-i, x1=i, y1=i, line_color="grey", line_dash="dot", fillcolor="rgba(0,0,0,0)")
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines+markers', name='Mean Path', line=dict(color='orange')), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='markers', name='Current Mean', marker=dict(color='red', size=12)), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines+markers', name='Best Fitness', line=dict(color='green')), row=1, col=2)
        self.fig.update_layout(title_text="Phase 1: Mean Discovery", title_x=0.5, height=500, showlegend=False)
        self.fig.update_xaxes(title_text="Z Dim 0", range=[-5, 5], row=1, col=1)
        self.fig.update_yaxes(title_text="Z Dim 1", range=[-5, 5], scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Generation", row=1, col=2)
        self.fig.update_yaxes(title_text="Fitness (Lower is Better)", type="log", row=1, col=2)

    def update(self, generation: int, mean_vec: np.ndarray, best_fitness: float):
        self.generation_history.append(generation)
        self.mean_history.append(mean_vec[:2].copy())
        self.fitness_history.append(best_fitness)
        mean_path_x, mean_path_y = zip(*self.mean_history) if self.mean_history else ([], [])
        with self.fig.batch_update():
            self.fig.data[0].x, self.fig.data[0].y = mean_path_x, mean_path_y
            self.fig.data[1].x, self.fig.data[1].y = [mean_vec[0]], [mean_vec[1]]
            self.fig.data[2].x, self.fig.data[2].y = self.generation_history, self.fitness_history

class BoundarySeekerVisualizer:
    """Visualizer for Phase 2: Plots the ellipsoid, samples, and eigenvalue spectrum."""
    def __init__(self, p_dim: int = 511):
        self.p_dim = p_dim
        self.fig = go.FigureWidget(make_subplots(
            rows=2, cols=2,
            subplot_titles=(f"Parameter Space Projection", "Failure Eigenvalue Spectrum", "Ellipsoid Volume & Failure Rate"),
            specs=[[{"rowspan": 2}, {}], [None, {"secondary_y": True}]],
            vertical_spacing=0.15
        ))
        self._init_figure()
        self.history = {'gen': [], 'log_det': [], 'fail_rate': []}
        display(self.fig)

    def _init_figure(self):
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines', name='Ellipsoid Boundary', line=dict(color='orange', width=2)), row=1, col=1)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='markers', name='Failed Samples', marker=dict(color='red', size=5, opacity=0.5)), row=1, col=1)
        
        self.fig.add_trace(go.Bar(x=[], y=[], name='Eigenvalues'), row=1, col=2)
        
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines', name='Log Volume', line=dict(color='blue')), row=2, col=2)
        self.fig.add_trace(go.Scatter(x=[], y=[], mode='lines', name='Failure Rate', line=dict(color='red', dash='dot')), secondary_y=True, row=2, col=2)
        
        self.fig.update_layout(
            title_text="Phase 2: Failure-Driven Boundary Search", title_x=0.5, height=700, showlegend=False,
            yaxis4=dict(title="Failure Rate (%)", overlaying="y3", side="right", range=[0, 100])
        )
        self.fig.update_xaxes(title_text="Dim 0", row=1, col=1)
        self.fig.update_yaxes(title_text="Dim 1", scaleanchor="x1", scaleratio=1, row=1, col=1)
        self.fig.update_xaxes(title_text="Eigenvalue Index", row=1, col=2)
        self.fig.update_yaxes(title_text="Eigenvalue", type="log", row=1, col=2)
        self.fig.update_xaxes(title_text="Generation", row=2, col=2)
        self.fig.update_yaxes(title_text="Log Det(Cov)", row=2, col=2)

    def update(self, generation: int, p_cov: np.ndarray, p_fail_proj: np.ndarray, p_ellipsoid_proj: np.ndarray, fail_rate: float, fail_eigenvalues: np.ndarray, viz_dims_info: str):
        self.history['gen'].append(generation)
        log_det = np.linalg.slogdet(p_cov)[1]
        self.history['log_det'].append(log_det)
        self.history['fail_rate'].append(fail_rate * 100)

        with self.fig.batch_update():
            # Update ellipsoid boundary and sample scatters
            self.fig.data[0].x, self.fig.data[0].y = p_ellipsoid_proj[:, 0], p_ellipsoid_proj[:, 1]
            self.fig.data[1].x = p_fail_proj[:, 0] if p_fail_proj.ndim == 2 and p_fail_proj.shape[0] > 0 else []
            self.fig.data[1].y = p_fail_proj[:, 1] if p_fail_proj.ndim == 2 and p_fail_proj.shape[0] > 0 else []
            
            # Update eigenvalue spectrum
            if fail_eigenvalues is not None:
                self.fig.data[2].x = list(range(len(fail_eigenvalues)))
                self.fig.data[2].y = fail_eigenvalues
            
            # Update metric plots
            self.fig.data[3].x, self.fig.data[3].y = self.history['gen'], self.history['log_det']
            self.fig.data[4].x, self.fig.data[4].y = self.history['gen'], self.history['fail_rate']

            # Dynamically update axis titles and ranges
            self.fig.update_xaxes(title_text=f"Projection Dim 1 ({viz_dims_info})", row=1, col=1)
            self.fig.update_yaxes(title_text=f"Projection Dim 2 ({viz_dims_info})", row=1, col=1)
            
            max_range = np.max(np.abs(p_ellipsoid_proj)) * 1.2 if p_ellipsoid_proj.size > 0 else 0.1
            min_range = 0.01
            final_range = max(max_range, min_range)
            self.fig.update_xaxes(range=[-final_range, final_range], row=1, col=1)
            self.fig.update_yaxes(range=[-final_range, final_range], row=1, col=1)

class Parameterization:
    # This class is assumed to be the final, correct version from previous steps
    def __init__(self, center_vec: np.ndarray):
        self.z_dim = center_vec.shape[0]
        self.p_dim = self.z_dim - 1
        self.north_pole = np.zeros(self.z_dim, dtype=np.float32); self.north_pole[-1] = 1.0
        self.rotation = self._get_rotation_matrix(center_vec); self.inv_rotation = self.rotation.T
    def _get_rotation_matrix(self, v_to: np.ndarray) -> np.ndarray:
        v_from = self.north_pole; v_to_unit = v_to / np.linalg.norm(v_to)
        if np.allclose(v_from, v_to_unit): return np.eye(self.z_dim, dtype=np.float32)
        if np.allclose(v_from, -v_to_unit): R = -np.eye(self.z_dim, dtype=np.float32); R[0, 0] = 1.0; return R
        u = v_from + v_to_unit; u /= np.linalg.norm(u)
        H1 = np.eye(self.z_dim) - 2 * np.outer(u, u); H2 = np.eye(self.z_dim) - 2 * np.outer(v_to_unit, v_to_unit)
        return H2 @ H1
    def map_to_z_space(self, p_vectors: np.ndarray) -> np.ndarray:
        p_vectors = np.atleast_2d(p_vectors)
        polydisk_pts = self._square_to_disk_nd(p_vectors)
        scale_factor = 2.0 / (np.sqrt(self.p_dim / 2.0) + 1e-9)
        disk_pts = polydisk_pts * scale_factor
        hemisphere_pts_aligned = self._inverse_laea_projection(disk_pts)
        return hemisphere_pts_aligned @ self.inv_rotation
    def map_to_parameter_space(self, z_vectors: np.ndarray) -> np.ndarray:
        z_vectors = np.atleast_2d(z_vectors); aligned_z = z_vectors @ self.rotation
        disk_pts = self._laea_projection(aligned_z)
        scale_factor = 2.0 / (np.sqrt(self.p_dim / 2.0) + 1e-9); polydisk_pts = disk_pts / scale_factor
        return self._disk_to_square_nd(polydisk_pts)
    def _laea_projection(self, z_aligned: np.ndarray) -> np.ndarray:
        scale = np.sqrt(2 / (1 + z_aligned[:, -1] + 1e-9)); return z_aligned[:, :-1] * scale[:, np.newaxis]
    def _inverse_laea_projection(self, disk_pts: np.ndarray) -> np.ndarray:
        norm_sq = np.sum(disk_pts**2, axis=1); norm_sq = np.clip(norm_sq, 0, 4)
        z = np.zeros((disk_pts.shape[0], self.z_dim), dtype=np.float32)
        with np.errstate(invalid='ignore'): z[:, :-1] = disk_pts * (np.sqrt(1 - norm_sq / 4))[:, np.newaxis]
        z[:, -1] = 1 - norm_sq / 2; return z
    def _square_to_disk_nd(self, points: np.ndarray) -> np.ndarray:
        out_pts = np.copy(points)
        for i in range(0, self.p_dim - (self.p_dim % 2), 2):
            x, y = points[:, i], points[:, i+1]; r, theta = np.zeros_like(x), np.zeros_like(x)
            mask = np.abs(x) > np.abs(y); r[mask] = x[mask]
            with np.errstate(divide='ignore', invalid='ignore'): theta[mask] = (np.pi / 4.0) * (y[mask] / x[mask])
            r[~mask] = y[~mask]
            with np.errstate(divide='ignore', invalid='ignore'): theta[~mask] = (np.pi / 2.0) - (np.pi / 4.0) * (x[~mask] / y[~mask])
            origin_mask = (np.abs(x) < 1e-9) & (np.abs(y) < 1e-9); theta[origin_mask] = 0
            out_pts[:, i], out_pts[:, i+1] = r * np.cos(theta), r * np.sin(theta)
        return out_pts
    def _disk_to_square_nd(self, points: np.ndarray) -> np.ndarray:
        out_pts = np.copy(points)
        for i in range(0, self.p_dim - (self.p_dim % 2), 2):
            disk_x, disk_y = points[:, i], points[:, i+1]
            r, phi = np.sqrt(disk_x**2 + disk_y**2), np.arctan2(disk_y, disk_x)
            square_u, square_v = np.zeros_like(r), np.zeros_like(r)
            mask_u_dom = (disk_x**2 >= disk_y**2)
            r_u, disk_x_u = r[mask_u_dom], disk_x[mask_u_dom]
            u_u = r_u * np.sign(disk_x_u); u_u[disk_x_u == 0] = 0
            with np.errstate(divide='ignore', invalid='ignore'): v_u = u_u * (4/np.pi) * np.arctan(disk_y[mask_u_dom] / disk_x_u)
            v_u[disk_x_u == 0] = 0; square_u[mask_u_dom], square_v[mask_u_dom] = u_u, v_u
            mask_v_dom = ~mask_u_dom
            r_v, disk_y_v = r[mask_v_dom], disk_y[mask_v_dom]
            v_v = r_v * np.sign(disk_y_v); v_v[disk_y_v == 0] = 0
            with np.errstate(divide='ignore', invalid='ignore'): u_v = v_v * (4/np.pi) * np.arctan(disk_x[mask_v_dom] / disk_y_v)
            u_v[disk_y_v == 0] = 0; square_u[mask_v_dom], square_v[mask_v_dom] = u_v, v_v
            out_pts[:, i], out_pts[:, i+1] = square_u, square_v
        return out_pts

class GeometricBoundarySeeker:
    """
    Finds the boundary of a category in Z-space using a two-phase geometric approach.
    """
    def __init__(self, target_filters: Dict, config: Dict, G: torch.nn.Module, models: Dict, device: torch.device):
        self.config = config; self.G = G.to(device); self.models = {name: model.to(device) for name, model in models.items()}
        self.device = device; self.z_dim = G.mapping.z_dim; self.p_dim = self.z_dim - 1
        self.target_bin = self._parse_filters(target_filters); self.dtype = torch.float32

    def _parse_filters(self, filters: Dict) -> List[Dict]:
        return [{'var': var, 'range': cond['range']} for var, cond in filters.items()]
    
    @torch.no_grad()
    def _calculate_fitness(self, z_batch_gpu: torch.Tensor) -> Tuple[torch.Tensor, torch.Tensor]:
        w_batch = self.G.mapping(z_batch_gpu, None)
        w_batch = w_batch[:, 0] if w_batch.ndim == 3 else w_batch
        final_mask = torch.full((w_batch.shape[0],), True, device=self.device)
        compliance_loss = torch.zeros(w_batch.shape[0], device=self.device)
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1) * 100
            final_mask &= (preds >= low) & (preds <= high)
            dist_low = torch.clamp(low - preds, min=0)
            dist_high = torch.clamp(preds - high, min=0)
            compliance_loss += dist_low + dist_high
        
        return compliance_loss, final_mask


    def find_category_center(self) -> np.ndarray:
        """Phase 1: Find the mean direction vector."""
        print("--- Starting Phase 1: Mean Discovery ---")
        cfg = self.config['phase1']
        mean = np.zeros(self.z_dim, dtype=np.float32)
        cov = np.eye(self.z_dim, dtype=np.float32) * cfg['initial_variance']
        vis = MeanDiscoveryVisualizer(self.z_dim)
        det = np.linalg.slogdet(cov)[1]
        successes = []
        success_n=0
        init_lr = 0.5
        pbar = tqdm(range(cfg['generations']), desc="Phase 1")
        for gen in pbar:
            z_cpu = np.random.multivariate_normal(mean, cov*np.cos(gen/cfg['generations']*np.pi*5)**2*(1-gen/cfg['generations'])**0.5, cfg['population_size']).astype(np.float32)
            z_gpu = torch.from_numpy(z_cpu).to(self.device, self.dtype)
            fitness, _ = self._calculate_fitness(z_gpu)
            fitness_np = fitness.cpu().numpy()
            
            elite_indices = np.argsort(fitness_np)[:cfg['elite_size']]
            lr = init_lr * (1 - (gen)/(cfg['generations']))
            if sum(fitness_np==0)<100:
                new_mean = np.mean(z_cpu[elite_indices], axis=0)
                mean = (1 - lr) * mean + lr * new_mean
            else:
                new_mean =np.mean(z_cpu[fitness_np==0], axis=0)
                mean = (1 - lr) * mean + lr * new_mean
                successes.append(z_cpu[fitness_np==0])
                success_n+=sum(fitness_np==0)
            mean = mean*0.99
            
            if success_n>1000:
                new_cov = np.cov(np.concatenate(successes)-mean.reshape(1,-1), rowvar=False)
                print(np.linalg.slogdet(new_cov)[1])
                cov = (1 - init_lr) * cov + init_lr * new_cov
                cov = (cov + cov.T) / 2.0
                cov = cov*0.999+np.eye(self.z_dim, dtype=np.float32)*2e-3
                det =np.linalg.slogdet(cov)[1]
                if det<100 and sum(fitness_np==0)>100:
                    cov = cov*1.0001
                if sum(fitness_np==1)==0:
                    cov = cov*1.0001
            best_fitness_val = fitness_np.mean()
            fitness, _ = self._calculate_fitness(torch.from_numpy(mean).to(self.device, self.dtype).unsqueeze(0))
            mean_fitness = fitness.cpu().numpy().mean()

            pbar.set_postfix(passed_fraction=f"{sum(fitness_np==0)/cfg['population_size']:.2f}", mean_norm=f"{np.linalg.norm(mean):.2f} mean_fitness={mean_fitness:.2f} cov_logdet={det:.2f} success_n={success_n}")
            if gen % 5 == 0:
                vis.update(gen, mean, best_fitness_val)
        
        mu_center = mean 
        print(f"--- Phase 1 Complete. Found center vector. ---")
        return mu_center, cov


    def find_boundary_distribution(self, mu_center: np.ndarray) -> Tuple[np.ndarray, np.ndarray]:
        """Phase 2: Geometrically grow an ellipsoid using a failure-driven approach."""
        print("\n--- Starting Phase 2: Failure-Driven Boundary Modeling ---")
        cfg = self.config['phase2']
        param = Parameterization(mu_center)
        vis = BoundarySeekerVisualizer(self.p_dim)

        p_mean = np.zeros(self.p_dim)
        zero_mean = np.zeros(self.p_dim)
        p_cov = np.eye(self.p_dim) * cfg['initial_variance']
        
        pca = None
        fail_T_momentum = None
        fail_mean_momentum = None
        pbar = tqdm(range(cfg['generations']), desc="Phase 2 (Failure-Driven)")
        p_fail_cache = []
        for gen in pbar:
            p_gauss = np.random.multivariate_normal(zero_mean, p_cov, cfg['population_size'])
            radii = 1-np.abs(np.random.randn(cfg['population_size'])*0.01)
            p_samples = p_mean + (p_gauss * (radii[:, np.newaxis] / (np.linalg.norm(p_gauss, axis=1, keepdims=True) + 1e-9)))@p_cov
            p_samples = np.clip(p_samples, -0.999, 0.999)
            z_samples = param.map_to_z_space(p_samples)
            z_samples_gpu = torch.from_numpy(z_samples).to(self.device, self.dtype)
            _, success_mask = self._calculate_fitness(z_samples_gpu)
            success_mask = success_mask.cpu().numpy() 
            
            p_fail = p_samples[~success_mask]
            fail_rate = len(p_fail) / cfg['population_size']
            
            fail_eigenvalues = None
            det = np.linalg.slogdet(p_cov)[1]
            if fail_rate < cfg['target_failure_rate_range'][0]:
                p_cov *= cfg['expansion_factor']
                pca = None
            elif fail_rate > cfg['target_failure_rate_range'][1] or (np.abs(p_samples)>1).mean()>0.001:
                 p_cov *= cfg['shrink_factor']
                 pca = None
            else:
                if len(p_fail) > self.p_dim:
                    # p_fail = np.concatenate([p_fail, p_samples[(np.abs(p_samples)>1).mean(axis=1)>0.0]])
                    p_fail_cache.append(p_fail)
                    p_fail = np.concatenate(p_fail_cache)
                    if len(p_fail) > 6:
                        p_fail_cache = p_fail_cache[1:]
                    fail_cov = np.cov(p_fail, rowvar=False)

                    p_fail_mean = np.mean(p_fail, axis=0)
                    fail_eigenvalues, fail_eigenvectors = np.linalg.eigh(fail_cov)
                    regular_eigenvalues, regular_eigenvectors = np.linalg.eigh(p_cov)
                    target_eigenvalue = regular_eigenvalues/np.mean(regular_eigenvalues)*np.mean(fail_eigenvalues)*1.001

                    scaling_factors = np.sqrt(target_eigenvalue / (fail_eigenvalues + 1e-9))
                    S = np.diag(scaling_factors)
                    
                    # Transformation matrix in the standard basis
                    T = fail_eigenvectors @ S @ fail_eigenvectors.T
                    if fail_T_momentum is None:
                        fail_T_momentum = T
                        fail_mean_momentum = p_fail_mean/512
                    else:
                        fail_T_momentum = (1 - 0.5) * fail_T_momentum + 0.5 * T
                        fail_mean_momentum = (1 - 0.5) * fail_mean_momentum + 0.5 * p_fail_mean
                        T = fail_T_momentum
                        p_fail_mean = fail_mean_momentum*0.999
                    
                    p_cov_new = T @ p_cov @ T.T
                    lr = cfg['learning_rate'] * (1 - gen/cfg['generations'])**0.5
                    p_cov = (1 - lr) * p_cov + lr * p_cov_new
                    p_mean = (1 - lr/10) * p_mean - lr/10 * p_fail_mean
                else:
                    p_cov *= cfg['expansion_factor'] # Not enough points for stable cov, expand
                    pca = None

            p_cov = (p_cov + p_cov.T) / 2.0
            if det<1100:
                p_cov = p_cov*1.0001
            pbar.set_postfix(fail_rate=f"{fail_rate*100:.1f}%", vol=f"{det:.2f} wrong={(np.abs(p_samples)>1).mean():.2f} {np.abs(p_samples).max():.2f} mean={np.linalg.norm(p_mean):.2f}")

            if gen % 5 == 0:
                if pca is None and len(p_fail) > 2:
                    pca_viz = PCA(n_components=2).fit(p_fail)
                else:
                    pca_viz = pca
                
                if pca_viz is not None:
                    proj_basis = pca_viz.components_[:2, :].T
                    p_cov_proj = proj_basis.T @ p_cov @ proj_basis
                    p_fail_proj = p_fail @ proj_basis
                    viz_dims_info = "PCA"
                else:
                    proj_basis = np.eye(self.p_dim, 2)
                    p_cov_proj = p_cov[np.ix_([0, 1], [0, 1])]
                    p_fail_proj = p_fail[:, :2] if p_fail.shape[0] > 0 else p_fail
                    viz_dims_info = "Default"
                
                # Project ellipsoid surface for visualization
                p_sphere = np.random.randn(200, self.p_dim)
                p_sphere /= np.linalg.norm(p_sphere, axis=1, keepdims=True)
                try: L = np.linalg.cholesky(p_cov)
                except np.linalg.LinAlgError:
                    eigvals, eigvecs = np.linalg.eigh(p_cov)
                    L = eigvecs @ np.diag(np.sqrt(np.maximum(eigvals, 0)))
                p_surface = (L @ p_sphere.T).T
                p_ellipsoid_proj = p_surface @ proj_basis

                vis.update(gen, p_cov, p_fail_proj, p_ellipsoid_proj, fail_rate, fail_eigenvalues, viz_dims_info)

        print(f"--- Phase 2 Complete ---")
        return p_mean, p_cov

    
    # Dummy classes for demonstration
    # device = 'mps'
    # CONFIG = {
    #     'phase1': { 'generations': 50, 'population_size': 2048, 'elite_size': 128, 'initial_variance': 1.0, 'learning_rate': 0.3 },
    #     'phase2': {
    #         'generations': 100,
    #         'population_size': 4096,
    #         'initial_variance': 1e-4,
    #         'learning_rate': 0.1,
    #         'shrink_factor': 0.99999,   # Less aggressive shrinking
    #         'expansion_factor': 1e-8 # Small constant outward push
    #     }
    # }
    # TARGET_FILTERS = { 'gender': {'range': (90, 100)}, 'age': {'range': (85, 100)} }


CONFIG = {
    'phase1': { 'generations':1000, 'population_size': 4096, 'elite_size': 256, 'initial_variance': 5., 'learning_rate': 0.5 },
    'phase2': {
        'generations': 1000,
        'population_size': 4096*5,
        'initial_variance': 20e-1,
        'learning_rate': 0.15,§
        'target_failure_rate_range': (0.25, 0.6), # Aim for 15-30% failures
        'expansion_factor': 1.001,
        'shrink_factor': 0.99,
    }
}
TARGET_FILTERS = { 'gender': {'range': (90, 100)}, 'age': {'range': (85, 100)} }

seeker = GeometricBoundarySeeker(target_filters=TARGET_FILTERS, config=CONFIG, G=G, models=ALL_MODELS, device=device)
center_vector = seeker.find_category_center()
final_p_mean, final_p_cov = seeker.find_boundary_distribution(center_vector)


--- Starting Phase 1: Mean Discovery ---


FigureWidget({
    'data': [{'line': {'color': 'orange'},
              'mode': 'lines+markers',
              'name': 'Mean Path',
              'type': 'scatter',
              'uid': '5988582d-7520-4dfe-9b1b-9d5763d8fccd',
              'x': [],
              'xaxis': 'x',
              'y': [],
              'yaxis': 'y'},
             {'marker': {'color': 'red', 'size': 12},
              'mode': 'markers',
              'name': 'Current Mean',
              'type': 'scatter',
              'uid': '35d6be8b-07bd-4599-8861-cd802abab798',
              'x': [],
              'xaxis': 'x',
              'y': [],
              'yaxis': 'y'},
             {'line': {'color': 'green'},
              'mode': 'lines+markers',
              'name': 'Best Fitness',
              'type': 'scatter',
              'uid': '40b41d15-88b1-4df3-ba2e-863273fe74c5',
              'x': [],
              'xaxis': 'x2',
              'y': [],
              'yaxis': 'y2'}],
    'layout': {'annotations': 

Phase 1:   0%|          | 0/1000 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [ ]:
rs = []
with torch.no_grad():
    for i in tqdm(range(100)):
        r = (ALL_MODELS['trustworthy'](sample_w(1_000,0.6)))*100
        rs.append(r.cpu().numpy().flatten())

plt.hist(np.concatenate(rs), bins=100)
plt.show()









In [ ]:
import numpy as np

class Parameterization:
    """
    Handles the rigorous, area-preserving mapping from a hypercube
    parameter space to a target hemisphere in a higher-dimensional space.
    """
    def __init__(self, center_vec: np.ndarray, accuracy_threshold: float = 1e-9):
        """
        Initializes the parameterization with a target direction vector.

        Args:
            center_vec (np.ndarray): A 1D array representing the target direction
                                     in the z_dim space. It will be normalized.
            accuracy_threshold (float): The L2 norm below which mappings are treated
                                        as linear to improve accuracy around the origin.
        """
        self.z_dim = center_vec.shape[0]
        self.p_dim = self.z_dim - 1
        self.north_pole = np.zeros(self.z_dim, dtype=np.float32)
        self.north_pole[-1] = 1.0
        self.rotation = self._get_rotation_matrix(center_vec)
        self.inv_rotation = self.rotation.T
        self.threshold = accuracy_threshold

    def _get_rotation_matrix(self, v_to: np.ndarray) -> np.ndarray:
        """
        Computes the rotation matrix that aligns the north pole to v_to.
        This uses the robust Householder reflection method for N-D vectors.
        """
        v_from = self.north_pole
        v_to_unit = v_to / np.linalg.norm(v_to)

        if np.allclose(v_from, v_to_unit):
            return np.eye(self.z_dim, dtype=np.float32)
        if np.allclose(v_from, -v_to_unit):
            R = -np.eye(self.z_dim, dtype=np.float32)
            R[0, 0] = 1.0  # Ensure determinant is +1 for a valid rotation
            return R

        # Intermediate vector for the first reflection
        u = v_from + v_to_unit
        u /= np.linalg.norm(u)

        # Reflector H1 maps v_from to -v_to_unit
        H1 = np.eye(self.z_dim) - 2 * np.outer(u, u)
        # Reflector H2 maps -v_to_unit to v_to_unit
        H2 = np.eye(self.z_dim) - 2 * np.outer(v_to_unit, v_to_unit)
        
        # The rotation is the composition of the two reflections
        return H2 @ H1

    def map_to_z_space(self, p_vectors: np.ndarray) -> np.ndarray:
        """Maps (N, p_dim) in parameter space cube to (N, z_dim) on hemisphere."""
        p_vectors = np.atleast_2d(p_vectors)
        polydisk_pts = self._square_to_disk_nd(p_vectors)
        
        scale_factor = 2.0 / (np.sqrt(self.p_dim / 2.0) + 1e-9)
        disk_pts = polydisk_pts * scale_factor
        
        hemisphere_pts_aligned = self._inverse_laea_projection(disk_pts)
        
        return hemisphere_pts_aligned @ self.inv_rotation

    def map_to_parameter_space(self, z_vectors: np.ndarray) -> np.ndarray:
        """Maps (N, z_dim) on hemisphere to (N, p_dim) in parameter space cube."""
        z_vectors = np.atleast_2d(z_vectors)
        
        aligned_z = z_vectors @ self.rotation
        disk_pts = self._laea_projection(aligned_z)
        
        scale_factor = 2.0 / (np.sqrt(self.p_dim / 2.0) + 1e-9)
        polydisk_pts = disk_pts / scale_factor
        
        return self._disk_to_square_nd(polydisk_pts)

    def _laea_projection(self, z_aligned: np.ndarray) -> np.ndarray:
        """Projects from standard hemisphere to the p-dimensional unit ball."""
        scale = np.sqrt(2 / (1 + z_aligned[:, -1] + 1e-9))
        return z_aligned[:, :-1] * scale[:, np.newaxis]

    def _inverse_laea_projection(self, disk_pts: np.ndarray) -> np.ndarray:
        """Projects from the p-dimensional unit ball to standard hemisphere."""
        norm_sq = np.sum(disk_pts**2, axis=1)
        norm_sq = np.clip(norm_sq, 0, 4)
        z = np.zeros((disk_pts.shape[0], self.z_dim), dtype=np.float32)
        with np.errstate(invalid='ignore'): # Ignore sqrt of negative for zero-norm points
             z[:, :-1] = disk_pts * (np.sqrt(1 - norm_sq / 4))[:, np.newaxis]
        z[:, -1] = 1 - norm_sq / 2
        return z

    def _square_to_disk_nd(self, points: np.ndarray) -> np.ndarray:
        """
        Maps a p-dim hypercube to a product of 2D disks by applying the
        Shirley-Chiu mapping to sequential pairs of coordinates.
        Uses an identity mapping for points near the origin to improve accuracy.
        """
        out_pts = np.copy(points)
        # --- High-accuracy mapping for points near the origin ---
        norms = np.linalg.norm(points, axis=1)
        linear_mask = norms < self.threshold
        # For points not near the origin, apply the full mapping
        nonlinear_mask = ~linear_mask
        
        if np.any(nonlinear_mask):
            points_to_map = points[nonlinear_mask]
            mapped_pts = np.copy(points_to_map)
            for i in range(0, self.p_dim - (self.p_dim % 2), 2):
                x = points_to_map[:, i]
                y = points_to_map[:, i+1]

                r = np.zeros_like(x)
                theta = np.zeros_like(x)

                mask = np.abs(x) > np.abs(y)
                
                r[mask] = x[mask]
                with np.errstate(divide='ignore', invalid='ignore'):
                    theta[mask] = (np.pi / 4.0) * (y[mask] / x[mask])

                r[~mask] = y[~mask]
                with np.errstate(divide='ignore', invalid='ignore'):
                    theta[~mask] = (np.pi / 2.0) - (np.pi / 4.0) * (x[~mask] / y[~mask])
                
                origin_mask = (np.abs(x) < 1e-9) & (np.abs(y) < 1e-9)
                theta[origin_mask] = 0

                mapped_pts[:, i] = r * np.cos(theta)
                mapped_pts[:, i+1] = r * np.sin(theta)
            out_pts[nonlinear_mask] = mapped_pts

        return out_pts

    def _disk_to_square_nd(self, points: np.ndarray) -> np.ndarray:
        """
        Inverse mapping from a product of 2D disks to a p-dim hypercube.
        Uses an identity mapping for points near the origin to improve accuracy.
        """
        out_pts = np.copy(points)
        # --- High-accuracy mapping for points near the origin ---
        norms = np.linalg.norm(points, axis=1)
        linear_mask = norms < self.threshold
        # For points not near the origin, apply the full mapping
        nonlinear_mask = ~linear_mask

        if np.any(nonlinear_mask):
            points_to_map = points[nonlinear_mask]
            mapped_pts = np.copy(points_to_map)
            for i in range(0, self.p_dim - (self.p_dim % 2), 2):
                disk_x = points_to_map[:, i]
                disk_y = points_to_map[:, i+1]

                r = np.sqrt(disk_x**2 + disk_y**2)
                phi = np.arctan2(disk_y, disk_x)
                
                square_u = np.zeros_like(r)
                square_v = np.zeros_like(r)

                mask_u_dom = (disk_x**2 >= disk_y**2)
                
                r_u = r[mask_u_dom]
                disk_x_u = disk_x[mask_u_dom]
                disk_y_u = disk_y[mask_u_dom]

                u_u = r_u * np.sign(disk_x_u)
                with np.errstate(divide='ignore', invalid='ignore'):
                    v_u = u_u * (4/np.pi) * np.arctan(disk_y_u / disk_x_u)
                v_u[disk_x_u == 0] = 0

                square_u[mask_u_dom] = u_u
                square_v[mask_u_dom] = v_u

                mask_v_dom = ~mask_u_dom
                r_v = r[mask_v_dom]
                disk_x_v = disk_x[mask_v_dom]
                disk_y_v = disk_y[mask_v_dom]

                v_v = r_v * np.sign(disk_y_v)
                with np.errstate(divide='ignore', invalid='ignore'):
                    u_v = v_v * (4/np.pi) * np.arctan(disk_x_v / disk_y_v)
                u_v[disk_y_v == 0] = 0
                
                square_u[mask_v_dom] = u_v
                square_v[mask_v_dom] = v_v
                
                mapped_pts[:, i] = square_u
                mapped_pts[:, i+1] = square_v
            out_pts[nonlinear_mask] = mapped_pts

        return out_pts

class TestParameterization():

    def __init__(self):
        """Set up a test case with a random direction vector."""
        self.z_dim = 512
        self.p_dim = self.z_dim - 1
        random_vec = np.random.randn(self.z_dim).astype(np.float32)
        self.center_vec = random_vec / np.linalg.norm(random_vec)
        self.param = Parameterization(self.center_vec)

    def run_all_tests(self):
        print("Running test_initialization...")
        self.test_initialization()
        print("OK")
        print("Running test_pole_alignment...")
        self.test_pole_alignment()
        print("OK")
        print("Running test_zero_mapping...")
        self.test_zero_mapping()
        print("OK")
        print("Running test_shape_consistency...")
        self.test_shape_consistency()
        print("OK")
        print("Running test_round_trip_consistency...")
        self.test_round_trip_consistency()
        print("OK")
        print("Running test_edge_case_north_pole...")
        self.test_edge_case_north_pole()
        print("OK")
        print("\nAll tests passed!")

    def test_initialization(self):
        """Test that the rotation matrix is valid."""
        self.assertEqual(self.param.rotation.shape, (self.z_dim, self.z_dim))
        identity = self.param.rotation @ self.param.inv_rotation
        np.testing.assert_allclose(identity, np.eye(self.z_dim), atol=1e-6)
        det = np.linalg.det(self.param.rotation)
        self.assertAlmostEqual(det, 1.0, places=5)

    def test_pole_alignment(self):
        """Test that the rotation correctly aligns the pole."""
        rotated_back = self.center_vec @ self.param.rotation
        np.testing.assert_allclose(rotated_back, self.param.north_pole, atol=1e-6)

    def test_zero_mapping(self):
        """Test that the origin of the parameter space maps to the center vector."""
        p_origin = np.zeros(self.p_dim)
        z_mapped = self.param.map_to_z_space(p_origin)
        
        self.assertEqual(z_mapped.shape, (1, self.z_dim))
        np.testing.assert_allclose(z_mapped.flatten(), self.center_vec, atol=1e-6)

    def test_shape_consistency(self):
        """Test that mapping functions return arrays of the correct shapes."""
        batch_size = 10
        p_vectors = np.random.rand(batch_size, self.p_dim)
        z_vectors = np.random.rand(batch_size, self.z_dim)
        z_vectors /= np.linalg.norm(z_vectors, axis=1, keepdims=True)

        self.assertEqual(self.param.map_to_z_space(p_vectors).shape, (batch_size, self.z_dim))
        self.assertEqual(self.param.map_to_parameter_space(z_vectors).shape, (batch_size, self.p_dim))

    def test_round_trip_consistency(self):
        """Test that mapping back and forth results in the original vector."""
        try:
            # Test 1: P-space -> Z-space -> P-space
            p_original = np.random.uniform(-1, 1, size=(10, self.p_dim))
            
            z_intermediate = self.param.map_to_z_space(p_original)
            p_roundtrip = self.param.map_to_parameter_space(z_intermediate)
            
            np.testing.assert_allclose(p_original, p_roundtrip, atol=1e-6)

            # Test 2: Z-space -> P-space -> Z-space
            random_z = np.random.randn(self.z_dim)
            v_ortho = random_z - np.dot(random_z, self.center_vec) * self.center_vec
            v_ortho /= np.linalg.norm(v_ortho)
            z_original = 0.5 * self.center_vec + np.sqrt(1 - 0.5**2) * v_ortho
            z_original = np.atleast_2d(z_original)

            p_intermediate = self.param.map_to_parameter_space(z_original)
            z_roundtrip = self.param.map_to_z_space(p_intermediate)

            np.testing.assert_allclose(z_original, z_roundtrip, atol=1e-6)
        except Exception as e:
            print(np.where(np.abs(p_original - p_roundtrip)[0] > 1e-6))
            raise e

    def test_edge_case_north_pole(self):
        """Test initialization when the center_vec is already the north pole."""
        param_north = Parameterization(self.param.north_pole)
        np.testing.assert_allclose(param_north.rotation, np.eye(self.z_dim), atol=1e-6)
    
    def assertEqual(self, a, b):
        assert a == b, f"Assertion failed: {a} != {b}"
    
    def assertAlmostEqual(self, a, b, places=5):
        assert abs(a - b) < 10**(-places), f"Assertion failed: {a} != {b} within {places} places"
    
if __name__ == '__main__':
    test = TestParameterization()
    # test.run_all_tests()
    print(test.center_vec-test.param.map_to_z_space(np.zeros((1,511))))


In [ ]:
import numpy as np

class Parameterization:
    """
    Handles the rigorous, area-preserving mapping from a hypercube
    parameter space to a target hemisphere in a higher-dimensional space.
    """
    def __init__(self, center_vec: np.ndarray):
        """
        Initializes the parameterization with a target direction vector.

        Args:
            center_vec (np.ndarray): A 1D array representing the target direction
                                     in the z_dim space. It will be normalized.
        """
        self.z_dim = center_vec.shape[0]
        self.p_dim = self.z_dim - 1
        self.north_pole = np.zeros(self.z_dim, dtype=np.float32)
        self.north_pole[-1] = 1.0
        self.rotation = self._get_rotation_matrix(center_vec)
        self.inv_rotation = self.rotation.T

    def _get_rotation_matrix(self, v_to: np.ndarray) -> np.ndarray:
        """
        Computes the rotation matrix that aligns the north pole to v_to.
        This uses the robust Householder reflection method for N-D vectors.
        """
        v_from = self.north_pole
        v_to_unit = v_to / np.linalg.norm(v_to)

        if np.allclose(v_from, v_to_unit):
            return np.eye(self.z_dim, dtype=np.float32)
        if np.allclose(v_from, -v_to_unit):
            R = -np.eye(self.z_dim, dtype=np.float32)
            R[0, 0] = 1.0  # Ensure determinant is +1 for a valid rotation
            return R

        # Intermediate vector for the first reflection
        u = v_from + v_to_unit
        u /= np.linalg.norm(u)

        # Reflector H1 maps v_from to -v_to_unit
        H1 = np.eye(self.z_dim) - 2 * np.outer(u, u)
        # Reflector H2 maps -v_to_unit to v_to_unit
        H2 = np.eye(self.z_dim) - 2 * np.outer(v_to_unit, v_to_unit)
        
        # The rotation is the composition of the two reflections
        return H2 @ H1

    def map_to_z_space(self, p_vectors: np.ndarray) -> np.ndarray:
        """Maps (N, p_dim) in parameter space cube to (N, z_dim) on hemisphere."""
        p_vectors = np.atleast_2d(p_vectors)
        polydisk_pts = self._square_to_disk_nd(p_vectors)
        
        scale_factor = 2.0 / (np.sqrt(self.p_dim / 2.0) + 1e-9)
        disk_pts = polydisk_pts * scale_factor
        
        hemisphere_pts_aligned = self._inverse_laea_projection(disk_pts)
        
        return hemisphere_pts_aligned @ self.inv_rotation

    def map_to_parameter_space(self, z_vectors: np.ndarray) -> np.ndarray:
        """Maps (N, z_dim) on hemisphere to (N, p_dim) in parameter space cube."""
        z_vectors = np.atleast_2d(z_vectors)
        
        aligned_z = z_vectors @ self.rotation
        disk_pts = self._laea_projection(aligned_z)
        
        scale_factor = 2.0 / (np.sqrt(self.p_dim / 2.0) + 1e-9)
        polydisk_pts = disk_pts / scale_factor
        
        return self._disk_to_square_nd(polydisk_pts)

    def _laea_projection(self, z_aligned: np.ndarray) -> np.ndarray:
        """Projects from standard hemisphere to the p-dimensional unit ball."""
        scale = np.sqrt(2 / (1 + z_aligned[:, -1] + 1e-9))
        return z_aligned[:, :-1] * scale[:, np.newaxis]

    def _inverse_laea_projection(self, disk_pts: np.ndarray) -> np.ndarray:
        """Projects from the p-dimensional unit ball to standard hemisphere."""
        norm_sq = np.sum(disk_pts**2, axis=1)
        norm_sq = np.clip(norm_sq, 0, 4)
        z = np.zeros((disk_pts.shape[0], self.z_dim), dtype=np.float32)
        with np.errstate(invalid='ignore'): # Ignore sqrt of negative for zero-norm points
             z[:, :-1] = disk_pts * (np.sqrt(1 - norm_sq / 4))[:, np.newaxis]
        z[:, -1] = 1 - norm_sq / 2
        return z

    def _square_to_disk_nd(self, points: np.ndarray) -> np.ndarray:
        """
        Maps a p-dim hypercube to a product of 2D disks by applying the
        Shirley-Chiu mapping to sequential pairs of coordinates.
        """
        out_pts = np.copy(points)
        for i in range(0, self.p_dim - (self.p_dim % 2), 2):
            x = points[:, i]
            y = points[:, i+1]

            r = np.zeros_like(x)
            theta = np.zeros_like(x)

            mask = np.abs(x) > np.abs(y)
            
            r[mask] = x[mask]
            with np.errstate(divide='ignore', invalid='ignore'):
                theta[mask] = (np.pi / 4.0) * (y[mask] / x[mask])

            r[~mask] = y[~mask]
            with np.errstate(divide='ignore', invalid='ignore'):
                theta[~mask] = (np.pi / 2.0) - (np.pi / 4.0) * (x[~mask] / y[~mask])
            
            # Handle origin case where x and y are zero
            origin_mask = (np.abs(x) < 1e-9) & (np.abs(y) < 1e-9)
            theta[origin_mask] = 0

            out_pts[:, i] = r * np.cos(theta)
            out_pts[:, i+1] = r * np.sin(theta)
        
        return out_pts

    def _disk_to_square_nd(self, points: np.ndarray) -> np.ndarray:
        """
        Corrected inverse mapping from a product of 2D disks to a p-dim hypercube,
        based directly on the Shirley-Chiu formulation.
        """
        out_pts = np.copy(points)
        for i in range(0, self.p_dim - (self.p_dim % 2), 2):
            disk_x = points[:, i]
            disk_y = points[:, i+1]

            r = np.sqrt(disk_x**2 + disk_y**2)
            
            square_u = np.zeros_like(r)
            square_v = np.zeros_like(r)

            # Mask where |x| >= |y| (u-dominant)
            mask_u_dom = (disk_x**2 >= disk_y**2)
            
            # Process u-dominant points (right and left wedges)
            r_u = r[mask_u_dom]
            disk_x_u = disk_x[mask_u_dom]
            disk_y_u = disk_y[mask_u_dom]

            u_u = r_u * np.sign(disk_x_u)
            with np.errstate(divide='ignore', invalid='ignore'):
                v_u = u_u * (4/np.pi) * np.arctan(disk_y_u / disk_x_u)
            v_u[disk_x_u == 0] = 0

            square_u[mask_u_dom] = u_u
            square_v[mask_u_dom] = v_u

            # Process v-dominant points (top and bottom wedges)
            mask_v_dom = ~mask_u_dom
            r_v = r[mask_v_dom]
            disk_x_v = disk_x[mask_v_dom]
            disk_y_v = disk_y[mask_v_dom]

            v_v = r_v * np.sign(disk_y_v)
            with np.errstate(divide='ignore', invalid='ignore'):
                u_v = v_v * (4/np.pi) * np.arctan(disk_x_v / disk_y_v)
            u_v[disk_y_v == 0] = 0
            
            square_u[mask_v_dom] = u_v
            square_v[mask_v_dom] = v_v
            
            out_pts[:, i] = square_u
            out_pts[:, i+1] = square_v

        return out_pts

class TestParameterization():

    def __init__(self):
        """Set up a test case with a random direction vector."""
        self.z_dim = 512
        self.p_dim = self.z_dim - 1
        random_vec = np.random.randn(self.z_dim).astype(np.float32)
        self.center_vec = random_vec / np.linalg.norm(random_vec)
        self.param = Parameterization(self.center_vec)

    def run_all_tests(self):
        print("Running test_initialization...")
        self.test_initialization()
        print("OK")
        print("Running test_pole_alignment...")
        self.test_pole_alignment()
        print("OK")
        print("Running test_zero_mapping...")
        self.test_zero_mapping()
        print("OK")
        print("Running test_shape_consistency...")
        self.test_shape_consistency()
        print("OK")
        print("Running test_round_trip_consistency...")
        self.test_round_trip_consistency()
        print("OK")
        print("Running test_edge_case_north_pole...")
        self.test_edge_case_north_pole()
        print("OK")
        print("\nAll tests passed!")

    def test_initialization(self):
        """Test that the rotation matrix is valid."""
        self.assertEqual(self.param.rotation.shape, (self.z_dim, self.z_dim))
        identity = self.param.rotation @ self.param.inv_rotation
        np.testing.assert_allclose(identity, np.eye(self.z_dim), atol=1e-6)
        det = np.linalg.det(self.param.rotation)
        self.assertAlmostEqual(det, 1.0, places=5)

    def test_pole_alignment(self):
        """Test that the rotation correctly aligns the pole."""
        rotated_back = self.center_vec @ self.param.rotation
        np.testing.assert_allclose(rotated_back, self.param.north_pole, atol=1e-6)

    def test_zero_mapping(self):
        """Test that the origin of the parameter space maps to the center vector."""
        p_origin = np.zeros(self.p_dim)
        z_mapped = self.param.map_to_z_space(p_origin)
        
        self.assertEqual(z_mapped.shape, (1, self.z_dim))
        np.testing.assert_allclose(z_mapped.flatten(), self.center_vec, atol=1e-6)

    def test_shape_consistency(self):
        """Test that mapping functions return arrays of the correct shapes."""
        batch_size = 10
        p_vectors = np.random.rand(batch_size, self.p_dim)
        z_vectors = np.random.rand(batch_size, self.z_dim)
        z_vectors /= np.linalg.norm(z_vectors, axis=1, keepdims=True)

        self.assertEqual(self.param.map_to_z_space(p_vectors).shape, (batch_size, self.z_dim))
        self.assertEqual(self.param.map_to_parameter_space(z_vectors).shape, (batch_size, self.p_dim))

    def test_round_trip_consistency(self):
        """Test that mapping back and forth results in the original vector."""
        try:
            # Test 1: P-space -> Z-space -> P-space
            p_original = np.random.uniform(-1, 1, size=(10, self.p_dim))
            
            z_intermediate = self.param.map_to_z_space(p_original)
            p_roundtrip = self.param.map_to_parameter_space(z_intermediate)
            
            np.testing.assert_allclose(p_original, p_roundtrip, atol=1e-6)

            # Test 2: Z-space -> P-space -> Z-space
            random_z = np.random.randn(self.z_dim)
            v_ortho = random_z - np.dot(random_z, self.center_vec) * self.center_vec
            v_ortho /= np.linalg.norm(v_ortho)
            z_original = 0.5 * self.center_vec + np.sqrt(1 - 0.5**2) * v_ortho
            z_original = np.atleast_2d(z_original)

            p_intermediate = self.param.map_to_parameter_space(z_original)
            z_roundtrip = self.param.map_to_z_space(p_intermediate)

            np.testing.assert_allclose(z_original, z_roundtrip, atol=1e-6)
        except Exception as e:
            print(np.where(np.abs(p_original - p_roundtrip)[0] > 1e-6))
            raise e

    def test_edge_case_north_pole(self):
        """Test initialization when the center_vec is already the north pole."""
        param_north = Parameterization(self.param.north_pole)
        np.testing.assert_allclose(param_north.rotation, np.eye(self.z_dim), atol=1e-6)
    
    def assertEqual(self, a, b):
        assert a == b, f"Assertion failed: {a} != {b}"
    
    def assertAlmostEqual(self, a, b, places=5):
        assert abs(a - b) < 10**(-places), f"Assertion failed: {a} != {b} within {places} places"
    
if __name__ == '__main__':
    test = TestParameterization()
    test.run_all_tests()


In [ ]:
import plotly.graph_objects as go
import numpy as np
import ipywidgets as widgets
from IPython.display import display
from sklearn.ensemble import RandomForestClassifier
from sklearn.decomposition import PCA

def create_live_cross_section_explorer(rf_classifier: RandomForestClassifier,
                                       successful_samples: np.ndarray,
                                       num_components: int = 5,
                                       resolution: int = 75):
    """
    Creates a live, continuously updating cross-section explorer for the RF
    decision boundary. Updates happen in real-time as sliders are dragged.
    """
    if num_components < 3:
        print("This visualization requires at least 3 principal components.")
        return
    if successful_samples.shape[0] < num_components:
        print(f"Not enough samples for {num_components}-component PCA.")
        return

    print("Preparing live interactive explorer...")

    # --- 1. One-Time Data Preparation and PCA ---
    successful_samples_norm = successful_samples / np.linalg.norm(successful_samples, axis=1, keepdims=True)
    pca = PCA(n_components=num_components)
    successful_samples_pca = pca.fit_transform(successful_samples_norm)
    data_mean = pca.mean_
    pc1, pc2, *depth_pcs = pca.components_

    # --- 2. Create the FigureWidget Layout (once) ---
    fig = go.FigureWidget(
        data=[
            go.Contour(contours=dict(coloring='heatmap', start=0, end=1), colorbar=dict(title='Success Probability')),
            go.Contour(contours=dict(start=0.5, end=0.5, coloring='lines'), line=dict(color='white', width=3, dash='dash'))
        ],
        layout=go.Layout(
            title_text="Live RF Boundary Cross-Section",
            width=1000, height=750, yaxis_scaleanchor="x"
        )
    )

    # --- 3. Define the fast update function ---
    def update_view(w3, w4, w5):
        # The origin of our 2D slice is shifted by the sliders
        plane_origin = data_mean + w3 * depth_pcs[0] + w4 * depth_pcs[1] + w5 * depth_pcs[2]

        x_min, x_max = successful_samples_pca[:, 0].min()-0.2, successful_samples_pca[:, 0].max()+1
        y_min, y_max = successful_samples_pca[:, 1].min()-0.4, successful_samples_pca[:, 1].max()+0.4
        x_grid = np.linspace(x_min, x_max, resolution)
        y_grid = np.linspace(y_min, y_max, resolution)
        xx, yy = np.meshgrid(x_grid, y_grid)

        grid_points_512d = plane_origin + xx.ravel()[:, np.newaxis] * pc1 + yy.ravel()[:, np.newaxis] * pc2
        grid_points_norm = grid_points_512d / np.linalg.norm(grid_points_512d, axis=1, keepdims=True)
        Z = rf_classifier.predict_proba(grid_points_norm)[:, 1].reshape(xx.shape)

        # Update the figure's data in-place for maximum performance
        with fig.batch_update():
            fig.data[0].x = x_grid
            fig.data[0].y = y_grid
            fig.data[0].z = Z
            fig.data[1].x = x_grid
            fig.data[1].y = y_grid
            fig.data[1].z = Z
            fig.layout.title.text = f"RF Boundary Slice (PC3={w3:.2f}, PC4={w4:.2f}, PC5={w5:.2f})"
            fig.layout.xaxis.title = 'Principal Component 1'
            fig.layout.yaxis.title = 'Principal Component 2'
            
    # --- 4. Create Sliders with continuous_update=True ---
    style = {'description_width': 'initial'}
    def make_slider(pc_index):
        min_val, max_val = successful_samples_pca[:, pc_index].min(), successful_samples_pca[:, pc_index].max()
        # Set continuous_update to True for live feedback
        return widgets.FloatSlider(value=0.0, min=min_val, max=max_val, step=(max_val-min_val)/100,
                                   description=f'Slice Position PC{pc_index + 1}', style=style,
                                   continuous_update=True, readout_format='.2f')

    slider3 = make_slider(2)
    slider4 = make_slider(3)
    slider5 = make_slider(4)
    
    # --- 5. Link sliders to the function and lay out the UI ---
    interactive_output = widgets.interactive_output(update_view, {'w3': slider3, 'w4': slider4, 'w5': slider5})
    
    # Display the final UI components together
    display(widgets.VBox([
        widgets.HTML("<h3>Live Boundary Explorer</h3>"),
        widgets.HTML("<p>Drag sliders to see the decision boundary change in real-time across different cross-sections.</p>"),
        slider3, slider4, slider5,
        fig
    ]))

# ==============================================================================
#                      EXECUTION
# ==============================================================================
# This assumes that 'trained_rf_classifier' and 'final_z_vectors_np'
# are available from the previous cell.

if 'trained_rf_classifier' in locals() and 'final_z_vectors_np' in locals():
    create_live_cross_section_explorer(
        rf_classifier=trained_rf_classifier,
        successful_samples=final_z_vectors_np
    )
else:
    print("Could not find the necessary variables ('trained_rf_classifier', 'final_z_vectors_np').")
    print("Please make sure you have run the previous cell successfully.")
    print("NOTE: If the plot appears blank, your Jupyter environment may need to be configured for Plotly FigureWidgets.")
    print("In JupyterLab, run: !pip install jupyterlab \"ipywidgets>=7.5\" && jupyter labextension install @jupyter-widgets/jupyterlab-manager plotlywidget")

In [ ]:
import unittest
import numpy as np

class Parameterization:
    """
    Handles the rigorous, area-preserving mapping from a hypercube
    parameter space to a target hemisphere in a higher-dimensional space.
    """
    def __init__(self, center_vec: np.ndarray):
        """
        Initializes the parameterization with a target direction vector.

        Args:
            center_vec (np.ndarray): A 1D array representing the target direction
                                     in the z_dim space. It will be normalized.
        """
        self.z_dim = center_vec.shape[0]
        self.p_dim = self.z_dim - 1
        self.north_pole = np.zeros(self.z_dim, dtype=np.float32)
        self.north_pole[-1] = 1.0
        self.rotation = self._get_rotation_matrix(center_vec)
        self.inv_rotation = self.rotation.T

    def _get_rotation_matrix(self, v_to: np.ndarray) -> np.ndarray:
        """
        Computes the rotation matrix that aligns the north pole to v_to.
        This uses the robust Householder reflection method for N-D vectors.
        """
        v_from = self.north_pole
        v_to_unit = v_to / np.linalg.norm(v_to)

        if np.allclose(v_from, v_to_unit):
            return np.eye(self.z_dim, dtype=np.float32)
        if np.allclose(v_from, -v_to_unit):
            R = -np.eye(self.z_dim, dtype=np.float32)
            R[0, 0] = 1.0  # Ensure determinant is +1 for a valid rotation
            return R

        # Intermediate vector for the first reflection
        u = v_from + v_to_unit
        u /= np.linalg.norm(u)

        # Reflector H1 maps v_from to -v_to_unit
        H1 = np.eye(self.z_dim) - 2 * np.outer(u, u)
        # Reflector H2 maps -v_to_unit to v_to_unit
        H2 = np.eye(self.z_dim) - 2 * np.outer(v_to_unit, v_to_unit)
        
        # The rotation is the composition of the two reflections
        return H2 @ H1

    def map_to_z_space(self, p_vectors: np.ndarray) -> np.ndarray:
        """Maps (N, p_dim) in parameter space cube to (N, z_dim) on hemisphere."""
        p_vectors = np.atleast_2d(p_vectors)
        disk_pts = self._square_to_disk_nd(p_vectors)
        hemisphere_pts_aligned = self._inverse_laea_projection(disk_pts)
        return hemisphere_pts_aligned @ self.inv_rotation

    def map_to_parameter_space(self, z_vectors: np.ndarray) -> np.ndarray:
        """Maps (N, z_dim) on hemisphere to (N, p_dim) in parameter space cube."""
        z_vectors = np.atleast_2d(z_vectors)
        aligned_z = z_vectors @ self.rotation
        disk_pts = self._laea_projection(aligned_z)
        return self._disk_to_square_nd(disk_pts)

    def _laea_projection(self, z_aligned: np.ndarray) -> np.ndarray:
        """Projects from standard hemisphere to the p-dimensional unit ball."""
        scale = np.sqrt(2 / (1 + z_aligned[:, -1] + 1e-9))
        return z_aligned[:, :-1] * scale[:, np.newaxis]

    def _inverse_laea_projection(self, disk_pts: np.ndarray) -> np.ndarray:
        """Projects from the p-dimensional unit ball to standard hemisphere."""
        norm_sq = np.sum(disk_pts**2, axis=1)
        norm_sq = np.clip(norm_sq, 0, 4)
        z = np.zeros((disk_pts.shape[0], self.z_dim), dtype=np.float32)
        z[:, :-1] = disk_pts * (np.sqrt(1 - norm_sq / 4))[:, np.newaxis]
        z[:, -1] = 1 - norm_sq / 2
        return z

    def _square_to_disk_nd(self, points: np.ndarray) -> np.ndarray:
        """
        Maps a p-dim hypercube to a product of 2D disks by applying the
        Shirley-Chiu mapping to sequential pairs of coordinates.
        """
        out_pts = np.copy(points)
        for i in range(0, self.p_dim - (self.p_dim % 2), 2):
            x = points[:, i]
            y = points[:, i+1]

            r = np.zeros_like(x)
            theta = np.zeros_like(x)

            mask = np.abs(x) > np.abs(y)
            
            # Branch 1: |x| > |y|
            r[mask] = x[mask]
            theta[mask] = (np.pi / 4.0) * (y[mask] / (x[mask] + 1e-9))

            # Branch 2: |y| >= |x|
            r[~mask] = y[~mask]
            theta[~mask] = (np.pi / 2.0) - (np.pi / 4.0) * (x[~mask] / (y[~mask] + 1e-9))
            
            out_pts[:, i] = r * np.cos(theta)
            out_pts[:, i+1] = r * np.sin(theta)
        
        return out_pts

    def _disk_to_square_nd(self, points: np.ndarray) -> np.ndarray:
        """
        Inverse mapping from a product of 2D disks to a p-dim hypercube.
        """
        out_pts = np.copy(points)
        for i in range(0, self.p_dim - (self.p_dim % 2), 2):
            disk_x = points[:, i]
            disk_y = points[:, i+1]

            r = np.sqrt(disk_x**2 + disk_y**2)
            phi = np.arctan2(disk_y, disk_x)
            
            square_x = np.zeros_like(r)
            square_y = np.zeros_like(r)

            mask1 = (phi > -np.pi / 4) & (phi <= np.pi / 4)
            mask2 = (phi > np.pi / 4) & (phi <= 3 * np.pi / 4)
            mask3 = (phi > 3 * np.pi / 4) | (phi <= -3 * np.pi / 4)
            mask4 = ~mask1 & ~mask2 & ~mask3

            # Avoid division by zero at tan(pi/2) and tan(-pi/2)
            with np.errstate(divide='ignore', invalid='ignore'):
                tan_phi = np.tan(phi)
                inv_tan_phi = 1.0 / tan_phi

            square_x[mask1] = r[mask1]
            square_y[mask1] = r[mask1] * tan_phi[mask1]

            square_y[mask2] = r[mask2]
            square_x[mask2] = r[mask2] * inv_tan_phi[mask2]

            square_x[mask3] = -r[mask3]
            square_y[mask3] = -r[mask3] * tan_phi[mask3]
            
            square_y[mask4] = -r[mask4]
            square_x[mask4] = -r[mask4] * inv_tan_phi[mask4]
            
            out_pts[:, i] = square_x
            out_pts[:, i+1] = square_y

        return out_pts


class TestParameterization(unittest.TestCase):

    def setUp(self):
        """Set up a test case with a random direction vector."""
        self.z_dim = 512
        self.p_dim = self.z_dim - 1
        random_vec = np.random.randn(self.z_dim).astype(np.float32)
        self.center_vec = random_vec / np.linalg.norm(random_vec)
        self.param = Parameterization(self.center_vec)

    def test_initialization(self):
        """Test that the rotation matrix is valid."""
        self.assertEqual(self.param.rotation.shape, (self.z_dim, self.z_dim))
        identity = self.param.rotation @ self.param.inv_rotation
        np.testing.assert_allclose(identity, np.eye(self.z_dim), atol=1e-6)
        det = np.linalg.det(self.param.rotation)
        self.assertAlmostEqual(det, 1.0, places=5)

    def test_pole_alignment(self):
        """Test that the rotation correctly aligns the pole."""
        rotated_back = self.center_vec @ self.param.rotation
        np.testing.assert_allclose(rotated_back, self.param.north_pole, atol=1e-6)

    def test_zero_mapping(self):
        """Test that the origin of the parameter space maps to the center vector."""
        p_origin = np.zeros(self.p_dim)
        z_mapped = self.param.map_to_z_space(p_origin)
        
        self.assertEqual(z_mapped.shape, (1, self.z_dim))
        np.testing.assert_allclose(z_mapped.flatten(), self.center_vec, atol=1e-6)

    def test_shape_consistency(self):
        """Test that mapping functions return arrays of the correct shapes."""
        batch_size = 10
        p_vectors = np.random.rand(batch_size, self.p_dim)
        z_vectors = np.random.rand(batch_size, self.z_dim)
        z_vectors /= np.linalg.norm(z_vectors, axis=1, keepdims=True)

        self.assertEqual(self.param.map_to_z_space(p_vectors).shape, (batch_size, self.z_dim))
        self.assertEqual(self.param.map_to_parameter_space(z_vectors).shape, (batch_size, self.p_dim))

    def test_round_trip_consistency(self):
        """Test that mapping back and forth results in the original vector."""
        # Test 1: P-space -> Z-space -> P-space
        # Use more than 2 dimensions to test the paired mapping
        p_original = np.random.uniform(-1, 1, size=(10, self.p_dim))
        
        z_intermediate = self.param.map_to_z_space(p_original)
        p_roundtrip = self.param.map_to_parameter_space(z_intermediate)
        
        # The last dimension might be untouched if p_dim is odd, so we test all pairs
        test_dims = self.p_dim - (self.p_dim % 2)
        np.testing.assert_allclose(p_original[:, :test_dims], p_roundtrip[:, :test_dims], atol=1e-6)

        # Test 2: Z-space -> P-space -> Z-space
        random_z = np.random.randn(self.z_dim)
        v_ortho = random_z - np.dot(random_z, self.center_vec) * self.center_vec
        v_ortho /= np.linalg.norm(v_ortho)
        z_original = 0.5 * self.center_vec + np.sqrt(1 - 0.5**2) * v_ortho
        z_original = np.atleast_2d(z_original)

        p_intermediate = self.param.map_to_parameter_space(z_original)
        z_roundtrip = self.param.map_to_z_space(p_intermediate)

        np.testing.assert_allclose(z_original, z_roundtrip, atol=1e-6)

    def test_edge_case_north_pole(self):
        """Test initialization when the center_vec is already the north pole."""
        param_north = Parameterization(self.param.north_pole)
        np.testing.assert_allclose(param_north.rotation, np.eye(self.z_dim), atol=1e-6)


if __name__ == '__main__':
    unittest.main(argv=['first-arg-is-ignored'], exit=False)


In [ ]:

# offset = 0 * 1
# current_w3 = w3 + offset

# # The origin of this specific slice
# plane_origin = data_mean + current_w3 * pc3 + w4 * depth_pcs[1] + w5 * depth_pcs[2]

# grid_points_512d = plane_origin + xx.ravel()[:, np.newaxis] * pc1 + yy.ravel()[:, np.newaxis] * pc2
# grid_points_norm = grid_points_512d / np.linalg.norm(grid_points_512d, axis=1, keepdims=True)
# Z = trained_rf_classifier.predict_proba()[:, 1].reshape(xx.shape)
# Z

In [ ]:
import torch
import numpy as np
import os
from tqdm.notebook import tqdm
from typing import List, Callable, Dict, Tuple
import time
import matplotlib.pyplot as plt
from matplotlib.patches import Ellipse
import matplotlib.transforms as transforms
# NEW: Import display and clear_output for Jupyter integration
from IPython.display import display, clear_output

class LiveZSpaceVisualizer:
    """
    Creates and dynamically updates a 2D plot of the Z-space search distribution,
    specifically designed to work within a Jupyter Notebook environment.
    """
    def __init__(self, z_dim=512):
        self.z_dim = z_dim
        # No plt.ion() needed for this method
        self.fig, self.ax = plt.subplots(figsize=(8, 8))
        
        # We create a placeholder handle for the display object
        self.handle = None
        
        # Plot static background elements once
        self._setup_plot()

    def _setup_plot(self):
        self.ax.set_title("Evolution of Z-Space Search Distribution (Live)")
        self.ax.set_xlabel("Z Dimension 0")
        self.ax.set_ylabel("Z Dimension 1")
        self.ax.axvline(0, color='grey', linestyle='--', linewidth=0.5)
        self.ax.axhline(0, color='grey', linestyle='--', linewidth=0.5)
        
        # Draw level sets of the N(0, I) prior
        for i in range(1, 4):
            circle = Ellipse((0, 0), width=i*2, height=i*2, edgecolor='grey', facecolor='none', linestyle=':', label=f'{i}σ Prior')
            self.ax.add_patch(circle)
            
        self.ax.set_xlim(-5, 5)
        self.ax.set_ylim(-5, 5)
        self.ax.set_aspect('equal', adjustable='box')
        self.ax.legend(loc="upper right")
        
        # Create placeholder artists for the dynamic elements
        self.ellipse = Ellipse((0, 0), width=0, height=0, facecolor='cyan', alpha=0.3)
        self.ax.add_patch(self.ellipse)
        self.mean_dot, = self.ax.plot([], [], 'ro', markersize=8, label='Search Mean')
        
        # Initial display of the empty plot
        self.handle = display(self.fig, display_id=True)

    def update_plot(self, mean_np: np.ndarray, cov_np: np.ndarray):
        """Updates the ellipse and mean dot with new distribution parameters."""
        mean_2d = mean_np[:2]
        cov_2d = cov_np[:2, :2]

        eigenvalues, eigenvectors = np.linalg.eigh(cov_2d)
        eigenvalues[eigenvalues < 0] = 0
        
        width, height = 2 * 2 * np.sqrt(eigenvalues)
        angle = np.degrees(np.arctan2(*eigenvectors[:, 0][::-1]))

        # Update artists
        self.ellipse.set_center(mean_2d)
        self.ellipse.set_width(width)
        self.ellipse.set_height(height)
        transform = transforms.Affine2D().rotate_deg_around(mean_2d[0], mean_2d[1], angle) + self.ax.transData
        self.ellipse.set_transform(transform)
        
        self.mean_dot.set_data([mean_2d[0]], [mean_2d[1]])
        
        # Update the display in the notebook cell
        self.handle.update(self.fig)

    def close(self):
        """Closes the plot figure to free up memory."""
        plt.close(self.fig)


class ZSpaceEvolutionarySampler:
    """
    Finds Z-space vectors for a single, specific attribute bin using an
    evolutionary strategy with KL divergence regularization.
    """
    def __init__(self, target_filters: Dict, config: Dict, models: Dict, G: torch.nn.Module, device: torch.device):
        self.config = config
        self.models = {name: model.to(device) for name, model in models.items()}
        self.G = G.to(device)
        self.device = device
        self.z_dim = self.G.mapping.z_dim
        self.target_bin = self._parse_filters(target_filters)
        self.mean = torch.zeros(self.z_dim, device=self.device)
        self.cov = torch.eye(self.z_dim, device=self.device)
        self.visualizer = LiveZSpaceVisualizer() if self.config.get('visualize_live', False) else None

    def _parse_filters(self, filters: Dict) -> List[Dict]:
        target = []
        print("Parsing target bin from range-based filters...")
        for var, condition_dict in filters.items():
            if 'range' not in condition_dict: raise ValueError(f"Filter for '{var}' must contain a 'range' key.")
            target.append({'var': var, 'range': condition_dict['range']})
        print(f"Target bin defined as: {target}")
        return target

    @torch.no_grad()
    def _calculate_fitness(self, z_batch_gpu: torch.Tensor) -> Tuple[torch.Tensor, torch.Tensor]:
        w_batch = self.G.mapping(z_batch_gpu, None, truncation_psi=self.config['truncation_psi'])[:, 0]
        bin_loss = 0
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            target_val = low if high == np.inf else (high if low == -np.inf else (low + high) / 2.0)
            preds = self.models[var](w_batch).view(-1)*100
            if high == np.inf: bin_loss += torch.clamp(low - preds, min=0)**2
            elif low == -np.inf: bin_loss += torch.clamp(preds - high, min=0)**2
            else: bin_loss += (preds - target_val)**2
        
        final_mask = torch.full((w_batch.shape[0],), True, device=self.device)
        for condition in self.target_bin:
            var, (low, high) = condition['var'], condition['range']
            preds = self.models[var](w_batch).view(-1)*100
            final_mask &= (preds >= low) & (preds <= high)
        
        return bin_loss, final_mask

    def _kl_divergence(self, mean: torch.Tensor, cov: torch.Tensor) -> float:
        d = self.z_dim
        sign, logdet = torch.linalg.slogdet(cov)
        if sign <= 0: return float('inf')
        return 0.5 * (torch.trace(cov) + torch.dot(mean, mean) - d - logdet)

    def run(self) -> np.ndarray:
        n_to_generate = self.config['n_samples_to_generate']
        population_size = self.config['population_size']
        n_elite = int(population_size * self.config['elite_fraction'])
        if n_elite <= 1: raise ValueError("Elite fraction too small.")

        print(f"Starting evolutionary search for {n_to_generate} samples...")
        pbar = tqdm(range(self.config['generations']), desc="Evolving Distribution")
        
        for gen in pbar:
            stable_cov = self.cov + torch.eye(self.z_dim, device=self.device) * 1e-6
            z_candidates_cpu = np.random.multivariate_normal(self.mean.cpu().numpy(), stable_cov.cpu().numpy(), size=population_size).astype(np.float32)
            z_candidates_gpu = torch.from_numpy(z_candidates_cpu).to(self.device)

            bin_compliance_fitness, final_mask = self._calculate_fitness(z_candidates_gpu)
            kl_penalty = self._kl_divergence(self.mean, self.cov)
            total_fitness = bin_compliance_fitness + self.config['kl_lambda'] * kl_penalty
            
            elite_indices = torch.argsort(total_fitness)[:n_elite]
            elite_z = z_candidates_gpu[elite_indices]
            
            new_mean = torch.mean(elite_z, dim=0)
            # Transpose elite_z so that variables are on rows, as expected by torch.cov
            new_cov = torch.cov(elite_z.T)
            
            lr = self.config['update_learning_rate']
            self.mean = (1 - lr) * self.mean + lr * new_mean
            self.cov = (1 - lr) * self.cov + lr * new_cov
            
            pbar.set_postfix(fitness=f"{total_fitness[elite_indices].mean().item():.2f}", kl=f"{kl_penalty.item():.2f}, success%={final_mask.float().mean().item()*100:.2f}")

            # --- Update the live plot ---
            if self.visualizer:
                self.visualizer.update_plot(self.mean.cpu().numpy(), self.cov.cpu().numpy())
                time.sleep(0.01) # Allow plot to redraw

        if self.visualizer:
            self.visualizer.close()
            
        print("\nEvolution complete. Harvesting and filtering final samples...")
        final_stable_cov = self.cov + torch.eye(self.z_dim, device=self.device) * 1e-6
        final_dist = torch.distributions.MultivariateNormal(self.mean, final_stable_cov)
        final_z_gpu = final_dist.sample((int(n_to_generate * 1.5),)) # Generate more to account for filtering
        
        with torch.no_grad():
            final_w_gpu = self.G.mapping(final_z_gpu, None, truncation_psi=self.config['truncation_psi'])[:, 0]
            final_mask = torch.full((final_w_gpu.shape[0],), True, device=self.device)
            for condition in self.target_bin:
                var, (low, high) = condition['var'], condition['range']
                preds = self.models[var](final_w_gpu).view(-1)*100
                final_mask &= (preds >= low) & (preds <= high)
        
        successful_z_gpu = final_z_gpu[final_mask][:n_to_generate]
        success_rate = (len(successful_z_gpu) / n_to_generate) * 100
        print(f"Successfully generated and filtered {success_rate:.2f}% of the requested final Z vectors.")
        
        return successful_z_gpu.cpu().numpy()

# ==============================================================================
#                      CONFIGURATION AND EXECUTION
# ==============================================================================

if __name__ == '__main__':
    # NOTE: The following variables are placeholders and must be defined
    #       in your actual execution environment for this script to run.
    #       - G: A pre-trained StyleGAN generator model.
    #       - ALL_MODELS: A dictionary mapping attribute names to pre-trained classifier models.
    #       - device: A torch.device object (e.g., torch.device('cuda:0')).
    

    EVOLUTIONARY_CONFIG = {
        'n_samples_to_generate': 1024,
        'population_size': 4096,
        'elite_fraction': 0.1,
        'generations': 50,
        'update_learning_rate': 0.5,
        'kl_lambda': 0.1,
        'truncation_psi': 1.0,
        'visualize_live': True, # Set to True to enable the live plot
    }

    TARGET_FILTERS = {
            'gender': {'range': (-np.inf, 45)},   # Represents gender < 45
            'age':    {'range': (60, np.inf)},      # Represents age >= 60
            'trustworthy': {'range': (60, 75)}    # Represents 60 <= trustworthy <= 75
        }

    sampler = ZSpaceEvolutionarySampler(
        target_filters=TARGET_FILTERS,
        config=EVOLUTIONARY_CONFIG,
        models=ALL_MODELS,
        G=G,
        device=device
    )
    
    final_z_vectors_np = sampler.run()

In [ ]:
np.linalg.norm(np.random.randn(512)*0.02)

In [ ]:
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, TensorDataset
import numpy as np
from tqdm import tqdm
import math

# ==============================================================================
#                      1. DEPENDENCIES & MOCK GENERATOR
# ==============================================================================
# This mock generator is for demonstration purposes.
# It produces outputs on a hypersphere to match the problem description.

class MockGenerator(torch.nn.Module):
    """
    A mock generator that simulates the G.mapping component.
    The forward pass now normalizes the output to lie on a hypersphere.
    """
    def __init__(self, z_dim, w_dim):
        super().__init__()
        self.z_dim = z_dim
        self.w_dim = w_dim
        # The internal network that produces pre-normalized vectors
        self.net = nn.Sequential(
            nn.Linear(z_dim, 1024),
            nn.LeakyReLU(0.2),
            nn.Linear(1024, 1024),
            nn.LeakyReLU(0.2),
            nn.Linear(1024, w_dim)
        )

    def mapping(self, z, c, truncation_psi=1.0):
        # Generate a pre-normalized w vector
        w_pre = self.net(z)
        # Normalize to project onto the unit hypersphere
        w_norm = w_pre / w_pre.norm(p=2, dim=1, keepdim=True)
        # Return in the expected shape [batch, 1, w_dim]
        return w_norm.unsqueeze(1)

# ==============================================================================
#      2. NORMALIZING FLOW MODEL (MODIFIED FOR SPHERICAL SHELL DISTRIBUTION)
# ==============================================================================
# This new architecture separates the modeling of radius and direction,
# and models the conditional probability of radius given direction p(r|u).

class ConditionalRadialFlow(nn.Module):
    """
    A 1D Normalizing Flow to model the vector's radius, *conditioned on its direction*.
    """
    def __init__(self, condition_dim, hidden_dim=1024):
        super().__init__()
        # This network takes the direction vector `u` as a condition and predicts
        # the parameters for the radial transformation.
        self.net = nn.Sequential(
            nn.Linear(condition_dim, hidden_dim*2),
            nn.ReLU(),
            nn.Linear(hidden_dim*2, hidden_dim*2),
            nn.ReLU(),
            nn.Linear(hidden_dim*2, hidden_dim*2),
            nn.ReLU(),
            nn.Linear(hidden_dim*2, 2) # Outputs shift and log_scale
        )
        # Base distribution is a standard 1D Gaussian.
        self.base_distribution = torch.distributions.Normal(0.0, 1.0)

    def log_prob(self, r, u):
        """
        Calculates the log probability of a given radius `r`, conditioned on direction `u`.
        Args:
            r (Tensor): A tensor of radii of shape [batch_size, 1].
            u (Tensor): The conditioning direction vector of shape [batch_size, D].
        """
        # Predict shift and log_scale from the direction vector u
        shift, log_scale = self.net(u/u.norm(p=2, dim=1, keepdim=True)).chunk(2, dim=-1)

        # Apply the transformation: z = (r - shift) / scale
        # We need to unsqueeze shift and log_scale to match the shape of r
        z = (r - shift.unsqueeze(1)) * torch.exp(-log_scale.unsqueeze(1))
        # Log probability from the base Gaussian distribution
        log_prob_base = self.base_distribution.log_prob(z).squeeze(-1)
        
        # Log determinant of the Jacobian for this transformation is -log_scale
        log_det_j = -log_scale

        return log_prob_base + log_det_j

class DirectionalFlow(nn.Module):
    """
    A Normalizing Flow for data on the surface of a hypersphere.
    This models the marginal probability of the direction, p(u).
    """
    def __init__(self, data_dim, num_layers=8, hidden_dim=512):
        super().__init__()
        self.data_dim = data_dim
        self.layers = nn.ModuleList([self._create_coupling_layer(data_dim, hidden_dim) for _ in range(num_layers)])

        # The base distribution is uniform on the surface of a (D-1) sphere.
        # Its log probability is the negative log of the surface area.
        log_surface_area = math.log(2) + (data_dim / 2.0) * math.log(math.pi) - torch.lgamma(torch.tensor(data_dim / 2.0))
        self.register_buffer('log_prob_base', -log_surface_area)

    def _create_coupling_layer(self, data_dim, hidden_dim):
        # A simple affine coupling layer
        return nn.Sequential(
            nn.Linear(data_dim // 2, hidden_dim), 
            nn.ReLU(),
            nn.Linear(hidden_dim, data_dim) # Outputs scale and translate
        )

    def log_prob(self, u):
        """Calculates the log probability of a direction vector `u`."""
        log_det_j_total = torch.zeros(u.shape[0], device=u.device)
        y = u/u.norm(p=2, dim=1, keepdim=True)
        
        for i, layer_net in enumerate(self.layers):
            # Flip which half is the input to the conditioner
            if i % 2 == 1:
                y = torch.cat([y[:, self.data_dim//2:], y[:, :self.data_dim//2]], dim=1)
            
            y1, y2 = y.chunk(2, dim=1)
            s_t = layer_net(y1)
            scale, translate = s_t.chunk(2, dim=1)
            scale = torch.tanh(scale) # Stabilize
            
            # Affine transformation
            y2 = y2 * torch.exp(scale) + translate
            y = torch.cat([y1, y2], dim=1)

            if i % 2 == 1:
                y = torch.cat([y[:, self.data_dim//2:], y[:, :self.data_dim//2]], dim=1)

            log_det_j_total += scale.sum(dim=1)

        # The transformation to the uniform base sphere is y -> y / ||y||.
        # The log determinant of its Jacobian is -(D-1)log(||y||).
        r_y = y.norm(p=2, dim=1).clamp(min=1e-8)
        log_det_projection = -(self.data_dim - 1) * torch.log(r_y)
        
        total_log_det = log_det_j_total + log_det_projection
        
        return self.log_prob_base.expand(u.shape[0]) + total_log_det


class SphericalWLogProbFlow(nn.Module):
    """The complete model that combines conditional radial and marginal directional flows."""
    def __init__(self, data_dim, num_layers=8):
        super().__init__()
        self.data_dim = data_dim
        # The RadialFlow is now conditional on the direction
        self.radial_flow = ConditionalRadialFlow(condition_dim=data_dim)
        self.directional_flow = DirectionalFlow(data_dim=data_dim, num_layers=num_layers)
        self.param = nn.Parameter(torch.tensor(0.0, requires_grad=True))
        self.param2 = nn.Parameter(torch.tensor(0.0, requires_grad=True))

    def log_prob(self, w):
        # --- Decompose the vector w into radius and direction ---
        r = w.norm(p=2, dim=1, keepdim=True).clamp(min=1e-8)
        u = w / r

        # --- Calculate log probability from each component using the chain rule: p(r,u) = p(r|u)p(u) ---
        # 1. Log probability of the radius, conditioned on direction: log p(r|u)
        log_p_radial_conditional = self.radial_flow.log_prob(r, u)
        
        # 2. Log probability of the direction (marginal): log p(u)
        log_p_directional_marginal = self.directional_flow.log_prob(u)

        # 3. Log determinant from the change of coordinates (Cartesian to Hyperspherical)
        # For p(w) -> p(r, u), the term is (D-1)log(r).
        log_det_coord_change = (self.data_dim - 1) * torch.log(r.squeeze(-1)) *torch.exp(self.param)

        # The total log probability is the sum of these components.
        return log_p_radial_conditional + log_p_directional_marginal +log_det_coord_change

# ==============================================================================
#                           3. EXECUTION IN JUPYTER
# ==============================================================================
if __name__ == '__main__':
    # --- Configuration ---
    Z_DIM = 512
    W_DIM = 512 # W-space is typically the same dimension as Z-space
    BATCH_SIZE = 1024
    EPOCHS = 50
    LEARNING_RATE = 8e-4
    TRAIN_SAMPLES = 100_000

    # --- Setup Models & Device ---
    device = torch.device("mps" if torch.backends.mps.is_available() else "cuda" if torch.cuda.is_available() else "cpu")
    print(f"Using device: {device}")
    
    # Instantiate the mock generator
    generator = G
    generator.eval() # Set generator to evaluation mode

    # Instantiate the density estimation model and optimizer
    model = SphericalWLogProbFlow(data_dim=W_DIM, num_layers=8).to(device)
    optimizer = torch.optim.AdamW(model.parameters(), lr=LEARNING_RATE)
    scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=EPOCHS*TRAIN_SAMPLES//BATCH_SIZE)
    
    # --- Manual Training Loop ---
    print("Starting training...")
    for epoch in range(EPOCHS):
        model.train()
        
        train_z = torch.randn(TRAIN_SAMPLES, Z_DIM, device=device)
        
        with torch.no_grad():
            w = generator.mapping(train_z, None, truncation_psi=1.0)[:, 0]
            w = w-G.mapping.w_avg
        train_loader = DataLoader(TensorDataset(w), batch_size=BATCH_SIZE, shuffle=True)
        progress_bar = tqdm(train_loader, desc=f"Epoch {epoch+1}/{EPOCHS} lr {optimizer.param_groups[0]['lr']:.4f}")
        
        for batch in progress_bar:
            z, = batch
            z = z.to(device)


            log_prob_w = model.log_prob(w)
            loss = -log_prob_w.mean()
            
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            scheduler.step()
            progress_bar.set_postfix(loss=f"{loss.item():.4f}")

    print("Training finished.")

    # --- Example Usage After Training ---
    model.eval()
    print("\n--- Model Evaluation ---")
    
z_sample = torch.randn(1000, Z_DIM).to(device)
with torch.no_grad():

    w_in_dist = generator.mapping(z_sample, None, truncation_psi=1.0)[:,0]
    w_in_dist = w_in_dist-G.mapping.w_avg
    log_p_in_dist = model.log_prob(w_in_dist)
    print(f"Avg log-prob for in-distribution points (on sphere): {log_p_in_dist.mean().item():.4f}")


    # 2. Test with out-of-distribution data (points NOT on the unit sphere)
    w_off_dist_1 = w_in_dist+ (w_in_dist-G.mapping.w_avg) * .01  # Points with radius 2.0
    w_off_dist_2 = w_in_dist- (w_in_dist-G.mapping.w_avg) * .01  # Points with radius 0.5
    log_p_off_dist_1 = model.log_prob(w_off_dist_1)
    log_p_off_dist_2 = model.log_prob(w_off_dist_2)
    print(f"Avg log-prob for OOD points (radius 2.0):          {log_p_off_dist_1.mean().item()-log_p_in_dist.mean().item():.4f}")
    print(f"Avg log-prob for OOD points (radius 0.5):          {log_p_off_dist_2.mean().item()-log_p_in_dist.mean().item():.4f}")

In [ ]:

z_sample = torch.randn(1000, Z_DIM).to(device)
with torch.no_grad():
    w_in_dist = generator.mapping(z_sample, None, truncation_psi=1.0)[:,0]
    w_in_dist = w_in_dist-G.mapping.w_avg
    log_p_in_dist = model.log_prob(w_in_dist)
    print(f"Avg log-prob for in-distribution points (on sphere): {log_p_in_dist.mean().item():.4f}")


    # 2. Test with out-of-distribution data (points NOT on the unit sphere)
    w_off_dist_1 = w_in_dist+ (w_in_dist-G.mapping.w_avg) * .01  # Points with radius 2.0
    w_off_dist_2 = w_in_dist- (w_in_dist-G.mapping.w_avg) * .01  # Points with radius 0.5
    log_p_off_dist_1 = model.log_prob(w_off_dist_1)
    log_p_off_dist_2 = model.log_prob(w_off_dist_2)
    print(f"Avg log-prob for OOD points (radius 2.0):          {log_p_off_dist_1.mean().item()-log_p_in_dist.mean().item():.4f}")
    print(f"Avg log-prob for OOD points (radius 0.5):          {log_p_off_dist_2.mean().item()-log_p_in_dist.mean().item():.4f}")

In [ ]:

# 1. Test with in-distribution data (points on the unit sphere)
z_sample = torch.randn(1000, Z_DIM).to(device)
with torch.no_grad():
    w_in_dist = generator.mapping(z_sample, None, truncation_psi=1.0)[:,0]
    w_in_dist = w_in_dist-G.mapping.w_avg
    log_p_in_dist = model.log_prob(w_in_dist)
print(f"Avg log-prob for in-distribution points (on sphere): {log_p_in_dist.mean().item():.4f}")

with torch.no_grad():
    # 2. Test with out-of-distribution data (points NOT on the unit sphere)
    # w_off_dist_1 = w_in_dist+ (w_in_dist-G.mapping.w_avg) * .01  # Points with radius 2.0
    # w_off_dist_2 = w_in_dist- (w_in_dist-G.mapping.w_avg) * .01  # Points with radius 0.5
    w_off_dist_1 = w_in_dist+ torch.randn_like(w_in_dist) * .01  # Points with radius 2.0
    w_off_dist_2 = w_in_dist- torch.randn_like(w_in_dist) * .01  # Points with radius 0.5
    log_p_off_dist_1 = model.log_prob(w_off_dist_1)
    log_p_off_dist_2 = model.log_prob(w_off_dist_2)
print(f"Avg log-prob for OOD points (radius 2.0):          {log_p_off_dist_1.mean().item()-log_p_in_dist.mean().item():.4f}")
print(f"Avg log-prob for OOD points (radius 0.5):          {log_p_off_dist_2.mean().item()-log_p_in_dist.mean().item():.4f}")


In [ ]:

class IntervalSampler:
    """
    Samples two intervals of a given width within a normalized [0, 1] space,
    ensuring the difference between their start points is uniformly distributed.
    
    The final interval coordinates are scaled to a target range [min_f_value, max_f_value].
    """
    def __init__(self, subsample_width, min_f_value, max_f_value, min_gap=None):
        """
        Initializes the sampler.

        Args:
            subsample_width (float): The width of each interval in the normalized [0, 1] space.
            min_f_value (float): The minimum value of the final target range.
            max_f_value (float): The maximum value of the final target range.
            min_gap (float, optional): The minimum required gap between the two intervals.
                                       If None, defaults to `subsample_width`.
        """
        self.subsample_width = subsample_width
        self.min_f_value = min_f_value
        self.f_range = max_f_value - min_f_value
        
        # --- NEW: Set min_gap, defaulting to subsample_width ---
        if min_gap is None:
            self.min_gap = self.subsample_width
        else:
            self.min_gap = min_gap
            
        # --- NEW: Updated validity check for the parameters ---
        # The total space taken by two intervals and the gap between them must be less than 1.
        # The uniform range for delta_x is [d_min, 1-d_min], so 1-d_min > d_min => 1 > 2*d_min
        # d_min = width + gap => 1 > 2*(width + gap) => width + gap < 0.5
        if self.subsample_width + self.min_gap >= 0.5:
            raise ValueError(
                f"The sum of subsample_width ({self.subsample_width}) and "
                f"min_gap ({self.min_gap}) must be less than 0.5."
            )

    def sample_intervals(self):
        """
        Correctly samples two intervals to guarantee the distribution of the
        unscaled (x2 - x1) is uniform over the valid range.
        
        Returns:
            A tuple containing (subsample_min_1, subsample_max_1, subsample_min_2, subsample_max_2).
        """
        width = self.subsample_width
        gap = self.min_gap # Use the configured gap

        # Step 1: Sample `delta_x` from its new target uniform distribution.
        
        # --- NEW: The minimum possible difference is updated ---
        d_min = width + gap
        
        # The target range for delta_x is [d_min, 1 - d_min].
        # The size of this range is (1 - d_min) - d_min = 1 - 2*d_min.
        delta_x_range_size = 1 - 2 * d_min
        
        delta_x = d_min + np.random.random() * delta_x_range_size

        # Step 2: Given delta_x, sample x1 from its valid range [0, 1 - width - delta_x].
        # This logic remains the same.
        max_x1 = 1 - width - delta_x
        x1 = np.random.random() * max_x1

        # Step 3: Calculate x2. It is now deterministic.
        x2 = x1 + delta_x
        
        # --- Final Linear Transformation to Target Range ---
        # The distribution remains uniform after scaling and shifting.
        
        subsample_min_1 = self.min_f_value + x1 * self.f_range
        subsample_max_1 = self.min_f_value + (x1 + width) * self.f_range

        subsample_min_2 = self.min_f_value + x2 * self.f_range
        subsample_max_2 = self.min_f_value + (x2 + width) * self.f_range
        
        return subsample_min_1, subsample_max_1, subsample_min_2, subsample_max_2



# --- Main Visualization Script ---

# 1. Define parameters for the sampler
MIN_F_VALUE = -5.0
MAX_F_VALUE = 5.0
SUBSAMPLE_WIDTH = 0.1
MIN_GAP = 0.15
HISTORY_SIZE = 5 # Remember the last 5 intervals

# 2. Initialize the stateful sampler

# 3. Create the plot with 9 subplots
fig, axes = plt.subplots(3, 3, figsize=(15, 12), sharex=True)
fig.suptitle(f"Visualization of Stateful Interval Sampler (History Size={HISTORY_SIZE})", fontsize=16)
axes = axes.flatten()

# 4. In each subplot, plot the next 4 *sequential* intervals from the single sampler instance
for i, ax in enumerate(axes):
    # Call sample_intervals sequentially to demonstrate the stateful, non-overlapping behavior.
    intervals_to_plot = [sampler.sample_intervals() for _ in range(4)]
    
    start_call_num = i * 4 + 1
    ax.set_title(f"Sequential Calls: {start_call_num} - {start_call_num + 3}")
    ax.set_yticks([]) # The y-positions are arbitrary, so we hide the ticks
    ax.set_xlim(MIN_F_VALUE, MAX_F_VALUE)
    ax.grid(axis='x', linestyle='--', alpha=0.6)

    # Plot each of the 4 interval pairs at a different y-level
    for y_pos, interval_pair in enumerate(intervals_to_plot):
        min1, max1, min2, max2 = interval_pair
        
        # Draw the first interval of the pair
        ax.hlines(y=y_pos, xmin=min1, xmax=max1, color='dodgerblue', linewidth=10, label=f'Interval 1' if y_pos==0 and i==0 else "")
        # Draw the second interval of the pair
        ax.hlines(y=y_pos, xmin=min2, xmax=max2, color='orangered', linewidth=10, label=f'Interval 2' if y_pos==0 and i==0 else "")

# Add labels and legend to the last plot for clarity
axes[-1].set_xlabel("f(x) value")
handles, labels = axes[0].get_legend_handles_labels()
fig.legend(handles, labels, loc='lower center', ncol=2, bbox_to_anchor=(0.5, 0.01))

plt.tight_layout(rect=[0, 0.05, 1, 0.96]) # Adjust layout to make space for suptitle and legend
plt.show()



a = [m[0]-m[3] for m in scheduler.ordered_intervals]
plt.hist(a)

In [ ]:
import torch
import abc

# --- Manifold Helper Classes (for providing geometric constraints) ---

class Manifold(abc.ABC):
    """Abstract base class to define a geometric space."""
    @abc.abstractmethod
    def project_to_tangent_space(self, p, v_ambient):
        pass

class SphereManifold(Manifold):
    """Helper class providing projection logic for the unit sphere."""
    def __init__(self, eps=1e-8):
        self.eps = eps
    def _normalize(self, x):
        return x / (torch.linalg.norm(x, dim=-1, keepdim=True) + self.eps)
    def project_to_tangent_space(self, p, v_ambient):
        p_unit = self._normalize(p)
        dot_product = torch.sum(p_unit * v_ambient, dim=-1, keepdim=True)
        return v_ambient - dot_product * p_unit

class DynamicStatisticalManifold(Manifold):
    """Helper class to compute local statistical geometry."""
    def __init__(self, data_cloud: torch.Tensor, k: int, eps=1e-8):
        self.data_cloud = data_cloud
        self.k = k
        self.eps = eps

    def get_natural_gradient(self, p, q):
        """Computes the unnormalized natural gradient at p towards q."""
        vanilla_direction = q - p
        local_covariance = self._get_local_covariance(p)
        return torch.bmm(local_covariance, vanilla_direction.unsqueeze(-1)).squeeze(-1)

    def _get_local_covariance(self, p: torch.Tensor):
        B, D = p.shape
        local_covariances = torch.zeros(B, D, D, device=p.device, dtype=p.dtype)
        for i in range(B): # This loop is inefficient but fine for demo.
            distances = torch.linalg.norm(self.data_cloud - p[i], dim=-1)
            _, indices = torch.topk(distances, self.k, largest=False)
            neighbors = self.data_cloud[indices]
            mean = torch.mean(neighbors, dim=0)
            neighbors_centered = neighbors - mean
            covariance = torch.matmul(neighbors_centered.T, neighbors_centered) / (self.k - 1)
            local_covariances[i] = covariance
        return local_covariances
    def project_to_tangent_space(self, p, v_ambient): return v_ambient


# --- The Analytical Path/Flow Class ---

class ConstrainedSlerpFlow:
    """
    Computes a curved path between two points x0 and x1.
    The path is an analytical approximation of a geodesic on a statistical manifold,
    combining SLERP with varying radii and natural gradient constraints.
    
    This class is designed for efficient, batched computation of x(t) and u(t).
    """
    def __init__(self, x0: torch.Tensor, x1: torch.Tensor, stat_manifold: DynamicStatisticalManifold, eps=1e-8):
        self.x0, self.x1 = x0, x1
        self.stat_manifold = stat_manifold
        self.eps = eps
        self.B, self.D = x0.shape
        
        # Pre-compute all t-independent values for efficiency
        self._precompute_constants()

    def _precompute_constants(self):
        # 1. Decompose into radius and unit vectors
        self.r0 = torch.linalg.norm(self.x0, dim=-1, keepdim=True)
        self.r1 = torch.linalg.norm(self.x1, dim=-1, keepdim=True)
        self.u0 = self.x0 / (self.r0 + self.eps)
        self.u1 = self.x1 / (self.r1 + self.eps)

        # 2. Get tangent velocity constraints from the statistical manifold
        sphere_helper = SphereManifold(self.eps)
        v_nat_0_ambient = self.stat_manifold.get_natural_gradient(self.x0, self.x1)
        v_nat_1_ambient = self.stat_manifold.get_natural_gradient(self.x1, self.x0) * -1.0
        
        self.v0 = sphere_helper.project_to_tangent_space(self.u0, v_nat_0_ambient)
        self.v1 = sphere_helper.project_to_tangent_space(self.u1, v_nat_1_ambient)

        # 3. Pre-calculate constants for the time-to-distance mapping s(t)
        self.s0_prime = torch.linalg.norm(self.v0, dim=-1, keepdim=True) # Initial speed
        self.s1_prime = torch.linalg.norm(self.v1, dim=-1, keepdim=True) # Final speed
    
        dot_product = torch.sum(self.u0 * self.u1, dim=-1, keepdim=True)
        self.theta = torch.acos(torch.clamp(dot_product, -1.0 + self.eps, 1.0 + self.eps))
        self.sin_theta = torch.sin(self.theta)
        
    def _get_s_and_s_prime(self, t):
        """Computes the scalar distance s(t) and its derivative s'(t) using a Hermite spline."""
        t2, t3 = t*t, t*t*t
        
        # Hermite basis functions for s(t)
        h10 = t3 - 2*t2 + t
        h01 = -2*t3 + 3*t2
        h11 = t3 - t2
        s_t = h10*self.s0_prime + h01*self.theta + h11*self.s1_prime

        # Derivatives of Hermite basis functions for s'(t)
        h10_dot = 3*t2 - 4*t + 1
        h01_dot = -6*t2 + 6*t
        h11_dot = 3*t2 - 2*t
        s_prime_t = h10_dot*self.s0_prime + h01_dot*self.theta + h11_dot*self.s1_prime
        
        return s_t, s_prime_t

    def xt(self, t: torch.Tensor):
        """Computes the position x(t) for a batch of times t."""
        if t.dim() == 1:
            t = t.view(-1, *([1] * (self.x0.dim() - 1)))

        s_t, _ = self._get_s_and_s_prime(t)
        
        # SLERP with non-linear time s(t)
        sin_s_t = torch.sin(s_t)
        sin_theta_minus_s_t = torch.sin(self.theta - s_t)
        
        # Directional interpolation
        ut_dir = torch.where(
            self.sin_theta < self.eps,
            self.u0, # If parallel, no rotation
            (sin_theta_minus_s_t / self.sin_theta) * self.u0 + (sin_s_t / self.sin_theta) * self.u1
        )
        
        # Radial interpolation
        rt = (1 - t) * self.r0 + t * self.r1
        
        return rt * ut_dir
        
    def ut(self, t: torch.Tensor):
        """Computes the tangent vector u(t) = d(x(t))/dt for a batch of times t."""
        if t.dim() == 1:
            t = t.view(-1, *([1] * (self.x0.dim() - 1)))
            
        s_t, s_prime_t = self._get_s_and_s_prime(t)

        # Component 1: Radial velocity
        radial_velocity_component = (self.r1 - self.r0) * self.xt(t) / ((1 - t) * self.r0 + t * self.r1 + self.eps)
        
        # Component 2: Tangential (rotational) velocity
        cos_s_t = torch.cos(s_t)
        cos_theta_minus_s_t = torch.cos(self.theta - s_t)
        
        d_ut_dir_dt = torch.where(
            self.sin_theta < self.eps,
            torch.zeros_like(self.u0), # No rotation if parallel
            s_prime_t / self.sin_theta * (cos_s_t * self.u1 - cos_theta_minus_s_t * self.u0)
        )
        
        rt = (1 - t) * self.r0 + t * self.r1
        tangential_velocity_component = rt * d_ut_dir_dt
        
        return radial_velocity_component + tangential_velocity_component

# --- Example Usage ---
import matplotlib.pyplot as plt
import numpy as np
if __name__ == '__main__':
    B, D = 20, 50 # Larger batch size, high dimension
    N_CLOUD, K_NEIGHBORS = 50_000, 250

    print(f"Simulating a batch of {B} paths in {D}-dimensional space.")

    # 1. Setup the geometric environment
    data_cloud = torch.randn(N_CLOUD, D)
    data_cloud = data_cloud *((torch.arange(1,D+1).unsqueeze(0)/10)**2 / torch.linalg.norm(data_cloud, dim=-1, keepdim=True) )
    stat_manifold = DynamicStatisticalManifold(data_cloud=data_cloud, k=K_NEIGHBORS)

    # 2. Sample a batch of start and end points
    x0_batch = data_cloud[torch.randint(0, N_CLOUD, (B,))]
    x1_batch = data_cloud[torch.randint(0, N_CLOUD, (B,))]

    # 3. Instantiate the flow object for the batch
    flow = ConstrainedSlerpFlow(x0_batch, x1_batch, stat_manifold)
    
    # 4. Sample a random time `t` for EACH path in the batch
    t_batch = torch.rand(B, 1)

    # 5. Compute xt and ut for the batch efficiently
    xt_batch = flow.xt(t_batch)
    ut_batch = flow.ut(t_batch)

    print("\n--- Batch Computation Results ---")
    print(f"Shape of xt batch: {xt_batch.shape}")
    print(f"Shape of ut batch: {ut_batch.shape}")
    
    # 6. Verification: Check if ut is approximately the derivative of xt
    # We can do this by taking a small step from xt and comparing with ut.
    delta = 1e-2
    xt_plus_delta = flow.xt(t_batch + delta)
    ut_numerical = (xt_plus_delta - xt_batch) / delta
    
    # Compare the analytical ut with the numerical one
    error = torch.mean(torch.linalg.norm(ut_batch, dim=-1)/torch.linalg.norm(ut_numerical, dim=-1))
    # error = torch.mean(torch.cosine_similarity(ut_batch, ut_numerical, dim=-1))
    print(f"\nVerification: Mean error between analytical and numerical ut: {error:.6f}")
    print("A small error indicates the analytical tangent `ut` is correct.")

    # 7. Visualization: Flow from t=0 to t=1 on first two PCs
    print("\n--- Visualization ---")
    
    # Compute PCA on data_cloud
    from sklearn.decomposition import PCA
    pca = PCA(n_components=2)
    data_cloud_2d = pca.fit_transform(data_cloud.cpu().numpy())
    
    # Project start and end points to 2D
    x0_2d = pca.transform(x0_batch.cpu().numpy())
    x1_2d = pca.transform(x1_batch.cpu().numpy())
    
    # Sample time points for visualization
    t_vis = torch.linspace(0, .5, 500).unsqueeze(1).repeat(1, B)  # 50 time points
    # colors = plt.cm.viridis(torch.linspace(0, 1, n_vis_paths))
    # Create visualization
    import matplotlib.pyplot as plt
    
    plt.figure(figsize=(12, 8))
    flow_vis = ConstrainedSlerpFlow(x0_batch, x1_batch, stat_manifold)
    paths = []
    for i,t in enumerate(t_vis):
        # Compute flow paths for visualization (using first few paths for clarity)
        n_vis_paths = 10
        
        # Compute positions along the flow
        xt_vis = flow_vis.xt(t)  # Shape: (50, n_vis_paths, D)
        xt_vis_2d = pca.transform(xt_vis.cpu().numpy())
        # print(xt_vis_2d.shape)
        paths.append(xt_vis_2d)

    paths = np.stack(paths,axis=1)
    # print(paths.shape)
    for j,path in enumerate(paths):
        plt.plot(path[:, 0], path[:, 1], 
                alpha=(1-j/len(paths))**2*0.5+0.5, linewidth=2, linestyle='--')#, color='black')
        # print(path.shape)
    plt.legend()
            
        
    # Plot data cloud (subsampled for clarity)
    # cloud_sample = data_cloud_2d[::100]  # Every 100th point
    # plt.scatter(cloud_sample[:, 0], cloud_sample[:, 1], c='lightgray', alpha=0.3, s=1, label='Data Cloud')
    
    # Plot flow paths
    
    # Plot start and end points
    plt.scatter(x0_2d[:, 0], x0_2d[:, 1], 
               c='red', s=100, marker='<', alpha=0.3, zorder=5)
    plt.scatter(x1_2d[:, 0], x1_2d[:, 1], 
               c='blue', s=100, marker='>', alpha=0.3, zorder=5)
    
    plt.xlabel('First Principal Component')
    plt.ylabel('Second Principal Component')
    plt.title('Constrained SLERP Flow Visualization (First 2 PCs)')
    plt.legend()
    plt.grid(True, alpha=0.3)
    plt.tight_layout()
    plt.show()
    
    print(f"Visualized {n_vis_paths} flow paths from t=0 to t=1")
    print("Red circles: Start points, Blue squares: End points")
    print("Colored lines: Flow trajectories")

In [ ]:
np.save("deixis_plot_paths4.npy", paths)

In [ ]:
import torch

class SimpleSlerpFlow:
    """
    Computes a simple spherical linear interpolation (SLERP) path between
    two points, x0 and x1, around a specified center.

    The path includes linear interpolation of the radius (distance from the center).
    This class is designed for efficient, batched computation of the path x(t).
    """
    def __init__(self, x0: torch.Tensor, x1: torch.Tensor, center: torch.Tensor = None, eps=1e-8):
        """
        Initializes the flow.

        Args:
            x0 (torch.Tensor): The starting points of shape (Batch, Dim).
            x1 (torch.Tensor): The ending points of shape (Batch, Dim).
            center (torch.Tensor, optional): The center of rotation. If None,
                the origin (0,0,...) is used. Must be broadcastable to x0/x1.
            eps (float): A small value for numerical stability.
        """
        self.x0 = x0
        self.x1 = x1
        self.eps = eps

        # If no center is provided, create a zero tensor with the correct batch and device.
        if center is None:
            self.center = torch.zeros_like(self.x0)
        else:
            self.center = center

        # Pre-compute all t-independent values for efficiency.
        self._precompute_constants()

    @torch.no_grad()
    def _precompute_constants(self):
        """Pre-computes vectors relative to the center, radii, and the angle between them."""
        # 1. Define vectors relative to the specified center
        self.vec0 = self.x0 - self.center
        self.vec1 = self.x1 - self.center

        # 2. Decompose into radius (distance from center) and unit vectors
        self.r0 = torch.linalg.norm(self.vec0, dim=-1, keepdim=True)
        self.r1 = torch.linalg.norm(self.vec1, dim=-1, keepdim=True)
        self.u0 = self.vec0 / (self.r0 + self.eps)
        self.u1 = self.vec1 / (self.r1 + self.eps)

        # 3. Calculate the angle between the unit vectors
        dot_product = torch.sum(self.u0 * self.u1, dim=-1, keepdim=True)
        self.theta = torch.acos(torch.clamp(dot_product, -1.0 + self.eps, 1.0 - self.eps))
        self.sin_theta = torch.sin(self.theta)

    @torch.no_grad()
    def xt(self, t: torch.Tensor):
        """
        Computes the interpolated position x(t) for a batch of times t.

        Args:
            t (torch.Tensor): A tensor of time values, typically between 0 and 1.
                               Can be a scalar or a tensor that can be broadcast.

        Returns:
            torch.Tensor: The interpolated points. Shape matches broadcast of t and x0.
        """
        # Ensure t is broadcastable for batched operations.
        # This adds trailing dimensions to t to match the dimensions of x0.
        while t.dim() < self.x0.dim():
            t = t.unsqueeze(-1)

        # --- Handle the edge case where vectors are nearly collinear ---
        # If the angle is very small, SLERP is unstable. A simple linear
        # interpolation of the vectors is more robust and equivalent in this limit.
        is_collinear = self.sin_theta.abs() < self.eps
        
        # Path for the collinear case (straight line from x0 to x1)
        vec_t_linear = (1 - t) * self.vec0 + t * self.vec1

        # --- Standard SLERP Path ---
        # The angle for interpolation at time t
        omega = t * self.theta
        
        # SLERP formula for the direction vector
        # This calculates the interpolated unit vector by rotating u0 towards u1.
        ut_dir = (
            (torch.sin(self.theta - omega) / (self.sin_theta + self.eps)) * self.u0 +
            (torch.sin(omega) / (self.sin_theta + self.eps)) * self.u1
        )
        
        # --- Radial Interpolation ---
        # Linearly interpolate the radius (distance from the center)
        rt = (1 - t) * self.r0 + t * self.r1

        # Combine interpolated direction and radius for the SLERP path
        vec_t_slerp = rt * ut_dir
        
        # Choose between SLERP and linear interpolation based on the angle
        vec_t = torch.where(is_collinear, vec_t_linear, vec_t_slerp)
        
        # Add the center back to get the final position in the original coordinate system
        return self.center + vec_t




t_vis = torch.linspace(0, 1, 500).unsqueeze(1).repeat(1, B)  # 50 time points
plt.figure(figsize=(12, 8))
flow_vis = SimpleSlerpFlow(x0_batch, x1_batch)
paths = []
for i,t in enumerate(t_vis):
    # Compute flow paths for visualization (using first few paths for clarity)
    n_vis_paths = 10
    
    # Compute positions along the flow
    xt_vis = flow_vis.xt(t)  # Shape: (50, n_vis_paths, D)
    xt_vis_2d = pca.transform(xt_vis.cpu().numpy())
    # print(xt_vis_2d.shape)
    paths.append(xt_vis_2d)

paths = np.stack(paths,axis=1)
# print(paths.shape)
for j,path in enumerate(paths):
    plt.plot(path[:, 0], path[:, 1], 
            alpha=(1-j/len(paths))**2*0.5+0.5, linewidth=2, linestyle='--')#, color='black')
    # print(path.shape)
plt.legend()
        
    
# Plot data cloud (subsampled for clarity)
# cloud_sample = data_cloud_2d[::100]  # Every 100th point
# plt.scatter(cloud_sample[:, 0], cloud_sample[:, 1], c='lightgray', alpha=0.3, s=1, label='Data Cloud')

# Plot flow paths

# Plot start and end points
plt.scatter(x0_2d[:, 0], x0_2d[:, 1], 
            c='red', s=100, marker='<', alpha=0.3, zorder=5)
plt.scatter(x1_2d[:, 0], x1_2d[:, 1], 
            c='blue', s=100, marker='>', alpha=0.3, zorder=5)

plt.xlabel('First Principal Component')
plt.ylabel('Second Principal Component')
plt.title('Constrained SLERP Flow Visualization (First 2 PCs)')
plt.legend()
plt.grid(True, alpha=0.3)
plt.tight_layout()
plt.show()

print(f"Visualized {n_vis_paths} flow paths from t=0 to t=1")
print("Red circles: Start points, Blue squares: End points")
print("Colored lines: Flow trajectories")

In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from scipy.stats import beta
from scipy.integrate import trapezoid
import ipywidgets as widgets
from IPython.display import display

# --- 1. Create the main figure widget ---
# Changed to 3 rows to accommodate the new bar plot
fig = go.FigureWidget(
    make_subplots(
        rows=3,
        cols=1,
        subplot_titles=(
            "<b>Probability Density Functions (PDF)</b>",
            "<b>Cumulative Distribution Functions (CDF)</b>",
            "<b>Metric Comparison</b>"
        ),
        vertical_spacing=0.1
    )
)

# --- 2. Add initial empty traces to the figure ---
# PDF traces
fig.add_trace(go.Scatter(name='Beta 1 PDF', line=dict(color='royalblue', width=3)), row=1, col=1)
fig.add_trace(go.Scatter(name='Beta 2 PDF', line=dict(color='firebrick', width=3)), row=1, col=1)

# CDF traces
fig.add_trace(go.Scatter(name='Beta 1 CDF', line=dict(color='royalblue', width=3)), row=2, col=1)
fig.add_trace(go.Scatter(name='Beta 2 CDF', line=dict(color='firebrick', width=3)), row=2, col=1)

# NEW: Bar plot trace for metrics
fig.add_trace(go.Bar(name='Metrics', orientation='h', marker_color='teal'), row=3, col=1)


# --- 3. Configure the layout of the plot ---
# Increased height for the new plot
fig.update_layout(
    height=900,
    title_text="Beta Distribution Analysis & Distances",
    title_x=0.5,
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
    margin=dict(l=50, r=50, t=100, b=50),
    showlegend=False # Hide legend for the bar plot for a cleaner look
)
fig.update_xaxes(title_text="x", range=[-0.01, 1.01], row=1, col=1)
fig.update_xaxes(title_text="x", range=[-0.01, 1.01], row=2, col=1)
fig.update_xaxes(title_text="Value", row=3, col=1) # New x-axis for bar plot

fig.update_yaxes(title_text="Density", row=1, col=1)
fig.update_yaxes(title_text="Probability", range=[-0.05, 1.05], row=2, col=1)
fig.update_yaxes(title_text="Metric", row=3, col=1) # New y-axis for bar plot


# --- 4. Create interactive slider widgets ---
slider_style = {'description_width': 'initial'}
alpha1_slider = widgets.FloatSlider(value=1.0, min=0.1, max=10.0, step=0.1, description='Alpha 1 (α₁):', style=slider_style)
beta1_slider = widgets.FloatSlider(value=3.0, min=0.1, max=10.0, step=0.1, description='Beta 1 (β₁):', style=slider_style)
alpha2_slider = widgets.FloatSlider(value=3.0, min=0.1, max=10.0, step=0.1, description='Alpha 2 (α₂):', style=slider_style)
beta2_slider = widgets.FloatSlider(value=1.0, min=0.1, max=10.0, step=0.1, description='Beta 2 (β₂):', style=slider_style)

# Create an HTML widget to display the calculated distances
output_text = widgets.HTML(value="", layout=widgets.Layout(padding='10px'))

# --- 5. Define the function that updates the plot and text ---
def update_plot(alpha1, beta1, alpha2, beta2):
    """
    Recalculates all values and updates the plot and text display
    based on new slider values.
    """
    x = np.linspace(0.001, 0.999, 500)
    u_space = np.linspace(0.001, 0.999, 1000)

    dist1 = beta(alpha1, beta1)
    pdf1, cdf1, mean1, var1, q1 = dist1.pdf(x), dist1.cdf(x), dist1.mean(), dist1.var(), dist1.ppf(u_space)

    dist2 = beta(alpha2, beta2)
    pdf2, cdf2, mean2, var2, q2 = dist2.pdf(x), dist2.cdf(x), dist2.mean(), dist2.var(), dist2.ppf(u_space)

    # --- Calculate Metrics ---
    mean_diff = (mean1 - mean2)
    w1_dist = (mean1**2 + var1)**0.5 - (mean2**2 + var2)**0.5
    rho = np.corrcoef(q1, q2)[0, 1] if len(q1) > 1 and len(q2) > 1 else 1.0
    w2_dist_sq_decomp = (mean1 - mean2)**2 + (np.sqrt(var1) - np.sqrt(var2))**2 + 2 * np.sqrt(var1 * var2) * (1 - rho)
    w2_dist = np.sqrt(max(0, w2_dist_sq_decomp))
    quantile_diff = (trapezoid((q1 - q2)/np.abs(q1 - q2), u_space))
    quantile_diff = quantile_diff**2*np.sign(quantile_diff)
    sq_quantile_diff = float(trapezoid(np.sign(q1 - q2)*(q1 - q2)**2, u_space))
    sq_quantile_diff = (sq_quantile_diff/np.sign(sq_quantile_diff))**0.5*np.sign(sq_quantile_diff)


    # --- Data for the bar plot ---
    metric_labels = [
        'Difference in Means', 'Your W₁ Formula', 'Wasserstein-2 (W₂)',
        'Quantile Difference', 'Squared Quantile Diff.'
    ]
    metric_values = [mean_diff, w1_dist, w2_dist, quantile_diff, sq_quantile_diff]

    # --- Update the plot using batch_update for efficiency ---

    with fig.batch_update():
        try:
            # Update PDF and CDF data
            fig.data[0].x, fig.data[0].y = x, pdf1
            fig.data[1].x, fig.data[1].y = x, pdf2
            fig.data[2].x, fig.data[2].y = x, cdf1
            fig.data[3].x, fig.data[3].y = x, cdf2

            # Update bar plot data
            fig.data[4].x = metric_values
            fig.data[4].y = metric_labels

            # Dynamically adjust axes
            max_pdf = max(np.nan_to_num(pdf1, nan=0, posinf=100).max(),
                        np.nan_to_num(pdf2, nan=0, posinf=100).max())
            fig.update_yaxes(range=[0, min(max_pdf * 1.1, 20)], row=1, col=1)
            
            # Make bar chart x-axis symmetrical
            max_bar_val = max(abs(v) for v in metric_values) * 1.1
            fig.update_xaxes(range=[-1, 1], row=3, col=1)
        except Exception as e:
            print(e)


    # --- Update the HTML text widget ---
    output_text.value = f"""
    <div style="font-family: sans-serif; line-height: 1.8; font-size: 14px;
                border: 1px solid #ccc; padding: 15px; border-radius: 8px; background-color: #f9f9f9;">
        <h4 style="margin-top:0;">Distance Metrics</h4>
        <table style="width:100%;">
            <tr>
                <td style="padding: 4px;">Difference in Means (μ₁ - μ₂)</td>
                <td style="padding: 4px; text-align:right;"><b>{mean_diff:.4f}</b></td>
            </tr>
            <tr>
                <td style="padding: 4px;">Your W₁ Formula</td>
                <td style="padding: 4px; text-align:right;"><b>{w1_dist:.4f}</b></td>
            </tr>
            <tr>
                <td style="padding: 4px;">Wasserstein-2 Distance (W₂)</td>
                <td style="padding: 4px; text-align:right;"><b>{w2_dist:.4f}</b></td>
            </tr>
            <tr><td colspan="2"><hr style="border-top: 1px dashed #ccc;"></td></tr>
            <tr>
                <td style="padding: 4px;">Quantile Difference ∫(q₁-q₂)du</td>
                <td style="padding: 4px; text-align:right;"><b>{quantile_diff:.4f}</b></td>
            </tr>
            <tr>
                <td style="padding: 4px;">Squared Quantile Diff. ∫(q₁-q₂)²du</td>
                <td style="padding: 4px; text-align:right;"><b>{sq_quantile_diff:.4f}</b></td>
            </tr>
        </table>
    </div>
    """

# --- 6. Link the sliders to the update function ---
interactive_output = widgets.interactive_output(
    update_plot,
    {'alpha1': alpha1_slider, 'beta1': beta1_slider, 'alpha2': alpha2_slider, 'beta2': beta2_slider}
)

# --- 7. Arrange the UI elements and display them ---
controls = widgets.VBox([
    widgets.HTML("<b><font color='royalblue'>Distribution 1 Parameters</font></b>"),
    alpha1_slider,
    beta1_slider,
    widgets.HTML("<hr><b><font color='firebrick'>Distribution 2 Parameters</font></b>"),
    alpha2_slider,
    beta2_slider
], layout=widgets.Layout(padding='10px'))

ui_panel = widgets.VBox([controls, output_text])
app_layout = widgets.HBox([fig, ui_panel])
display(app_layout)


In [ ]:
X,y,weights